In [1]:
import numpy as np
import os
import pandas as pd
from arcpy import env
from arcpy import TableToTable_conversion
import matplotlib.ticker as mtick

In [2]:
dirWork = os.getcwd()
dirData = os.path.join(dirWork, r'data')
dirTDM  = os.path.join(dirData, r'tdm\1_WF')
dirFactors   = os.path.join(dirWork, r'data-processed\factors')
dirResults   = os.path.join(dirWork, r'results')

# Run Settings

In [3]:
#set to true for first time to create CSVs, false to speed up for subsequent times
process_TDMdbftocsv = False

#export results
export_results = True

# Define Scenarios

In [4]:
df_Scenarios = pd.DataFrame()


#define AdjCode for pivot when model is not related to forecast
#AADT will be adjusted based on difference between scenario and forecast scenario TDMs
#if ForecastScenarioID is note defined, then the associated forecast volume will be used for that year
#DBF don't include filename extension

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'Base19',
                                    'ScenarioName'   : '2019 Base',
                                    'ScenarioYear'   :  2019,
                                    'ScenarioGroup'  : 'Base',
                                    'SegSummaryCSV'  : 'v831_SE19_Net19_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'TIP24',
                                    'ScenarioName'   : '2024 TIP',
                                    'ScenarioYear'   :  2024,
                                    'ScenarioGroup'  : 'TIP',
                                    'SegSummaryCSV'  : 'v831_SE24_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'Base19'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'RTP30',
                                    'ScenarioName'   : '2030 RTP',
                                    'ScenarioYear'   :  2030,
                                    'ScenarioGroup'  : 'RTP',
                                    'SegSummaryCSV'  : 'v831_SE30_Net30_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'TIP24'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'RTP40',
                                    'ScenarioName'   : '2040 RTP',
                                    'ScenarioYear'   :  2040,
                                    'ScenarioGroup'  : 'RTP',
                                    'SegSummaryCSV'  : 'v831_SE40_Net40_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'RTP30'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode' : 'RTP50',
                                    'ScenarioName' : '2050 RTP',
                                    'ScenarioYear' :  2050,
                                    'ScenarioGroup': 'RTP',
                                    'SegSummaryCSV': 'v831_SE50_Net50_Summary_SEGID_Detailed.csv',
                                    'Process'      : 'Yes',
                                    'PrvScenarioCode': 'RTP40'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'NB30',
                                    'ScenarioName'   : '2030 No Build',
                                    'ScenarioYear'   :  2030,
                                    'ScenarioGroup'  : 'No Build',
                                    'AdjScenarioCode': 'RTP30',
                                    'SegSummaryCSV'  : 'v831_SE30_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'TIP24'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'NB40',
                                    'ScenarioName'   : '2040 No Build',
                                    'ScenarioYear'   :  2040,
                                    'ScenarioGroup'  : 'No Build',
                                    'AdjScenarioCode': 'RTP40',
                                    'SegSummaryCSV'  : 'v831_SE40_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'NB30'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'NB50',
                                    'ScenarioName'   : '2050 No Build',
                                    'ScenarioYear'   :  2050,
                                    'ScenarioGroup'  : 'No Build',
                                    'AdjScenarioCode': 'RTP50',
                                    'SegSummaryCSV'  : 'v831_SE50_Net24_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'NB40'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'UF30',
                                    'ScenarioName'   : '2030 Needs',
                                    'ScenarioYear'   :  2030,
                                    'ScenarioGroup'  : 'Needs',
                                    'AdjScenarioCode': 'RTP30',
                                    'SegSummaryCSV'  : 'v831_SE30_Net30UF_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'TIP24'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'UF40',
                                    'ScenarioName'   : '2040 Needs',
                                    'ScenarioYear'   :  2040,
                                    'ScenarioGroup'  : 'Needs',
                                    'AdjScenarioCode': 'RTP40',
                                    'SegSummaryCSV'  : 'v831_SE40_Net40UF_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'UF30'
                                   },ignore_index=True)

df_Scenarios = df_Scenarios.append({'ScenarioCode'   : 'UF50',
                                    'ScenarioName'   : '2050 Needs',
                                    'ScenarioYear'   :  2050,
                                    'ScenarioGroup'  : 'Needs',
                                    'AdjScenarioCode': 'RTP50',
                                    'SegSummaryCSV'  : 'v831_SE50_Net50UF_Summary_SEGID_Detailed.csv',
                                    'Process'        : 'Yes',
                                    'PrvScenarioCode': 'UF40'
                                   },ignore_index=True)

#all scenarios will be read in to allow for pivoting if needed
df_Scenarios.index.name = 'ScenarioID'
df_Scenarios['ScenarioYear'] = pd.to_numeric(df_Scenarios['ScenarioYear'], downcast='integer')
df_Scenarios

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [5]:
df_Scenarios_toProcess = df_Scenarios[df_Scenarios['Process']=='Yes']
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [6]:
df_Scenarios_toAdjust = df_Scenarios_toProcess[df_Scenarios_toProcess['AdjScenarioCode'].notnull()]
df_Scenarios_toAdjust

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [7]:
#define functions to get scenario data
def idFromCode (sCode):
    return df_Scenarios.index[df_Scenarios['ScenarioCode'] == sCode].tolist()[0]
def yrFromCode (sCode):
    return df_Scenarios[df_Scenarios['ScenarioCode'] == sCode].iloc[0]['ScenarioYear']
def codeFromID (sID):
    return df_Scenarios.loc[sID]['ScenarioCode']
def yearFromID (sID):
    return df_Scenarios.loc[sID]['ScenarioYear']

#quick tests of functions
#display(idFromCode('50RTP'))
#display(yrFromCode('50RTP'))
#display(codeFromID(4))
#display(yearFromID(4))
#display(df_Scenarios.loc[7]['ScenarioCode'])

# Define Desired V/C Groupings

In [8]:
#season groups

df_VCGroup_Seasons = pd.DataFrame()

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Ann',
                                                'SeasonName'    : 'Annual',
                                                'SeasonGroup'   : 'S00-Ann',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Win',
                                                'SeasonName'    : 'Winter',
                                                'SeasonGroup'   : 'S01-Win',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Spr',
                                                'SeasonName'    : 'Spring',
                                                'SeasonGroup'   : 'S02-Spr',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Sum',
                                                'SeasonName'    : 'Summer',
                                                'SeasonGroup'   : 'S03-Sum',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Fal',
                                                'SeasonName'    : 'Fall',
                                                'SeasonGroup'   : 'S04-Fal',
                                                'SeasonType'    : 'Season'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Jan',
                                                'SeasonName'    : 'January',
                                                'SeasonGroup'   : 'M01-Jan',
                                                'SeasonType'    : 'Month',
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Feb',
                                                'SeasonName'    : 'February',
                                                'SeasonGroup'   : 'M02-Feb',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Mar',
                                                'SeasonName'    : 'March',
                                                'SeasonGroup'   : 'M03-Mar',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Apr',
                                                'SeasonName'    : 'April',
                                                'SeasonGroup'   : 'M04-Apr',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'May',
                                                'SeasonName'    : 'May',
                                                'SeasonGroup'   : 'M05-May',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Jun',
                                                'SeasonName'    : 'June',
                                                'SeasonGroup'   : 'M06-Jun',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Jul',
                                                'SeasonName'    : 'July',
                                                'SeasonGroup'   : 'M07-Jul',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Aug',
                                                'SeasonName'    : 'August',
                                                'SeasonGroup'   : 'M08-Aug',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Sep',
                                                'SeasonName'    : 'September',
                                                'SeasonGroup'   : 'M09-Sep',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Oct',
                                                'SeasonName'    : 'October',
                                                'SeasonGroup'   : 'M10-Oct',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Nov',
                                                'SeasonName'    : 'November',
                                                'SeasonGroup'   : 'M11-Nov',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

df_VCGroup_Seasons = df_VCGroup_Seasons.append({'SeasonCode'    : 'Dec',
                                                'SeasonName'    : 'December',
                                                'SeasonGroup'   : 'M12-Dec',
                                                'SeasonType'    : 'Month'
                                               },ignore_index=True)

display(df_VCGroup_Seasons)

#day-of-week groups

df_VCGroup_DOWPkHr = pd.DataFrame()

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'WkAM',
                                                'DOWPkName' : 'AM - Weekday',
                                                'DOWGroup'  : 'W1-Weekday',
                                                'Prd'       : 'AM',
                                                'HrPctOf'   : 'Prd' #calculate peak Hr using Prd volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'WkMD',
                                                'DOWPkName' : 'Midday - Weekday',
                                                'DOWGroup'  : 'W1-Weekday',
                                                'Prd'       : 'MD',
                                                'HrPctOf'   : 'Prd' #calculate peak Hr using Prd volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'WkPM',
                                                'DOWPkName' : 'PM - Weekday',
                                                'DOWGroup'  : 'W1-Weekday',
                                                'Prd'       : 'PM',
                                                'HrPctOf'   : 'Prd' #calculate peak Hr using Prd volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'FrPM',
                                                'DOWPkName' : 'PM - Friday',
                                                'DOWGroup'  : '5-Friday',
                                                'Prd'       : 'PM',
                                                'HrPctOf'   : 'DY' #calculate peak Hr using DY volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'SaDY',
                                                'DOWPkName' : 'Saturday',
                                                'DOWGroup'  : '6-Saturday',
                                                'Prd'       : 'DY',
                                                'HrPctOf'   : 'DY' #calculate peak Hr using DY volume
                                               },ignore_index=True)

df_VCGroup_DOWPkHr = df_VCGroup_DOWPkHr.append({'DOWPkCode' : 'SuDY',
                                                'DOWPkName' : 'Sunday',
                                                'DOWGroup'  : '7-Sunday',
                                                'Prd'       : 'DY',
                                                'HrPctOf'   : 'DY' #calculate peak Hr using DY volume
                                               },ignore_index=True)

display(df_VCGroup_DOWPkHr)

#directional factor when using DY volumes for peak Hr calcs
#taken from HCM 2000 Exhibit 9-2
dDYDirectionalFactor = 0.6

#directional factor not used in Prd volume calcs, since those include directionality

SeasonCode SeasonGroup SeasonName SeasonType
0         Ann     S00-Ann     Annual     Season
1         Win     S01-Win     Winter     Season
2         Spr     S02-Spr     Spring     Season
3         Sum     S03-Sum     Summer     Season
4         Fal     S04-Fal       Fall     Season
5         Jan     M01-Jan    January      Month
6         Feb     M02-Feb   February      Month
7         Mar     M03-Mar      March      Month
8         Apr     M04-Apr      April      Month
9         May     M05-May        May      Month
10        Jun     M06-Jun       June      Month
11        Jul     M07-Jul       July      Month
12        Aug     M08-Aug     August      Month
13        Sep     M09-Sep  September      Month
14        Oct     M10-Oct    October      Month
15        Nov     M11-Nov   November      Month
16        Dec     M12-Dec   December      Month

DOWGroup DOWPkCode         DOWPkName HrPctOf Prd
0  W1-Weekday      WkAM      AM - Weekday     Prd  AM
1  W1-Weekday      WkMD  Midday - Weekday     Prd  MD
2  W1-Weekday      WkPM      PM - Weekday     Prd  PM
3    5-Friday      FrPM       PM - Friday      DY  PM
4  6-Saturday      SaDY          Saturday      DY  DY
5    7-Sunday      SuDY            Sunday      DY  DY

In [9]:
import itertools

#create df with all possible season and day-of-weak/peak groups
df_VCGroups = pd.DataFrame(list(itertools.product(df_VCGroup_Seasons['SeasonCode'],df_VCGroup_DOWPkHr['DOWPkCode'])),columns=['SeasonCode','DOWPkCode'])

df_VCGroups = pd.DataFrame(df_VCGroups)
pd.set_option('display.max_rows', df_VCGroups.shape[0]+1)

#display(df_VCGroups)

#add season data
df_VCGroups = pd.DataFrame.merge(df_VCGroups, df_VCGroup_Seasons, on='SeasonCode')

#add dow-peak data
df_VCGroups = pd.DataFrame.merge(df_VCGroups, df_VCGroup_DOWPkHr, on='DOWPkCode')

#set id name
df_VCGroups.index.name = 'VCGroupID'

df_VCGroups['VCGroupCode'] = df_VCGroups['SeasonCode'] + df_VCGroups['DOWPkCode']

df_VCGroups = df_VCGroups.drop(columns=['SeasonCode','DOWPkCode','SeasonName','DOWPkName'])

display(df_VCGroups)

SeasonGroup SeasonType    DOWGroup HrPctOf Prd VCGroupCode
VCGroupID                                                           
0             S00-Ann     Season  W1-Weekday     Prd  AM     AnnWkAM
1             S01-Win     Season  W1-Weekday     Prd  AM     WinWkAM
2             S02-Spr     Season  W1-Weekday     Prd  AM     SprWkAM
3             S03-Sum     Season  W1-Weekday     Prd  AM     SumWkAM
4             S04-Fal     Season  W1-Weekday     Prd  AM     FalWkAM
5             M01-Jan      Month  W1-Weekday     Prd  AM     JanWkAM
6             M02-Feb      Month  W1-Weekday     Prd  AM     FebWkAM
7             M03-Mar      Month  W1-Weekday     Prd  AM     MarWkAM
8             M04-Apr      Month  W1-Weekday     Prd  AM     AprWkAM
9             M05-May      Month  W1-Weekday     Prd  AM     MayWkAM
10            M06-Jun      Month  W1-Weekday     Prd  AM     JunWkAM
11            M07-Jul      Month  W1-Weekday     Prd  AM     JulWkAM
12            M08-Aug      Month  W1-Weekday     Prd  AM     AugWkAM
13            M09-Sep      Month  W1-Weekday     Prd  AM     SepWkAM
14            M10-Oct      Month  W1-Weekday     Prd  AM     OctWkAM
15            M11-Nov      Month  W1-Weekday     Prd  AM     NovWkAM
16            M12-Dec      Month  W1-Weekday     Prd  AM     DecWkAM
17            S00-Ann     Season  W1-Weekday     Prd  MD     AnnWkMD
18            S01-Win     Season  W1-Weekday     Prd  MD     WinWkMD
19            S02-Spr     Season  W1-Weekday     Prd  MD     SprWkMD
20            S03-Sum     Season  W1-Weekday     Prd  MD     SumWkMD
21            S04-Fal     Season  W1-Weekday     Prd  MD     FalWkMD
22            M01-Jan      Month  W1-Weekday     Prd  MD     JanWkMD
23            M02-Feb      Month  W1-Weekday     Prd  MD     FebWkMD
24            M03-Mar      Month  W1-Weekday     Prd  MD     MarWkMD
25            M04-Apr      Month  W1-Weekday     Prd  MD     AprWkMD
26            M05-May      Month  W1-Weekday     Prd  MD     MayWkMD
27            M06-Jun      Month  W1-Weekday     Prd  MD     JunWkMD
28            M07-Jul      Month  W1-Weekday     Prd  MD     JulWkMD
29            M08-Aug      Month  W1-Weekday     Prd  MD     AugWkMD
30            M09-Sep      Month  W1-Weekday     Prd  MD     SepWkMD
31            M10-Oct      Month  W1-Weekday     Prd  MD     OctWkMD
32            M11-Nov      Month  W1-Weekday     Prd  MD     NovWkMD
33            M12-Dec      Month  W1-Weekday     Prd  MD     DecWkMD
34            S00-Ann     Season  W1-Weekday     Prd  PM     AnnWkPM
35            S01-Win     Season  W1-Weekday     Prd  PM     WinWkPM
36            S02-Spr     Season  W1-Weekday     Prd  PM     SprWkPM
37            S03-Sum     Season  W1-Weekday     Prd  PM     SumWkPM
38            S04-Fal     Season  W1-Weekday     Prd  PM     FalWkPM
39            M01-Jan      Month  W1-Weekday     Prd  PM     JanWkPM
40            M02-Feb      Month  W1-Weekday     Prd  PM     FebWkPM
41            M03-Mar      Month  W1-Weekday     Prd  PM     MarWkPM
42            M04-Apr      Month  W1-Weekday     Prd  PM     AprWkPM
43            M05-May      Month  W1-Weekday     Prd  PM     MayWkPM
44            M06-Jun      Month  W1-Weekday     Prd  PM     JunWkPM
45            M07-Jul      Month  W1-Weekday     Prd  PM     JulWkPM
46            M08-Aug      Month  W1-Weekday     Prd  PM     AugWkPM
47            M09-Sep      Month  W1-Weekday     Prd  PM     SepWkPM
48            M10-Oct      Month  W1-Weekday     Prd  PM     OctWkPM
49            M11-Nov      Month  W1-Weekday     Prd  PM     NovWkPM
50            M12-Dec      Month  W1-Weekday     Prd  PM     DecWkPM
51            S00-Ann     Season    5-Friday      DY  PM     AnnFrPM
52            S01-Win     Season    5-Friday      DY  PM     WinFrPM
53            S02-Spr     Season    5-Friday      DY  PM     SprFrPM
54            S03-Sum     Season    5-Friday      DY  PM     SumFrPM
55            S04-Fal     Season    5-Friday      DY  PM     FalFrPM
56      

# TDM SEGID Detail

In [10]:
#column names from TDM
nameSegID      = 'SEGID'
nameFG         = 'FUNCGROUP'
nameLinks      = 'LINKS'
nameLanes      = 'LANES'
nameVol        = 'VOL'
nameCap1HL     = 'CAP1HL'
nameAT         = 'AREATYPE'
nameFT         = 'FT'
nameFTClass    = 'FTCLASS'
nameFGFac      = 'FGFAC'
namePrdFac     = 'PRDFAC'
nameDYVOL      = 'DY_VOL'
nameDirections = 'DIRECTIONS'
nameDFac       = 'DFAC'
nameMDPct      = 'MDPERCENT'
nameHVPct      = 'HVPERCENT'
nameSegTotal   = 'SegDYVol_TDM'

#column for scenario year
nameSID = 'ScenarioID'
nameS =   'ScenarioName'
nameSYr = 'ScenarioYear'

#additional column name variables
nameLT = 'LT'
nameMD = 'MD'
nameHV = 'HV'

nameVolType = 'VolType'
namePrd  = 'Prd'
nameCapPer  = 'CapPer'
nameCap1Hr  = 'Cap1Hr'
nameDir     = 'Dir'

#value for functional group (FG) total row, so that it can be removed
nameFGTotalValue = 'Total'

#arrays for values by direction

aNameDir1Columns   = ['D1_'+nameFT,'D1_'+nameFTClass,'D1_'+nameLanes,'D1_'+nameCap1HL]
aNameDir2Columns   = ['D2_'+nameFT,'D2_'+nameFTClass,'D2_'+nameLanes,'D2_'+nameCap1HL]
aNameDirColumns    = [      nameFT,      nameFTClass,      nameLanes,      nameCap1HL]    
aNameDirIndexNoDir = [nameSegID,nameFG]
aNameDirIndexWiDir = [nameSegID,nameFG,nameDir]

#arrays for values by Prd
aNamePrdFac = ['DY_PRDFAC','AM_PRDFAC','MD_PRDFAC','PM_PRDFAC','EV_PRDFAC'] #add DY_PRDFAC = 1 later in script for calc ease

#arrays for values by direction, Prd
aNameDirPrdDFac      = ['D1_DY_'+nameDFac     ,'D1_AM_'+nameDFac     ,'D1_MD_'+nameDFac     ,'D1_PM_'+nameDFac     ,'D1_EV_'+nameDFac     ,'D2_DY_'+nameDFac     ,'D2_AM_'+nameDFac     ,'D2_MD_'+nameDFac     ,'D2_PM_'+nameDFac     ,'D2_EV_'+nameDFac     ]
aNameDirPrdMDPct = ['D1_DY_'+nameMDPct,'D1_AM_'+nameMDPct,'D1_MD_'+nameMDPct,'D1_PM_'+nameMDPct,'D1_EV_'+nameMDPct,'D2_DY_'+nameMDPct,'D2_AM_'+nameMDPct,'D2_MD_'+nameMDPct,'D2_PM_'+nameMDPct,'D2_EV_'+nameMDPct]
aNameDirPrdHVPct = ['D1_DY_'+nameHVPct,'D1_AM_'+nameHVPct,'D1_MD_'+nameHVPct,'D1_PM_'+nameHVPct,'D1_EV_'+nameHVPct,'D2_DY_'+nameHVPct,'D2_AM_'+nameHVPct,'D2_MD_'+nameHVPct,'D2_PM_'+nameHVPct,'D2_EV_'+nameHVPct]

indexTotal             = [nameSegID]
indexMelt              = [nameSegID,nameFG]
#indexDY             = [nameSegID,nameFG,nameCap1HL,nameLinks,nameLanes,nameAT,nameFT]

#Hrs within Prd, for capacity
dPrdDuration = {
     'Prd'     : ['AM','MD','PM','EV','DY'],
     'PrdHrs': [   3,   6,   3,  12,     24]
     
}
df_PrdDuration = pd.DataFrame(dPrdDuration)

In [11]:
dfs_TDM =[]
dfs_TDM_Total = []

#all scenarios will be read in to allow for pivoting

for (idx, row) in df_Scenarios.iterrows():

    print(row.loc[nameS] + ' CSV Processing')

    csvFileName = os.path.join(dirTDM, row.SegSummaryCSV)

    df_TDM_import = pd.read_csv(csvFileName)
    df_TDM_import[nameFG] = df_TDM_import[nameFG].str.strip() #strip leading and trailing spaces
    
    #totals for DY segment volume
    df_TDM_SegDYVol = df_TDM_import[df_TDM_import[nameFG] == nameFGTotalValue].copy()
    df_TDM_SegDYVol = df_TDM_SegDYVol[[nameSegID,nameDYVOL]]
    df_TDM_SegDYVol = df_TDM_SegDYVol.rename(columns={nameDYVOL: nameSegTotal})
    
    dfs_TDM_Total.append(df_TDM_SegDYVol[[nameSegID,nameSegTotal]])
    
    #display(df_TDM_SegDYVol)
    
    #Remove rows with no links and total
    df_TDM_import         = df_TDM_import[df_TDM_import[nameLinks] > 0                ]
    df_TDM_import         = df_TDM_import[df_TDM_import[nameFG]    != nameFGTotalValue]

    #data with segment level values
    df_TDM_Seg = pd.DataFrame.merge(df_TDM_import[[nameSegID,nameFG,nameAT,nameFGFac]],df_TDM_SegDYVol,on=nameSegID)    
    
    #normalize data with direction fields
    df_Dir1Columns          = df_TDM_import[aNameDirIndexNoDir + aNameDir1Columns].copy()
    df_Dir1Columns.columns  = (aNameDirIndexNoDir + aNameDirColumns)
    df_Dir1Columns[nameDir] = 'D1'
    
    df_Dir2Columns          = df_TDM_import[aNameDirIndexNoDir + aNameDir2Columns].copy()
    df_Dir2Columns.columns  = (aNameDirIndexNoDir + aNameDirColumns)
    df_Dir2Columns[nameDir] = 'D2'
    
    #display(df_Dir1Columns)
    #display(df_Dir2Columns)
    
    df_TDM_Dir = pd.concat([df_Dir1Columns,df_Dir2Columns])
    #display(df_Dir)
    
    #normalize data with Prd fields
    df_TDM_import['DY_PRDFAC'] = 1
    df_TDM_PrdFac = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNamePrdFac)

    #directional factors
    df_TDM_PrdFac[namePrd] = df_TDM_PrdFac['variable'].str.get(0) + df_TDM_PrdFac['variable'].str.get(1)
    df_TDM_PrdFac          = df_TDM_PrdFac.rename(columns={'value': namePrdFac})
    df_TDM_PrdFac          = df_TDM_PrdFac.drop(columns=['variable'])
    
    df_TDM_Prd = df_TDM_PrdFac
    
    #display(df_TDM_Prd)
    
    #normalize data with dir/Prd fields
    df_TDM_DFac      = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNameDirPrdDFac     )
    df_TDM_MDPct = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNameDirPrdMDPct)
    df_TDM_HVPct = pd.melt(df_TDM_import, id_vars=indexMelt, value_vars=aNameDirPrdHVPct)

    #directional factors
    df_TDM_DFac[nameDir] = df_TDM_DFac['variable'].str.get(0) + df_TDM_DFac['variable'].str.get(1)
    df_TDM_DFac[namePrd] = df_TDM_DFac['variable'].str.get(3) + df_TDM_DFac['variable'].str.get(4)
    df_TDM_DFac          = df_TDM_DFac.rename(columns={'value': nameDFac})
    df_TDM_DFac          = df_TDM_DFac.drop(columns=['variable'])
    
    #display(df_TDM_DFac)
    
    #medium truck Pcts
    df_TDM_MDPct[nameDir] = df_TDM_MDPct['variable'].str.get(0) + df_TDM_MDPct['variable'].str.get(1)
    df_TDM_MDPct[namePrd] = df_TDM_MDPct['variable'].str.get(3) + df_TDM_MDPct['variable'].str.get(4)
    df_TDM_MDPct          = df_TDM_MDPct.rename(columns={'value': nameMDPct})
    df_TDM_MDPct          = df_TDM_MDPct.drop(columns=['variable'])
    
    #display(df_TDM_MDPct)    
    
    #medium truck Pcts
    df_TDM_HVPct[nameDir] = df_TDM_HVPct['variable'].str.get(0) + df_TDM_HVPct['variable'].str.get(1)
    df_TDM_HVPct[namePrd] = df_TDM_HVPct['variable'].str.get(3) + df_TDM_HVPct['variable'].str.get(4)
    df_TDM_HVPct          = df_TDM_HVPct.rename(columns={'value': nameHVPct})
    df_TDM_HVPct          = df_TDM_HVPct.drop(columns=['variable'])
    
    #display(df_TDM_HVPct)
    
    #merge dir/Prd dataframes
    df_TDM_DirPrd = pd.DataFrame.merge(df_TDM_DFac  ,df_TDM_MDPct,on=(nameSegID,nameFG,nameDir,namePrd))
    df_TDM_DirPrd = pd.DataFrame.merge(df_TDM_DirPrd,df_TDM_HVPct,on=(nameSegID,nameFG,nameDir,namePrd))
    
    #display(df_DirPrd)
    
    df_TDM_byFGDirPrd = pd.DataFrame.merge(df_TDM_Seg          ,df_TDM_Dir   ,on=(nameSegID,nameFG)) #merge direction
    df_TDM_byFGDirPrd = pd.DataFrame.merge(df_TDM_byFGDirPrd,df_TDM_Prd   ,on=(nameSegID,nameFG)) #merge Prd
    df_TDM_byFGDirPrd = pd.DataFrame.merge(df_TDM_byFGDirPrd,df_TDM_DirPrd,on=(nameSegID,nameFG,namePrd,nameDir)) #merge Prd/direction

    #calculate DY directional for peak-Hr-Pct-of-DY calcs
    #assumes when DY volumes is used, TDM directional factor not valid, eg. weekends    
    #both directions use same directional factor
    df_TDM_byFGDirPrd.loc[(df_TDM_byFGDirPrd[namePrd] == 'DY'), nameDFac] = dDYDirectionalFactor
    df_TDM_byFGDirPrd.loc[(df_TDM_byFGDirPrd[namePrd] == 'DY'), namePrd] = 'DY'
        
    df_TDM_byFGDirPrd = df_TDM_byFGDirPrd[[nameSegID,nameAT,nameSegTotal,nameFG,nameFGFac,nameDir,nameLanes,nameFT,nameFTClass,nameCap1HL,nameDFac,namePrd,namePrdFac,nameMDPct,nameHVPct]]
    display(df_TDM_byFGDirPrd)

    dfs_TDM.append(df_TDM_byFGDirPrd)

    df_Check = df_TDM_byFGDirPrd.copy()
    df_Check['FactorsCombined'] = df_Check[nameFGFac] * df_Check[nameDFac] * df_Check[namePrdFac]
    
    #The sum of all factors should 2.2 (1.0 for non-total and 2xDFac(0.6) for totals, add little extra on each side for rounding
    df_Check = df_Check.groupby(indexTotal).agg({'FactorsCombined':[np.sum]})
    df_Check.columns = df_Check.columns.droplevel(1)
    df_Check = df_Check[((df_Check['FactorsCombined'] > 2.2003) | (df_Check['FactorsCombined'] < 2.1997) & (df_Check['FactorsCombined'] != 0))]
    display(print(row.loc[nameS] + ' Checks:'))
    display(df_Check)

print('Done')

2019 Base CSV Processing


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
1      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
2      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
3      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
4      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
...           ...       ...           ...       ...    ...  ..    ...   ...   
37205   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
37206   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
37207   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
37208   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
37209   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   

                         FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0         Principal Arterial        1065  0.6000  DY  1.0000        8.0   
1         Principal Arterial        1065  0.5004  AM  0.1829        6.3   
2         Principal Arterial        1065  0.4927  MD  0.3244        9.3   
3         Principal Arterial        1065  0.4960  PM  0.2601        6.8   
4         Principal Arterial        1065  0.5136  EV  0.2326        8.8   
...                          ...     ...     ...  ..     ...        ...   
37205           Freeway             1473  0.6000  DY  1.0000       13.1   
37206           Freeway             1473  0.4799  AM  0.1859       11.9   
37207           Freeway             1473  0.5014  MD  0.3238       14.5   
37208           Freeway             1473  0.5174  PM  0.2579       11.4   
37209           Freeway             1473  0.5447  EV  0.2324       13.8   

       HVPERCENT  
0            6.0  
1            4.5  
2            6.9  
3            5.2  
4            6.9  
...          ...  
37205        6.7  
37206        6.1  
37207        7.4  
37208        5.9  
37209        7.1  

[37210 rows x 15 columns]

2019 Base Checks:


None

Empty DataFrame
Columns: [FactorsCombined]
Index: []

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
1      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
2      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
3      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
4      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
...           ...       ...           ...       ...    ...  ..    ...  ...   
41385   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41386   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41387   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41388   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41389   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   

                         FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0         Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1         Principal Arterial        1065  0.5723  AM  0.1884        5.4   
2         Principal Arterial        1065  0.5041  MD  0.3195        9.0   
3         Principal Arterial        1065  0.4578  PM  0.2597        7.3   
4         Principal Arterial        1065  0.4811  EV  0.2324        9.5   
...                          ...     ...     ...  ..     ...        ...   
41385       Minor Arterial           939  0.6000  DY  1.0000       14.8   
41386       Minor Arterial           939  0.4840  AM  0.1903       12.6   
41387       Minor Arterial           939  0.5030  MD  0.3046       15.9   
41388       Minor Arterial           939  0.5212  PM  0.3017       14.6   
41389       Minor Arterial           939  0.5164  EV  0.2034       15.4   

       HVPERCENT  
0            5.9  
1            3.9  
2            6.8  
3            5.4  
4            7.0  
...          ...  
41385        6.5  
41386        5.6  
41387        7.2  
41388        6.1  
41389        7.0  

[41390 rows x 15 columns]

2050 Needs Checks:


None

Empty DataFrame
Columns: [FactorsCombined]
Index: []

Done


In [12]:
#df_TDM_byFGDirPrd[df_TDM_byFGDirPrd[nameSegID]=='0015_282.2']

In [13]:
#df_TDM_Seg[df_TDM_Seg[nameSegID]=='0015_282.2']

In [14]:
df_TDM_byFGDirPrd

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
1      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
2      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
3      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
4      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
...           ...       ...           ...       ...    ...  ..    ...  ...   
41385   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41386   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41387   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41388   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
41389   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   

                         FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0         Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1         Principal Arterial        1065  0.5723  AM  0.1884        5.4   
2         Principal Arterial        1065  0.5041  MD  0.3195        9.0   
3         Principal Arterial        1065  0.4578  PM  0.2597        7.3   
4         Principal Arterial        1065  0.4811  EV  0.2324        9.5   
...                          ...     ...     ...  ..     ...        ...   
41385       Minor Arterial           939  0.6000  DY  1.0000       14.8   
41386       Minor Arterial           939  0.4840  AM  0.1903       12.6   
41387       Minor Arterial           939  0.5030  MD  0.3046       15.9   
41388       Minor Arterial           939  0.5212  PM  0.3017       14.6   
41389       Minor Arterial           939  0.5164  EV  0.2034       15.4   

       HVPERCENT  
0            5.9  
1            3.9  
2            6.8  
3            5.4  
4            7.0  
...          ...  
41385        6.5  
41386        5.6  
41387        7.2  
41388        6.1  
41389        7.0  

[41390 rows x 15 columns]

In [15]:
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [16]:
df_Scenarios_toAdjust

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [17]:
#calculate adjustment for forecast for those non-RTP scenarios

dfs_ForecastAdj = []

for (idx, row) in df_Scenarios_toAdjust.iterrows():

    #print(row.loc[nameS] + ' CSV Importing')
    
    df_base = dfs_TDM_Total[idFromCode(row.loc['AdjScenarioCode'])]
    df_base.columns = (['SEGID','DYVolBase'])
    df_scenario  = dfs_TDM_Total[idFromCode(row.loc['ScenarioCode'])]
    df_scenario.columns = (['SEGID','DYVolScenario'])
    
    display(df_base)
    display(df_scenario)
    
    df_ForecastAdj = pd.DataFrame.merge(df_scenario,df_base,on=nameSegID,how='left')
    df_ForecastAdj['DYVolAdj'] = df_ForecastAdj['DYVolScenario'] - df_ForecastAdj['DYVolBase']
    
    df_ForecastAdj.to_csv(os.path.join(dirResults,'ForecastAdj_' + row.loc['ScenarioCode'] + '.csv'))
    
    display(df_ForecastAdj)
    
    dfs_ForecastAdj.append(df_ForecastAdj)

SEGID  DYVolBase
0      0006_146.9     1559.1
5      0006_149.9     1755.5
10     0006_150.6     1970.6
15     0006_152.6     2894.4
20     0006_152.9     3986.8
...           ...        ...
18850   WFRC_8215     7150.7
18855   WFRC_8216    18404.2
18860   WFRC_8217        0.0
18865   WFRC_8218    33756.9
18870   WFRC_8219     4713.8

[3775 rows x 2 columns]

SEGID  DYVolScenario
0      0006_146.9         1546.0
5      0006_149.9         1998.1
10     0006_150.6         2226.3
15     0006_152.6         3243.1
20     0006_152.9         4373.1
...           ...            ...
18350   WFRC_8213          706.9
18355   WFRC_8215         6655.8
18360   WFRC_8216        17437.8
18365   WFRC_8217            0.0
18370   WFRC_8218        34052.5

[3675 rows x 2 columns]

SEGID  DYVolScenario  DYVolBase  DYVolAdj
0     0006_146.9         1546.0     1559.1     -13.1
1     0006_149.9         1998.1     1755.5     242.6
2     0006_150.6         2226.3     1970.6     255.7
3     0006_152.6         3243.1     2894.4     348.7
4     0006_152.9         4373.1     3986.8     386.3
...          ...            ...        ...       ...
3670   WFRC_8213          706.9      710.0      -3.1
3671   WFRC_8215         6655.8     7150.7    -494.9
3672   WFRC_8216        17437.8    18404.2    -966.4
3673   WFRC_8217            0.0        0.0       0.0
3674   WFRC_8218        34052.5    33756.9     295.6

[3675 rows x 4 columns]

SEGID  DYVolBase
0      0006_146.9     1684.9
5      0006_149.9     2230.4
10     0006_150.6     2456.4
15     0006_152.6     3346.8
20     0006_152.9     4750.9
...           ...        ...
19170   WFRC_8215     9600.5
19175   WFRC_8216    22968.7
19180   WFRC_8217        0.0
19185   WFRC_8218    37570.2
19190   WFRC_8219     4935.3

[3839 rows x 2 columns]

SEGID  DYVolScenario
0      0006_146.9         1669.8
5      0006_149.9         3098.9
10     0006_150.6         3352.3
15     0006_152.6         4473.5
20     0006_152.9         6005.6
...           ...            ...
18350   WFRC_8213          829.5
18355   WFRC_8215         8957.0
18360   WFRC_8216        23391.2
18365   WFRC_8217            0.0
18370   WFRC_8218        38507.2

[3675 rows x 2 columns]

...

SEGID  DYVolScenario
0      0006_146.9         1686.0
5      0006_149.9         2111.0
10     0006_150.6         2340.3
15     0006_152.6         3251.5
20     0006_152.9         4679.7
...           ...            ...
19185   WFRC_8215         9404.2
19190   WFRC_8216        24993.1
19195   WFRC_8217            0.0
19200   WFRC_8218        38149.5
19205   WFRC_8219         4955.3

[3842 rows x 2 columns]

SEGID  DYVolScenario  DYVolBase  DYVolAdj
0     0006_146.9         1686.0     1684.9       1.1
1     0006_149.9         2111.0     2230.4    -119.4
2     0006_150.6         2340.3     2456.4    -116.1
3     0006_152.6         3251.5     3346.8     -95.3
4     0006_152.9         4679.7     4750.9     -71.2
...          ...            ...        ...       ...
3837   WFRC_8215         9404.2     9600.5    -196.3
3838   WFRC_8216        24993.1    22968.7    2024.4
3839   WFRC_8217            0.0        0.0       0.0
3840   WFRC_8218        38149.5    37570.2     579.3
3841   WFRC_8219         4955.3     4935.3      20.0

[3842 rows x 4 columns]

SEGID  DYVolBase
0      0006_146.9     1811.9
5      0006_149.9     3020.6
10     0006_150.6     3267.4
15     0006_152.6     4370.0
20     0006_152.9     5979.1
...           ...        ...
19610   WFRC_8215    12274.6
19615   WFRC_8216    28433.0
19620   WFRC_8217    25756.0
19625   WFRC_8218    42419.0
19630   WFRC_8219    13113.3

[3927 rows x 2 columns]

SEGID  DYVolScenario
0      0006_146.9         1813.3
5      0006_149.9         3029.6
10     0006_150.6         3276.9
15     0006_152.6         4372.0
20     0006_152.9         5982.7
...           ...            ...
19625   WFRC_8215        11926.5
19630   WFRC_8216        28419.9
19635   WFRC_8217        25320.7
19640   WFRC_8218        42391.0
19645   WFRC_8219        13363.9

[3930 rows x 2 columns]

SEGID  DYVolScenario  DYVolBase  DYVolAdj
0     0006_146.9         1813.3     1811.9       1.4
1     0006_149.9         3029.6     3020.6       9.0
2     0006_150.6         3276.9     3267.4       9.5
3     0006_152.6         4372.0     4370.0       2.0
4     0006_152.9         5982.7     5979.1       3.6
...          ...            ...        ...       ...
3925   WFRC_8215        11926.5    12274.6    -348.1
3926   WFRC_8216        28419.9    28433.0     -13.1
3927   WFRC_8217        25320.7    25756.0    -435.3
3928   WFRC_8218        42391.0    42419.0     -28.0
3929   WFRC_8219        13363.9    13113.3     250.6

[3930 rows x 4 columns]

# AADT and AvgAnnualPrdVol Forecasts (Segments, Forecasts, TDM)

In [18]:
#import arcgis libraries
from arcgis.gis import *
gis = GIS()

shp_Forecasts = os.path.join(dirData,  r'forecasts\WFRCForecasts_2019RTP_v831_20200508_StateWideMerged_20200608h.shp')
                        
#import into spatially-enabled DataFrame
sdf_Forecasts = pd.DataFrame.spatial.from_featureclass(shp_Forecasts)
sdf_Forecasts

FID                   RELEASE       SEGID ROUTE_ID        BMP  \
0        0  2019 RTP v8.3.1 20200508  0068_036.0     0068  36.037998   
1        1  2019 RTP v8.3.1 20200508   WFRC_8000     WFRC   1.488000   
2        2  2019 RTP v8.3.1 20200508  0131_001.7     0131   1.742000   
3        3  2019 RTP v8.3.1 20200508  0068_038.1     0068  38.106998   
4        4  2019 RTP v8.3.1 20200508  2927_000.0     2927   0.000000   
...    ...                       ...         ...      ...        ...   
8510  8510  2019 RTP v8.3.1 20200508    MAG_6248        0   0.000000   
8511  8511  2019 RTP v8.3.1 20200508  2822_000.0     2822   0.000000   
8512  8512  2019 RTP v8.3.1 20200508    MAG_6249        0   0.000000   
8513  8513  2019 RTP v8.3.1 20200508    MAG_6250        0   0.000000   
8514  8514  2019 RTP v8.3.1 20200508    MAG_6251        0   0.000000   

            EMP         FULLNAME  CO_FIPS    CO_NAME            X  ...  \
0     38.106998  CAMP WILLIAMS R       35  SALT LAKE  420614.3190  ...   
1      1.488000                        35  SALT LAKE  420880.8540  ...   
2      3.047000  PORTER ROCKWELL       35  SALT LAKE  422891.2500  ...   
3     39.167000  CAMP WILLIAMS R       35  SALT LAKE  419789.5850  ...   
4      1.019000    DEER RIDGE DR       35  SALT LAKE  428613.1110  ...   
...         ...              ...      ...        ...          ...  ...   
8510   0.000000                        49       UTAH  432054.9277  ...   
8511   3.328000     NEBO LOOP RD       49       UTAH  439736.1222  ...   
8512   0.000000                         0                  0.0000  ...   
8513   0.000000                         0                  0.0000  ...   
8514   0.000000                         0                  0.0000  ...   

      FAC_SUM  FAC_FAL  FAC_MAXMO  FAC_MAX  FACMANADJ  SUTRUCKS  CUTRUCKS  \
0       1.057    1.022          6    1.067          0     0.063     0.030   
1       1.057    1.022          6    1.067          0     0.035     0.025   
2       1.026    1.018          9    1.044          0     0.032     0.018   
3       1.057    1.022          6    1.067          0     0.040     0.020   
4       1.057    1.022          6    1.067          0     0.035     0.025   
...       ...      ...        ...      ...        ...       ...       ...   
8510    1.026    1.018          9    1.044          0     0.032     0.018   
8511    1.088    1.033          8    1.092          0     0.017     0.012   
8512    1.057    1.022          6    1.067          0     0.120     0.100   
8513    1.057    1.022          6    1.067          0     0.120     0.100   
8514    1.011    1.004          5    1.023          0     0.034     0.015   

      PLANAREA   Shape_Leng                                              SHAPE  
0         WFRC     0.000000  {"paths": [[[421160.5499999998, 4476386.34], [...  
1         WFRC     0.000000  {"paths": [[[420067.91000000015, 4479534.80000...  
2         WFRC     0.000000  {"paths": [[[422222.28000000026, 4480359.77], ...  
3         WFRC     0.000000  {"paths": [[[420067.91000000015, 4479534.80000...  
4         WFRC     0.000000  {"paths": [[[427935.76999999955, 4480756.36999...  
...        ...          ...                                                ...  
8510       MAG   473.796140  {"paths": [[[435487.7599999998, 4462445.02], [...  
8511       MAG  5344.226776  {"paths": [[[438394.3700000001, 4430771.32], [...  
8512       MAG   595.109691  {"paths": [[[442185.8794999998, 4440527.9736],...  
8513       MAG   441.873728  {"paths": [[[442531.98900000006, 4440253.285],...  
8514       MAG   807.882418  {"paths": [[[443317.86000000034, 4440169.38000...  

[8515 rows x 104 columns]

In [19]:
for col in sdf_Forecasts.columns: 
    print(col) 

FID
RELEASE
SEGID
ROUTE_ID
BMP
EMP
FULLNAME
CO_FIPS
CO_NAME
X
Y
DISTANCE
F2050
F2040
F2030
F2024
F2019
CH17TO50
CH40TO50
CH30TO40
CH24TO30
CH19TO24
CH15TO19
CH17TO19
FNOTES
MOREINFO
WFRC_FLG
AADT2017
AADT2016
AADT2015
AADT2014
AADT2013
AADT2012
AADT2011
AADT2010
AADT2009
AADT2008
AADT2007
AADT2006
AADT2005
AADT2004
AADT2003
AADT2002
AADT2001
AADT2000
AADT1999
AADT1998
AADT1997
AADT1996
AADT1994
AADT1993
AADT1992
AADT1991
AADT1990
AADT1989
AADT1988
AADT1987
AADT1986
AADT1985
AADT1984
AADT1983
AADT1982
AADT1981
SUTRK2017
CUTRK2017
DOWFACFC
DOWFACAT
FAC_MON
FAC_TUE
FAC_WED
FAC_THU
FAC_FRI
FAC_SAT
FAC_SUN
FAC_WDAVG
FAC_WEAVG
FAC_WEMAX
SSNGRP
SSNVOLCLS
SSNATGROUP
FAC_JAN
FAC_FEB
FAC_MAR
FAC_APR
FAC_MAY
FAC_JUN
FAC_JUL
FAC_AUG
FAC_SEP
FAC_OCT
FAC_NOV
FAC_DEC
FAC_WIN
FAC_SPR
FAC_SUM
FAC_FAL
FAC_MAXMO
FAC_MAX
FACMANADJ
SUTRUCKS
CUTRUCKS
PLANAREA
Shape_Leng
SHAPE


In [20]:
df = sdf_Forecasts

df = df[(df[nameSegID]=='0015_295.6')]

df

FID                   RELEASE       SEGID ROUTE_ID         BMP      EMP  \
388  388  2019 RTP v8.3.1 20200508  0015_295.6     0015  295.640991  297.944   

        FULLNAME  CO_FIPS    CO_NAME           X  ...  FAC_SUM  FAC_FAL  \
388  I-15 NB FWY       35  SALT LAKE  423474.649  ...    1.033    1.012   

     FAC_MAXMO  FAC_MAX  FACMANADJ  SUTRUCKS  CUTRUCKS  PLANAREA  Shape_Leng  \
388          8    1.039          0      0.24     0.067      WFRC         0.0   

                                                 SHAPE  
388  {"paths": [[[423819.33999999985, 4493412.10999...  

[1 rows x 104 columns]

In [21]:
#normalize data with forecasts

meltIndex    = ['SEGID','DOWFACFC','SSNGRP']
valueColumns = ['AADT2017','F2019','F2024','F2030','F2040','F2050']
df_Forecasts = pd.melt(sdf_Forecasts, id_vars=meltIndex, value_vars=valueColumns)
df_Forecasts.columns = ('SEGID','DOWFACFC','SsnGrp','FCOL','ForecastAADT')
df_Forecasts['FYEAR'] = (df_Forecasts['FCOL'].str[-4:]).astype('int64')
df_Forecasts['ForecastAADTAdj'] = 0 #placeholder column to preserve location
df_Forecasts['AvgAnnualPrdVol'] = 0 #placeholder column to preserve location
df_Forecasts = df_Forecasts[['SEGID','FYEAR','ForecastAADT','ForecastAADTAdj','AvgAnnualPrdVol','DOWFACFC','SsnGrp']]
df_Forecasts

SEGID  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0      0068_036.0   2017         31000                0                0   
1       WFRC_8000   2017             0                0                0   
2      0131_001.7   2017          1000                0                0   
3      0068_038.1   2017         22000                0                0   
4      2927_000.0   2017           500                0                0   
...           ...    ...           ...              ...              ...   
51085    MAG_6248   2050        118000                0                0   
51086  2822_000.0   2050          2100                0                0   
51087    MAG_6249   2050         15000                0                0   
51088    MAG_6250   2050         23000                0                0   
51089    MAG_6251   2050         20000                0                0   

         DOWFACFC             SsnGrp  
0        Arterial  StatewideArterial  
1        Arterial  StatewideArterial  
2        Arterial  StatewideArterial  
3        Arterial  StatewideArterial  
4        Arterial  StatewideArterial  
...           ...                ...  
51085  Expressway  StatewideArterial  
51086    Arterial  StatewideArterial  
51087    Arterial  StatewideArterial  
51088    Arterial  StatewideArterial  
51089    Arterial  StatewideArterial  

[51090 rows x 7 columns]

In [22]:
#df_Forecasts[(df_Forecasts[nameSegID]=='0015_282.2')]

In [23]:
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [24]:
#Hrs within Prd, for capacity
dRoundForecast = {
     'RoundIndex'  : [ 1,  2,   3,    4,     5],
     'ForecastBin' : [ 0,100,1000,10000,100000],
     'RoundToValue': [10, 50, 100,  500,  1000]
}
df_RoundForecast = pd.DataFrame(dRoundForecast)
display(df_RoundForecast)

lRoundBins = df_RoundForecast['ForecastBin'].to_list()
lRoundBase = df_RoundForecast['RoundToValue'].to_list()

def forecast_round(x):
    base = lRoundBase[np.digitize([x],lRoundBins)[0]-1]
    return int(base * round(float(x)/base))

#df = pd.Series([11,16,21]).apply(lambda x: custom_round(x, base=5))

RoundIndex  ForecastBin  RoundToValue
0           1            0            10
1           2          100            50
2           3         1000           100
3           4        10000           500
4           5       100000          1000

In [25]:
display(lRoundBase[np.digitize([1],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([54],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([123],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([1254],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([15456],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([2897651],lRoundBins)[0]-1])
display(lRoundBase[np.digitize([1564654654654],lRoundBins)[0]-1])

display(forecast_round(1))
display(forecast_round(54))
display(forecast_round(123))
display(forecast_round(1254))
display(forecast_round(15456))
display(forecast_round(2897651))
display(forecast_round(1564654654654))

10

10

50

100

500

...

100

1300

15500

2898000

1564654655000

In [26]:
#calculate forecast DY volume for each scenario to process

dfs_PrdForecasts = []
df_Forecasts_SYEAR_tocsv = pd.DataFrame()

for (idx, row) in df_Scenarios_toProcess.iterrows():

    _scenarioID = idx
    
    print(row.loc[nameS] + ' Processing')
    print(idx)
    #df_base = dfs_TDM_Total[idFromCode(row.loc['AdjScenarioCode'])]

    #display(dfs_TDM[idx])
    
    df_TDM = dfs_TDM[idx]
    
    #get TDM year
    _scenarioyear = yearFromID(_scenarioID)
    
    #filter only for year of forecast
    
    df_Forecasts['ForecastAADTAdj'] = df_Forecasts['ForecastAADT'] # set adjusted volume so value is set for unadjusted scenarios
    
    df_Forecasts_SYEAR = df_Forecasts[df_Forecasts.FYEAR == _scenarioyear]
    
    #adjust forecast
    
    for (idx, row) in df_Scenarios_toAdjust.iterrows():
        if (_scenarioID == idx):
            #display("adjust this")
            
            #get adjust id
            _adjustId = df_Scenarios_toAdjust.index.get_loc(idx)

            #display(_adjustId)
            #display(dfs_ForecastAdj[_adjustId])
            
            df_Forecasts_Adjust = pd.DataFrame.merge(df_Forecasts_SYEAR,dfs_ForecastAdj[_adjustId],on='SEGID')
            
            #adjust volume. if scenario vol = 0 then zero out forecast volume, otherwise forecast volume is adjusted
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['DYVolScenario'] == 0), 'ForecastAADTAdj'] = 0
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['DYVolScenario']  > 0), 'ForecastAADTAdj'] = df_Forecasts_Adjust['ForecastAADT'] + df_Forecasts_Adjust['DYVolAdj'] 
            
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['DYVolScenario'] == 0), 'ForecastAADTAdj'] = 0
            
            #if adjustment < 0 then bring to 0
            df_Forecasts_Adjust.loc[(df_Forecasts_Adjust['ForecastAADTAdj']   < 0), 'ForecastAADTAdj'] = 0  
            
            #display(df_Forecasts_Adjust) 
            
            df_Forecasts_Adjust = df_Forecasts_Adjust[['SEGID','FYEAR','ForecastAADT','ForecastAADTAdj','AvgAnnualPrdVol','DOWFACFC','SsnGrp']]
            #df_Forecasts_Adjust = df_Forecasts_Adjust.rename(columns={"DYVolBase": "ForecastAADT"})
            
            #display(df_Forecasts_Adjust['ForecastAADTAdj'])
            df_Forecasts_Adjust['RoundBin'] = np.digitize(df_Forecasts_Adjust['ForecastAADTAdj'],lRoundBins)
            df_Forecasts_Adjust_forRounding = pd.DataFrame.merge(df_Forecasts_Adjust,df_RoundForecast,left_on='RoundBin',right_on='RoundIndex')
            df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded'] = round((df_Forecasts_Adjust_forRounding['ForecastAADTAdj']/df_Forecasts_Adjust_forRounding['RoundToValue']),0)*df_Forecasts_Adjust_forRounding['RoundToValue']
            df_Forecasts_Adjust_forRounding = df_Forecasts_Adjust_forRounding.fillna(0)
            df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded'] = df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded'].astype(int)
            display(df_Forecasts_Adjust_forRounding[['ForecastAADTAdj','RoundBin','RoundToValue','ForecastAADTAdjRounded']])
            
            df_Forecasts_Adjust_forRounding['ForecastAADTAdj'] = df_Forecasts_Adjust_forRounding['ForecastAADTAdjRounded']
            
            df_Forecasts_Adjust_forRounding = df_Forecasts_Adjust_forRounding.drop(columns=['RoundIndex','ForecastBin','RoundBin','RoundToValue','ForecastAADTAdjRounded'])
            
            df_Forecasts_SYEAR = df_Forecasts_Adjust_forRounding.copy()            
            
    df_Forecasts_SYEAR = df_Forecasts_SYEAR.fillna(0)
    #df_Forecasts_SYEAR['ForecastAADT'] = df_Forecasts_SYEAR['ForecastAADT'].astype(int)
    #df_Forecasts_SYEAR['ForecastAADTAdj'] = df_Forecasts_SYEAR['ForecastAADTAdj'].astype(int)
    
    #display(df_Forecasts_SYEAR)
    
    df_Forecasts_SYEAR_export = df_Forecasts_SYEAR.copy()
    df_Forecasts_SYEAR_export['ScenarioCode'] = codeFromID(_scenarioID)
    df_Forecasts_SYEAR_export = df_Forecasts_SYEAR_export[['ScenarioCode','SEGID','ForecastAADT']]
    
    df_Forecasts_SYEAR_tocsv = pd.concat([df_Forecasts_SYEAR_tocsv,df_Forecasts_SYEAR_export])
    
    #display(os.path.join(dirResults + "0_Forecast_" + codeFromID(_scenarioID) + ".csv"))
    #df_Forecasts_SYEAR_export.to_csv(os.path.join(dirResults + r"\\0_Forecast_" + codeFromID(_scenarioID) + ".csv"),index=False)
    
    #join with TDM data
    df_Forecasts_withPrd = pd.DataFrame.merge(df_TDM, df_Forecasts_SYEAR, on=('SEGID'))
    
    df_Forecasts_withPrd['AvgAnnualPrdVol'] = df_Forecasts_withPrd['ForecastAADTAdj'] * df_Forecasts_withPrd[nameFGFac] * df_Forecasts_withPrd[nameDFac] * df_Forecasts_withPrd[namePrdFac]
    
    #display(df_Forecasts_withPrd.head(20))
    
    dfs_PrdForecasts.append(df_Forecasts_withPrd)

display(os.path.join(dirResults + "0_Forecast_" + codeFromID(_scenarioID) + ".csv"))
df_Forecasts_SYEAR_tocsv.to_csv(os.path.join(dirResults + r"\\0_Forecasts.csv"),index=False)


2019 Base Processing
0
2024 TIP Processing
1
2030 RTP Processing
2
2040 RTP Processing
3
2050 RTP Processing
4
2030 No Build Processing
5


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             48004.4         4           500                   48000
1             16923.2         4           500                   17000
2             31978.1         4           500                   32000
3             34666.0         4           500                   34500
4             22533.0         4           500                   22500
...               ...       ...           ...                     ...
3666            168.9         2            50                     150
3667            162.2         2            50                     150
3668            113.0         2            50                     100
3669            630.9         2            50                     650
3670            313.5         2            50                     300

[3671 rows x 4 columns]

2040 No Build Processing
6


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             48920.1         4           500                   49000
1             25166.9         4           500                   25000
2             12111.7         4           500                   12000
3             37638.5         4           500                   37500
4             15692.2         4           500                   15500
...               ...       ...           ...                     ...
3666            660.9         2            50                     650
3667            298.4         2            50                     300
3668            544.7         2            50                     550
3669            760.8         2            50                     750
3670            237.9         2            50                     250

[3671 rows x 4 columns]

2050 No Build Processing
7


...

2040 Needs Processing
9


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             10047.4         4           500                   10000
1             48007.9         4           500                   48000
2             28463.0         4           500                   28500
3             37612.8         4           500                   37500
4             25318.3         4           500                   25500
...               ...       ...           ...                     ...
3805            526.5         2            50                     550
3806            568.9         2            50                     550
3807            406.0         2            50                     400
3808            438.8         2            50                     450
3809            126.0         2            50                     150

[3810 rows x 4 columns]

2050 Needs Processing
10


ForecastAADTAdj  RoundBin  RoundToValue  ForecastAADTAdjRounded
0             10132.6         4           500                   10000
1             56174.6         4           500                   56000
2             20949.8         4           500                   21000
3             31991.7         4           500                   32000
4             28718.9         4           500                   28500
...               ...       ...           ...                     ...
3893            698.2         2            50                     700
3894            948.8         2            50                     950
3895            200.9         2            50                     200
3896            100.1         2            50                     100
3897            400.5         2            50                     400

[3898 rows x 4 columns]

'E:\\GitHub\\V-over-C-Calculations\\results0_Forecast_UF50.csv'

In [27]:
df = dfs_PrdForecasts[10]

df[(df[nameSegID]=='0015_282.2')]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP   FGFAC Dir  LANES    FT  \
920  0015_282.2       4.0      251700.9  Arterial  0.0507  D1    2.0   3.0   
921  0015_282.2       4.0      251700.9  Arterial  0.0507  D1    2.0   3.0   
922  0015_282.2       4.0      251700.9  Arterial  0.0507  D1    2.0   3.0   
923  0015_282.2       4.0      251700.9  Arterial  0.0507  D1    2.0   3.0   
924  0015_282.2       4.0      251700.9  Arterial  0.0507  D1    2.0   3.0   
925  0015_282.2       4.0      251700.9  Arterial  0.0507  D2    2.0   3.0   
926  0015_282.2       4.0      251700.9  Arterial  0.0507  D2    2.0   3.0   
927  0015_282.2       4.0      251700.9  Arterial  0.0507  D2    2.0   3.0   
928  0015_282.2       4.0      251700.9  Arterial  0.0507  D2    2.0   3.0   
929  0015_282.2       4.0      251700.9  Arterial  0.0507  D2    2.0   3.0   
930  0015_282.2       4.0      251700.9   Freeway  0.6973  D1    5.0  23.0   
931  0015_282.2       4.0      251700.9   Freeway  0.6973  D1    5.0  23.0   
932  0015_282.2       4.0      251700.9   Freeway  0.6973  D1    5.0  23.0   
933  0015_282.2       4.0      251700.9   Freeway  0.6973  D1    5.0  23.0   
934  0015_282.2       4.0      251700.9   Freeway  0.6973  D1    5.0  23.0   
935  0015_282.2       4.0      251700.9   Freeway  0.6973  D2    5.0  23.0   
936  0015_282.2       4.0      251700.9   Freeway  0.6973  D2    5.0  23.0   
937  0015_282.2       4.0      251700.9   Freeway  0.6973  D2    5.0  23.0   
938  0015_282.2       4.0      251700.9   Freeway  0.6973  D2    5.0  23.0   
939  0015_282.2       4.0      251700.9   Freeway  0.6973  D2    5.0  23.0   
940  0015_282.2       4.0      251700.9   Managed  0.0952  D1    1.0  38.0   
941  0015_282.2       4.0      251700.9   Managed  0.0952  D1    1.0  38.0   
942  0015_282.2       4.0      251700.9   Managed  0.0952  D1    1.0  38.0   
943  0015_282.2       4.0      251700.9   Managed  0.0952  D1    1.0  38.0   
944  0015_282.2       4.0      251700.9   Managed  0.0952  D1    1.0  38.0   
945  0015_282.2       4.0      251700.9   Managed  0.0952  D2    1.0  38.0   
946  0015_282.2       4.0      251700.9   Managed  0.0952  D2    1.0  38.0   
947  0015_282.2       4.0      251700.9   Managed  0.0952  D2    1.0  38.0   
948  0015_282.2       4.0      251700.9   Managed  0.0952  D2    1.0  38.0   
949  0015_282.2       4.0      251700.9   Managed  0.0952  D2    1.0  38.0   
950  0015_282.2       4.0      251700.9   CD Road  0.1567  D1    2.0  21.0   
951  0015_282.2       4.0      251700.9   CD Road  0.1567  D1    2.0  21.0   
952  0015_282.2       4.0      251700.9   CD Road  0.1567  D1    2.0  21.0   
953  0015_282.2       4.0      251700.9   CD Road  0.1567  D1    2.0  21.0   
954  0015_282.2       4.0      251700.9   CD Road  0.1567  D1    2.0  21.0   
955  0015_282.2       4.0      251700.9   CD Road  0.1567  D2    2.0  21.0   
956  0015_282.2       4.0      251700.9   CD Road  0.1567  D2    2.0  21.0   
957  0015_282.2       4.0      251700.9   CD Road  0.1567  D2    2.0  21.0   
958  0015_282.2       4.0      251700.9   CD Road  0.1567  D2    2.0  21.0   
959  0015_282.2       4.0      251700.9   CD Road  0.1567  D2    2.0  21.0   

                       FTCLASS  CAP1HL  ...  Prd  PRDFAC  MDPERCENT  \
920       Minor Arterial           978  ...   DY  1.0000       11.7   
921       Minor Arterial           978  ...   AM  0.2184        8.9   
922       Minor Arterial           978  ...   MD  0.2923       12.1   
923       Minor Arterial           978  ...   PM  0.2931       11.9   
924       Minor Arterial           978  ...   EV  0.1962       15.5   
925       Minor Arterial           972  ...   DY  1.0000       10.7   
926       Minor Arterial           972  ...   AM  0.2184       16.2   
927       Minor Arterial           972  ...   MD  0.2923       11.4   
928       Minor Arterial           972  ...   PM  0.2931        9.4   
929       Minor Arterial           972  ...   EV  0.1962       10.2   
930           Freeway         

# Adjust for Season, DOW

In [28]:
#read in data from other notebook pre-processing

csv_SeasonFactors = os.path.join(dirFactors, r'SeasonFactors.csv')
csv_DOWFactors = os.path.join(dirFactors, r'DOWFactors.csv')
csv_TODFactors = os.path.join(dirFactors, r'TODFactors.csv')

df_SeasonFactors = pd.read_csv(csv_SeasonFactors)
df_DOWFactors = pd.read_csv(csv_DOWFactors)
df_TODFactors = pd.read_csv(csv_TODFactors)

df_SeasonFactors = df_SeasonFactors.rename(columns={"FuncGroup": nameFG, "AreaType": nameAT})
df_DOWFactors = df_DOWFactors.rename(columns={"FuncGroup": nameFG, "AreaType": nameAT})
df_TODFactors = df_TODFactors.rename(columns={"FuncGroup": nameFG, "AreaType": nameAT})

display(df_SeasonFactors)
display(df_DOWFactors)
display(df_TODFactors)
display(df_TODFactors[df_TODFactors['SeasonGroup']=='S00-Ann'])

SsnGrp      SsnATGroup     SsnVolCls  AREATYPE  Vol_From  \
0            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
1            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
2            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
3            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
4            AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
...                 ...             ...           ...       ...       ...   
8887  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8888  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8889  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8890  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
8891  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   

       Vol_To FUNCGROUP SiteGroupSeason SeasonGroup  SeasonFactor  
0     1000000  Arterial             SN0     M01-Jan         0.273  
1     1000000  Arterial             SN0     M02-Feb         0.303  
2     1000000  Arterial             SN0     M03-Mar         0.397  
3     1000000  Arterial             SN0     M04-Apr         0.499  
4     1000000  Arterial             SN0     M05-May         1.005  
...       ...       ...             ...         ...           ...  
8887  1000000   CD Road             SNX     S03-Sum         1.066  
8888  1000000   CD Road             SNX     S04-Fal         1.001  
8889  1000000   CD Road             SNX    MaxMonth         1.099  
8890  1000000   CD Road             SNX   MaxSeason         1.066  
8891  1000000   CD Road             SNX     S00-Ann         1.000  

[8892 rows x 10 columns]

DOWFACFC  AREATYPE FUNCGROUP SiteGroupDOW     DOWGroup  DOWFactor
0        Arterial         1  Arterial          WD0     1-Monday      0.907
1        Arterial         1  Arterial          WD0    2-Tuesday      0.902
2        Arterial         1  Arterial          WD0  3-Wednesday      0.943
3        Arterial         1  Arterial          WD0   4-Thursday      0.995
4        Arterial         1  Arterial          WD0     5-Friday      1.170
...           ...       ...       ...          ...          ...        ...
2335  FreewayUS40         5   CD Road          WDK     5-Friday      1.170
2336  FreewayUS40         5   CD Road          WDK   6-Saturday      1.029
2337  FreewayUS40         5   CD Road          WDK     7-Sunday      0.777
2338  FreewayUS40         5   CD Road          WDK   W1-Weekday      1.007
2339  FreewayUS40         5   CD Road          WDK    MaxSatSun      1.007

[2340 rows x 6 columns]

SiteGroupSeason SeasonGroup    DOWGroup Prd HrPctOf  VolPkHrPct
0                 SN0     M01-Jan    1-Monday  AM     Prd      0.5528
1                 SN0     M01-Jan    1-Monday  DY     Prd      0.1351
2                 SN0     M01-Jan    1-Monday  EV     Prd      0.2926
3                 SN0     M01-Jan    1-Monday  MD     Prd      0.2534
4                 SN0     M01-Jan    1-Monday  PM     Prd      0.4179
...               ...         ...         ...  ..     ...         ...
58135             XX4     S04-Fal  W2-Weekend  AM      DY      0.0611
58136             XX4     S04-Fal  W2-Weekend  DY      DY      0.0872
58137             XX4     S04-Fal  W2-Weekend  EV      DY      0.0623
58138             XX4     S04-Fal  W2-Weekend  MD      DY      0.0658
58139             XX4     S04-Fal  W2-Weekend  PM      DY      0.0867

[58140 rows x 6 columns]

SiteGroupSeason SeasonGroup    DOWGroup Prd HrPctOf  VolPkHrPct
540               SN0     S00-Ann    1-Monday  AM     Prd      0.4722
541               SN0     S00-Ann    1-Monday  DY     Prd      0.1144
542               SN0     S00-Ann    1-Monday  EV     Prd      0.2825
543               SN0     S00-Ann    1-Monday  MD     Prd      0.2266
544               SN0     S00-Ann    1-Monday  PM     Prd      0.3920
...               ...         ...         ...  ..     ...         ...
57955             XX4     S00-Ann  W2-Weekend  AM      DY      0.0608
57956             XX4     S00-Ann  W2-Weekend  DY      DY      0.0872
57957             XX4     S00-Ann  W2-Weekend  EV      DY      0.0617
57958             XX4     S00-Ann  W2-Weekend  MD      DY      0.0658
57959             XX4     S00-Ann  W2-Weekend  PM      DY      0.0867

[3420 rows x 6 columns]

In [29]:
df_SD = pd.DataFrame.merge(df_SeasonFactors,df_DOWFactors,on=(nameAT,nameFG))
df_SD

SsnGrp      SsnATGroup     SsnVolCls  AREATYPE  Vol_From  \
0               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
1               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
2               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
3               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
4               AlpineLoop  0-AllAreaTypes  0-AllVolumes         1         0   
...                    ...             ...           ...       ...       ...   
1040359  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040360  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040361  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040362  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   
1040363  WashingtonFreeway  0-AllAreaTypes  0-AllVolumes         5         0   

          Vol_To FUNCGROUP SiteGroupSeason SeasonGroup  SeasonFactor  \
0        1000000  Arterial             SN0     M01-Jan         0.273   
1        1000000  Arterial             SN0     M01-Jan         0.273   
2        1000000  Arterial             SN0     M01-Jan         0.273   
3        1000000  Arterial             SN0     M01-Jan         0.273   
4        1000000  Arterial             SN0     M01-Jan         0.273   
...          ...       ...             ...         ...           ...   
1040359  1000000   CD Road             SNX     S00-Ann         1.000   
1040360  1000000   CD Road             SNX     S00-Ann         1.000   
1040361  1000000   CD Road             SNX     S00-Ann         1.000   
1040362  1000000   CD Road             SNX     S00-Ann         1.000   
1040363  1000000   CD Road             SNX     S00-Ann         1.000   

            DOWFACFC SiteGroupDOW     DOWGroup  DOWFactor  
0           Arterial          WD0     1-Monday      0.907  
1           Arterial          WD0    2-Tuesday      0.902  
2           Arterial          WD0  3-Wednesday      0.943  
3           Arterial          WD0   4-Thursday      0.995  
4           Arterial          WD0     5-Friday      1.170  
...              ...          ...          ...        ...  
1040359  FreewayUS40          WDK     5-Friday      1.170  
1040360  FreewayUS40          WDK   6-Saturday      1.029  
1040361  FreewayUS40          WDK     7-Sunday      0.777  
1040362  FreewayUS40          WDK   W1-Weekday      1.007  
1040363  FreewayUS40          WDK    MaxSatSun      1.007  

[1040364 rows x 14 columns]

In [30]:
#add season factor

dfs_PrdForecasts_Season = []

#for (idx, row) in dfs_PrdForecasts.iterrows():

for df_PrdForecasts in dfs_PrdForecasts: 
    
    #joing forecasts data with season factors
    df_PrdForecasts_Season = pd.DataFrame.merge(df_PrdForecasts,df_SeasonFactors,on=('SsnGrp',nameFG,nameAT),how='left')
    
    #remove unapplicable volume classes
    df_PrdForecasts_Season = df_PrdForecasts_Season[(df_PrdForecasts_Season.ForecastAADT >= df_PrdForecasts_Season.Vol_From) & (df_PrdForecasts_Season.ForecastAADT < df_PrdForecasts_Season.Vol_To)]
    
    #calculate Average Season
    df_PrdForecasts_Season['AvgSsnPrdVol'] = df_PrdForecasts_Season['AvgAnnualPrdVol'] *df_PrdForecasts_Season['SeasonFactor'] 
    df_PrdForecasts_Season['AvgSsnPrdVol'] = df_PrdForecasts_Season['AvgSsnPrdVol'].astype(int)
    
    display(df_PrdForecasts_Season)
    
    dfs_PrdForecasts_Season.append(df_PrdForecasts_Season)
    

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
19      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
20      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
21      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
22      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
23      0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
...            ...       ...           ...       ...    ...  ..    ...   ...   
767215   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
767216   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
767217   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
767218   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
767219   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   

                          FTCLASS  CAP1HL  ...     DOWFACFC  \
19         Principal Arterial        1065  ...     Arterial   
20         Principal Arterial        1065  ...     Arterial   
21         Principal Arterial        1065  ...     Arterial   
22         Principal Arterial        1065  ...     Arterial   
23         Principal Arterial        1065  ...     Arterial   
...                           ...     ...  ...          ...   
767215           Freeway             1473  ...  FreewayI215   
767216           Freeway             1473  ...  FreewayI215   
767217           Freeway             1473  ...  FreewayI215   
767218           Freeway             1473  ...  FreewayI215   
767219           Freeway             1473  ...  FreewayI215   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
19      StatewideArterial         1-Rural    UTRuralLow         0     2500   
20      StatewideArterial         1-Rural    UTRuralLow         0     2500   
21      StatewideArterial         1-Rural    UTRuralLow         0     2500   
22      StatewideArterial         1-Rural    UTRuralLow         0     2500   
23      StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
767215        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767216        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767217        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767218        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767219        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   

        SiteGroupSeason  SeasonGroup  SeasonFactor AvgSsnPrdVol  
19                  SNP      M01-Jan         0.815            0  
20                  SNP      M02-Feb         0.862            0  
21                  SNP      M03-Mar         0.949            0  
22                  SNP      M04-Apr         1.023            0  
23                  SNP      M05-May         1.079            0  
...                 ...          ...           ...          ...  
767215              SN8      S03-Sum         1.012         3266  
767216              SN8      S04-Fal         1.003         3237  
767217              SN8     MaxMonth         1.025         3308  
767218              SN8    MaxSeason         1.015         3276  
767219              SN8      S00-Ann         1.000         3228  

[706420 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
19      0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
20      0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
21      0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
22      0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
23      0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
...            ...       ...           ...       ...    ...  ..    ...   ...   
767215   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
767216   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
767217   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
767218   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
767219   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   

                          FTCLASS  CAP1HL  ...     DOWFACFC  \
19         Principal Arterial        1065  ...     Arterial   
20         Principal Arterial        1065  ...     Arterial   
21         Principal Arterial        1065  ...     Arterial   
22         Principal Arterial        1065  ...     Arterial   
23         Principal Arterial        1065  ...     Arterial   
...                           ...     ...  ...          ...   
767215           Freeway             1473  ...  FreewayI215   
767216           Freeway             1473  ...  FreewayI215   
767217           Freeway             1473  ...  FreewayI215   
767218           Freeway             1473  ...  FreewayI215   
767219           Freeway             1473  ...  FreewayI215   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
19      StatewideArterial         1-Rural    UTRuralLow         0     2500   
20      StatewideArterial         1-Rural    UTRuralLow         0     2500   
21      StatewideArterial         1-Rural    UTRuralLow         0     2500   
22      StatewideArterial         1-Rural    UTRuralLow         0     2500   
23      StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
767215        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767216        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767217        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767218        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
767219        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   

        SiteGroupSeason  SeasonGroup  SeasonFactor AvgSsnPrdVol  
19                  SNP      M01-Jan         0.815            0  
20                  SNP      M02-Feb         0.862            0  
21                  SNP      M03-Mar         0.949            0  
22                  SNP      M04-Apr         1.023            0  
23                  SNP      M05-May         1.079            0  
...                 ...          ...           ...          ...  
767215              SN8      S03-Sum         1.012         3358  
767216              SN8      S04-Fal         1.003         3328  
767217              SN8     MaxMonth         1.025         3401  
767218              SN8    MaxSeason         1.015         3368  
767219              SN8      S00-Ann         1.000         3318  

[717820 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
782795   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
782796   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
782797   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
782798   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
782799   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL  ...  DOWFACFC             SsnGrp  \
19         Principal Arterial        1065  ...  Arterial  StatewideArterial   
20         Principal Arterial        1065  ...  Arterial  StatewideArterial   
21         Principal Arterial        1065  ...  Arterial  StatewideArterial   
22         Principal Arterial        1065  ...  Arterial  StatewideArterial   
23         Principal Arterial        1065  ...  Arterial  StatewideArterial   
...                           ...     ...  ...       ...                ...   
782795       Minor Arterial           939  ...  Arterial  StatewideArterial   
782796       Minor Arterial           939  ...  Arterial  StatewideArterial   
782797       Minor Arterial           939  ...  Arterial  StatewideArterial   
782798       Minor Arterial           939  ...  Arterial  StatewideArterial   
782799       Minor Arterial           939  ...  Arterial  StatewideArterial   

          SsnATGroup     SsnVolCls  Vol_From   Vol_To  SiteGroupSeason  \
19           1-Rural    UTRuralLow         0     2500              SNP   
20           1-Rural    UTRuralLow         0     2500              SNP   
21           1-Rural    UTRuralLow         0     2500              SNP   
22           1-Rural    UTRuralLow         0     2500              SNP   
23           1-Rural    UTRuralLow         0     2500              SNP   
...              ...           ...       ...      ...              ...   
782795  2-Transition  0-AllVolumes         0  1000000              SNS   
782796  2-Transition  0-AllVolumes         0  1000000              SNS   
782797  2-Transition  0-AllVolumes         0  1000000              SNS   
782798  2-Transition  0-AllVolumes         0  1000000              SNS   
782799  2-Transition  0-AllVolumes         0  1000000              SNS   

        SeasonGroup  SeasonFactor AvgSsnPrdVol  
19          M01-Jan         0.815            0  
20          M02-Feb         0.862            0  
21          M03-Mar         0.949            0  
22          M04-Apr         1.023            0  
23          M05-May         1.079            0  
...             ...           ...          ...  
782795      S03-Sum         1.057          743  
782796      S04-Fal         1.022          718  
782797     MaxMonth         1.067          750  
782798    MaxSeason         1.057          743  
782799      S00-Ann         1.000          703  

[739100 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
792865   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
792866   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
792867   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
792868   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
792869   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL  ...  DOWFACFC             SsnGrp  \
19         Principal Arterial        1065  ...  Arterial  StatewideArterial   
20         Principal Arterial        1065  ...  Arterial  StatewideArterial   
21         Principal Arterial        1065  ...  Arterial  StatewideArterial   
22         Principal Arterial        1065  ...  Arterial  StatewideArterial   
23         Principal Arterial        1065  ...  Arterial  StatewideArterial   
...                           ...     ...  ...       ...                ...   
792865       Minor Arterial           939  ...  Arterial  StatewideArterial   
792866       Minor Arterial           939  ...  Arterial  StatewideArterial   
792867       Minor Arterial           939  ...  Arterial  StatewideArterial   
792868       Minor Arterial           939  ...  Arterial  StatewideArterial   
792869       Minor Arterial           939  ...  Arterial  StatewideArterial   

          SsnATGroup     SsnVolCls  Vol_From   Vol_To  SiteGroupSeason  \
19           1-Rural    UTRuralLow         0     2500              SNP   
20           1-Rural    UTRuralLow         0     2500              SNP   
21           1-Rural    UTRuralLow         0     2500              SNP   
22           1-Rural    UTRuralLow         0     2500              SNP   
23           1-Rural    UTRuralLow         0     2500              SNP   
...              ...           ...       ...      ...              ...   
792865  2-Transition  0-AllVolumes         0  1000000              SNS   
792866  2-Transition  0-AllVolumes         0  1000000              SNS   
792867  2-Transition  0-AllVolumes         0  1000000              SNS   
792868  2-Transition  0-AllVolumes         0  1000000              SNS   
792869  2-Transition  0-AllVolumes         0  1000000              SNS   

        SeasonGroup  SeasonFactor AvgSsnPrdVol  
19          M01-Jan         0.815            0  
20          M02-Feb         0.862            0  
21          M03-Mar         0.949            0  
22          M04-Apr         1.023            0  
23          M05-May         1.079            0  
...             ...           ...          ...  
792865      S03-Sum         1.057          791  
792866      S04-Fal         1.022          765  
792867     MaxMonth         1.067          799  
792868    MaxSeason         1.057          791  
792869      S00-Ann         1.000          748  

[758670 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
798375   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
798376   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
798377   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
798378   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
798379   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL  ...  DOWFACFC             SsnGrp  \
19         Principal Arterial        1065  ...  Arterial  StatewideArterial   
20         Principal Arterial        1065  ...  Arterial  StatewideArterial   
21         Principal Arterial        1065  ...  Arterial  StatewideArterial   
22         Principal Arterial        1065  ...  Arterial  StatewideArterial   
23         Principal Arterial        1065  ...  Arterial  StatewideArterial   
...                           ...     ...  ...       ...                ...   
798375       Minor Arterial           939  ...  Arterial  StatewideArterial   
798376       Minor Arterial           939  ...  Arterial  StatewideArterial   
798377       Minor Arterial           939  ...  Arterial  StatewideArterial   
798378       Minor Arterial           939  ...  Arterial  StatewideArterial   
798379       Minor Arterial           939  ...  Arterial  StatewideArterial   

          SsnATGroup     SsnVolCls  Vol_From   Vol_To  SiteGroupSeason  \
19           1-Rural    UTRuralLow         0     2500              SNP   
20           1-Rural    UTRuralLow         0     2500              SNP   
21           1-Rural    UTRuralLow         0     2500              SNP   
22           1-Rural    UTRuralLow         0     2500              SNP   
23           1-Rural    UTRuralLow         0     2500              SNP   
...              ...           ...       ...      ...              ...   
798375  2-Transition  0-AllVolumes         0  1000000              SNS   
798376  2-Transition  0-AllVolumes         0  1000000              SNS   
798377  2-Transition  0-AllVolumes         0  1000000              SNS   
798378  2-Transition  0-AllVolumes         0  1000000              SNS   
798379  2-Transition  0-AllVolumes         0  1000000              SNS   

        SeasonGroup  SeasonFactor AvgSsnPrdVol  
19          M01-Jan         0.815         1026  
20          M02-Feb         0.862         1086  
21          M03-Mar         0.949         1195  
22          M04-Apr         1.023         1288  
23          M05-May         1.079         1359  
...             ...           ...          ...  
798375      S03-Sum         1.057         1351  
798376      S04-Fal         1.022         1307  
798377     MaxMonth         1.067         1364  
798378    MaxSeason         1.057         1351  
798379      S00-Ann         1.000         1279  

[779760 rows x 29 columns]

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
19      0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
20      0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
21      0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
22      0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
23      0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
...            ...       ...           ...       ...    ...  ..    ...   ...   
748975   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
748976   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
748977   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
748978   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
748979   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   

                          FTCLASS  CAP1HL  ...     DOWFACFC  \
19         Principal Arterial        1065  ...     Arterial   
20         Principal Arterial        1065  ...     Arterial   
21         Principal Arterial        1065  ...     Arterial   
22         Principal Arterial        1065  ...     Arterial   
23         Principal Arterial        1065  ...     Arterial   
...                           ...     ...  ...          ...   
748975           Freeway             1473  ...  FreewayI215   
748976           Freeway             1473  ...  FreewayI215   
748977           Freeway             1473  ...  FreewayI215   
748978           Freeway             1473  ...  FreewayI215   
748979           Freeway             1473  ...  FreewayI215   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
19      StatewideArterial         1-Rural    UTRuralLow         0     2500   
20      StatewideArterial         1-Rural    UTRuralLow         0     2500   
21      StatewideArterial         1-Rural    UTRuralLow         0     2500   
22      StatewideArterial         1-Rural    UTRuralLow         0     2500   
23      StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
748975        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
748976        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
748977        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
748978        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
748979        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   

        SiteGroupSeason  SeasonGroup  SeasonFactor AvgSsnPrdVol  
19                  SNP      M01-Jan         0.815            0  
20                  SNP      M02-Feb         0.862            0  
21                  SNP      M03-Mar         0.949            0  
22                  SNP      M04-Apr         1.023            0  
23                  SNP      M05-May         1.079            0  
...                 ...          ...           ...          ...  
748975              SN8      S03-Sum         1.012         4271  
748976              SN8      S04-Fal         1.003         4233  
748977              SN8     MaxMonth         1.025         4326  
748978              SN8    MaxSeason         1.015         4284  
748979              SN8      S00-Ann         1.000         4221  

[717820 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
19      0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
20      0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
21      0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
22      0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
23      0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
...            ...       ...           ...       ...    ...  ..    ...   ...   
732635   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
732636   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
732637   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
732638   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
732639   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   

                          FTCLASS  CAP1HL  ...     DOWFACFC  \
19         Principal Arterial        1065  ...     Arterial   
20         Principal Arterial        1065  ...     Arterial   
21         Principal Arterial        1065  ...     Arterial   
22         Principal Arterial        1065  ...     Arterial   
23         Principal Arterial        1065  ...     Arterial   
...                           ...     ...  ...          ...   
732635           Freeway             1473  ...  FreewayI215   
732636           Freeway             1473  ...  FreewayI215   
732637           Freeway             1473  ...  FreewayI215   
732638           Freeway             1473  ...  FreewayI215   
732639           Freeway             1473  ...  FreewayI215   

                   SsnGrp      SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
19      StatewideArterial         1-Rural    UTRuralLow         0     2500   
20      StatewideArterial         1-Rural    UTRuralLow         0     2500   
21      StatewideArterial         1-Rural    UTRuralLow         0     2500   
22      StatewideArterial         1-Rural    UTRuralLow         0     2500   
23      StatewideArterial         1-Rural    UTRuralLow         0     2500   
...                   ...             ...           ...       ...      ...   
732635        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
732636        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
732637        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
732638        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   
732639        FreewayI215  0-AllAreaTypes  0-AllVolumes         0  1000000   

        SiteGroupSeason  SeasonGroup  SeasonFactor AvgSsnPrdVol  
19                  SNP      M01-Jan         0.815         1026  
20                  SNP      M02-Feb         0.862         1086  
21                  SNP      M03-Mar         0.949         1195  
22                  SNP      M04-Apr         1.023         1288  
23                  SNP      M05-May         1.079         1359  
...                 ...          ...           ...          ...  
732635              SN8      S03-Sum         1.012         4769  
732636              SN8      S04-Fal         1.003         4726  
732637              SN8     MaxMonth         1.025         4830  
732638              SN8    MaxSeason         1.015         4783  
732639              SN8      S00-Ann         1.000         4712  

[717820 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
783365   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
783366   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
783367   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
783368   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
783369   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL  ...  DOWFACFC             SsnGrp  \
19         Principal Arterial        1065  ...  Arterial  StatewideArterial   
20         Principal Arterial        1065  ...  Arterial  StatewideArterial   
21         Principal Arterial        1065  ...  Arterial  StatewideArterial   
22         Principal Arterial        1065  ...  Arterial  StatewideArterial   
23         Principal Arterial        1065  ...  Arterial  StatewideArterial   
...                           ...     ...  ...       ...                ...   
783365       Minor Arterial           939  ...  Arterial  StatewideArterial   
783366       Minor Arterial           939  ...  Arterial  StatewideArterial   
783367       Minor Arterial           939  ...  Arterial  StatewideArterial   
783368       Minor Arterial           939  ...  Arterial  StatewideArterial   
783369       Minor Arterial           939  ...  Arterial  StatewideArterial   

          SsnATGroup     SsnVolCls  Vol_From   Vol_To  SiteGroupSeason  \
19           1-Rural    UTRuralLow         0     2500              SNP   
20           1-Rural    UTRuralLow         0     2500              SNP   
21           1-Rural    UTRuralLow         0     2500              SNP   
22           1-Rural    UTRuralLow         0     2500              SNP   
23           1-Rural    UTRuralLow         0     2500              SNP   
...              ...           ...       ...      ...              ...   
783365  2-Transition  0-AllVolumes         0  1000000              SNS   
783366  2-Transition  0-AllVolumes         0  1000000              SNS   
783367  2-Transition  0-AllVolumes         0  1000000              SNS   
783368  2-Transition  0-AllVolumes         0  1000000              SNS   
783369  2-Transition  0-AllVolumes         0  1000000              SNS   

        SeasonGroup  SeasonFactor AvgSsnPrdVol  
19          M01-Jan         0.815            0  
20          M02-Feb         0.862            0  
21          M03-Mar         0.949            0  
22          M04-Apr         1.023            0  
23          M05-May         1.079            0  
...             ...           ...          ...  
783365      S03-Sum         1.057          754  
783366      S04-Fal         1.022          729  
783367     MaxMonth         1.067          761  
783368    MaxSeason         1.057          754  
783369      S00-Ann         1.000          713  

[740430 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
795715   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
795716   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
795717   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
795718   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
795719   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL  ...  DOWFACFC             SsnGrp  \
19         Principal Arterial        1065  ...  Arterial  StatewideArterial   
20         Principal Arterial        1065  ...  Arterial  StatewideArterial   
21         Principal Arterial        1065  ...  Arterial  StatewideArterial   
22         Principal Arterial        1065  ...  Arterial  StatewideArterial   
23         Principal Arterial        1065  ...  Arterial  StatewideArterial   
...                           ...     ...  ...       ...                ...   
795715       Minor Arterial           939  ...  Arterial  StatewideArterial   
795716       Minor Arterial           939  ...  Arterial  StatewideArterial   
795717       Minor Arterial           939  ...  Arterial  StatewideArterial   
795718       Minor Arterial           939  ...  Arterial  StatewideArterial   
795719       Minor Arterial           939  ...  Arterial  StatewideArterial   

          SsnATGroup     SsnVolCls  Vol_From   Vol_To  SiteGroupSeason  \
19           1-Rural    UTRuralLow         0     2500              SNP   
20           1-Rural    UTRuralLow         0     2500              SNP   
21           1-Rural    UTRuralLow         0     2500              SNP   
22           1-Rural    UTRuralLow         0     2500              SNP   
23           1-Rural    UTRuralLow         0     2500              SNP   
...              ...           ...       ...      ...              ...   
795715  2-Transition  0-AllVolumes         0  1000000              SNS   
795716  2-Transition  0-AllVolumes         0  1000000              SNS   
795717  2-Transition  0-AllVolumes         0  1000000              SNS   
795718  2-Transition  0-AllVolumes         0  1000000              SNS   
795719  2-Transition  0-AllVolumes         0  1000000              SNS   

        SeasonGroup  SeasonFactor AvgSsnPrdVol  
19          M01-Jan         0.815            0  
20          M02-Feb         0.862            0  
21          M03-Mar         0.949            0  
22          M04-Apr         1.023            0  
23          M05-May         1.079            0  
...             ...           ...          ...  
795715      S03-Sum         1.057          800  
795716      S04-Fal         1.022          773  
795717     MaxMonth         1.067          808  
795718    MaxSeason         1.057          800  
795719      S00-Ann         1.000          757  

[761140 rows x 29 columns]

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
19      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
20      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
21      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
22      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
23      0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
798945   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
798946   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
798947   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
798948   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
798949   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL  ...  DOWFACFC             SsnGrp  \
19         Principal Arterial        1065  ...  Arterial  StatewideArterial   
20         Principal Arterial        1065  ...  Arterial  StatewideArterial   
21         Principal Arterial        1065  ...  Arterial  StatewideArterial   
22         Principal Arterial        1065  ...  Arterial  StatewideArterial   
23         Principal Arterial        1065  ...  Arterial  StatewideArterial   
...                           ...     ...  ...       ...                ...   
798945       Minor Arterial           939  ...  Arterial  StatewideArterial   
798946       Minor Arterial           939  ...  Arterial  StatewideArterial   
798947       Minor Arterial           939  ...  Arterial  StatewideArterial   
798948       Minor Arterial           939  ...  Arterial  StatewideArterial   
798949       Minor Arterial           939  ...  Arterial  StatewideArterial   

          SsnATGroup     SsnVolCls  Vol_From   Vol_To  SiteGroupSeason  \
19           1-Rural    UTRuralLow         0     2500              SNP   
20           1-Rural    UTRuralLow         0     2500              SNP   
21           1-Rural    UTRuralLow         0     2500              SNP   
22           1-Rural    UTRuralLow         0     2500              SNP   
23           1-Rural    UTRuralLow         0     2500              SNP   
...              ...           ...       ...      ...              ...   
798945  2-Transition  0-AllVolumes         0  1000000              SNS   
798946  2-Transition  0-AllVolumes         0  1000000              SNS   
798947  2-Transition  0-AllVolumes         0  1000000              SNS   
798948  2-Transition  0-AllVolumes         0  1000000              SNS   
798949  2-Transition  0-AllVolumes         0  1000000              SNS   

        SeasonGroup  SeasonFactor AvgSsnPrdVol  
19          M01-Jan         0.815         1026  
20          M02-Feb         0.862         1086  
21          M03-Mar         0.949         1195  
22          M04-Apr         1.023         1288  
23          M05-May         1.079         1359  
...             ...           ...          ...  
798945      S03-Sum         1.057         1554  
798946      S04-Fal         1.022         1502  
798947     MaxMonth         1.067         1569  
798948    MaxSeason         1.057         1554  
798949      S00-Ann         1.000         1470  

[780330 rows x 29 columns]

In [59]:
#add dow factor

dfs_PrdForecasts_Season_DOW = []

#for (idx, row) in dfs_PrdForecasts.iterrows():

for df_PrdForecasts_Season in dfs_PrdForecasts_Season: 
    
    #joing forecasts data with season factors
    df_PrdForecasts_Season_DOW = pd.DataFrame.merge(df_PrdForecasts_Season,df_DOWFactors,on=('DOWFACFC',nameFG,nameAT),how='left')
    
    #calculate Average Season DOW
    df_PrdForecasts_Season_DOW['AvgSsnDOWPrdVol'] = df_PrdForecasts_Season_DOW['AvgSsnPrdVol'] * df_PrdForecasts_Season_DOW['DOWFactor'] 
    df_PrdForecasts_Season_DOW['AvgSsnDOWPrdVol'] = df_PrdForecasts_Season_DOW['AvgSsnDOWPrdVol'].astype(int)

    display(df_PrdForecasts_Season_DOW)
    
    dfs_PrdForecasts_Season_DOW.append(df_PrdForecasts_Season_DOW)

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0        0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
1        0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
2        0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
3        0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
4        0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0   2.0   
...             ...       ...           ...       ...    ...  ..    ...   ...   
6357775   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
6357776   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
6357777   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
6357778   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   
6357779   WFRC_8218       3.0       28631.8   CD Road    1.0  D2    1.0  31.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        8.0   
1           Principal Arterial        1065  0.6000  DY  1.0000        8.0   
2           Principal Arterial        1065  0.6000  DY  1.0000        8.0   
3           Principal Arterial        1065  0.6000  DY  1.0000        8.0   
4           Principal Arterial        1065  0.6000  DY  1.0000        8.0   
...                            ...     ...     ...  ..     ...        ...   
6357775           Freeway             1473  0.5447  EV  0.2324       13.8   
6357776           Freeway             1473  0.5447  EV  0.2324       13.8   
6357777           Freeway             1473  0.5447  EV  0.2324       13.8   
6357778           Freeway             1473  0.5447  EV  0.2324       13.8   
6357779           Freeway             1473  0.5447  EV  0.2324       13.8   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              6.0   2019             0                0          0.00000   
1              6.0   2019             0                0          0.00000   
2              6.0   2019             0                0          0.00000   
3              6.0   2019             0                0          0.00000   
4              6.0   2019             0                0          0.00000   
...            ...    ...           ...              ...              ...   
6357775        7.1   2019         25500            25500       3228.00114   
6357776        7.1   2019         25500            25500       3228.00114   
6357777        7.1   2019         25500            25500       3228.00114   
6357778        7.1   2019         25500            25500       3228.00114   
6357779        7.1   2019         25500            25500       3228.00114   

            DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  \
0           Arterial  StatewideArterial         1-Rural    UTRuralLow   
1           Arterial  StatewideArterial         1-Rural    UTRuralLow   
2           Arterial  StatewideArterial         1-Rural    UTRuralLow   
3           Arterial  StatewideArterial         1-Rural    UTRuralLow   
4           Arterial  StatewideArterial         1-Rural    UTRuralLow   
...              ...                ...             ...           ...   
6357775  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6357776  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6357777  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6357778  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6357779  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   

         Vol_From   Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  \
0               0     2500             SNP     M01-Jan         0.815   
1               0     2500             SNP     M01-Jan         0.815   
2               0     2500             SNP     M01-Jan         0.815   
3               0     2500

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0        0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
1        0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
2        0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
3        0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
4        0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0   2.0   
...             ...       ...           ...       ...    ...  ..    ...   ...   
6460375   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
6460376   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
6460377   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
6460378   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   
6460379   WFRC_8218       3.0       31030.8   CD Road    1.0  D2    1.0  31.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY   1.000        7.6   
1           Principal Arterial        1065  0.6000  DY   1.000        7.6   
2           Principal Arterial        1065  0.6000  DY   1.000        7.6   
3           Principal Arterial        1065  0.6000  DY   1.000        7.6   
4           Principal Arterial        1065  0.6000  DY   1.000        7.6   
...                            ...     ...     ...  ..     ...        ...   
6460375           Freeway             1473  0.5202  EV   0.232       15.0   
6460376           Freeway             1473  0.5202  EV   0.232       15.0   
6460377           Freeway             1473  0.5202  EV   0.232       15.0   
6460378           Freeway             1473  0.5202  EV   0.232       15.0   
6460379           Freeway             1473  0.5202  EV   0.232       15.0   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              6.2   2024             0                0            0.000   
1              6.2   2024             0                0            0.000   
2              6.2   2024             0                0            0.000   
3              6.2   2024             0                0            0.000   
4              6.2   2024             0                0            0.000   
...            ...    ...           ...              ...              ...   
6460375        7.6   2024         27500            27500         3318.876   
6460376        7.6   2024         27500            27500         3318.876   
6460377        7.6   2024         27500            27500         3318.876   
6460378        7.6   2024         27500            27500         3318.876   
6460379        7.6   2024         27500            27500         3318.876   

            DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  \
0           Arterial  StatewideArterial         1-Rural    UTRuralLow   
1           Arterial  StatewideArterial         1-Rural    UTRuralLow   
2           Arterial  StatewideArterial         1-Rural    UTRuralLow   
3           Arterial  StatewideArterial         1-Rural    UTRuralLow   
4           Arterial  StatewideArterial         1-Rural    UTRuralLow   
...              ...                ...             ...           ...   
6460375  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460376  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460377  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460378  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460379  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   

         Vol_From   Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  \
0               0     2500             SNP     M01-Jan         0.815   
1               0     2500             SNP     M01-Jan         0.815   
2               0     2500             SNP     M01-Jan         0.815   
3               0     2500

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
6651895   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
6651896   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
6651897   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
6651898   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   
6651899   WFRC_8219       2.0        4713.8  Arterial    1.0  D2    1.0  3.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
...                            ...     ...     ...  ..     ...        ...   
6651895       Minor Arterial           939  0.4894  EV  0.2318        9.5   
6651896       Minor Arterial           939  0.4894  EV  0.2318        9.5   
6651897       Minor Arterial           939  0.4894  EV  0.2318        9.5   
6651898       Minor Arterial           939  0.4894  EV  0.2318        9.5   
6651899       Minor Arterial           939  0.4894  EV  0.2318        9.5   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              5.9   2030             0                0         0.000000   
1              5.9   2030             0                0         0.000000   
2              5.9   2030             0                0         0.000000   
3              5.9   2030             0                0         0.000000   
4              5.9   2030             0                0         0.000000   
...            ...    ...           ...              ...              ...   
6651895        5.7   2030          6200             6200       703.346104   
6651896        5.7   2030          6200             6200       703.346104   
6651897        5.7   2030          6200             6200       703.346104   
6651898        5.7   2030          6200             6200       703.346104   
6651899        5.7   2030          6200             6200       703.346104   

         DOWFACFC             SsnGrp    SsnATGroup     SsnVolCls  Vol_From  \
0        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
1        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
2        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
3        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
4        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
...           ...                ...           ...           ...       ...   
6651895  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6651896  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6651897  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6651898  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6651899  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   

          Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0           2500             SNP     M01-Jan         0.815             0   
1           2500             SNP     M01-Jan         0.815             0   
2           2500             SNP     M

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
6828025   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
6828026   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
6828027   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
6828028   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   
6828029   WFRC_8219       2.0        4935.3  Arterial    1.0  D2    1.0  3.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
...                            ...     ...     ...  ..     ...        ...   
6828025       Minor Arterial           939  0.4927  EV  0.2375       10.4   
6828026       Minor Arterial           939  0.4927  EV  0.2375       10.4   
6828027       Minor Arterial           939  0.4927  EV  0.2375       10.4   
6828028       Minor Arterial           939  0.4927  EV  0.2375       10.4   
6828029       Minor Arterial           939  0.4927  EV  0.2375       10.4   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              5.9   2040             0                0            0.000   
1              5.9   2040             0                0            0.000   
2              5.9   2040             0                0            0.000   
3              5.9   2040             0                0            0.000   
4              5.9   2040             0                0            0.000   
...            ...    ...           ...              ...              ...   
6828025        6.1   2040          6400             6400          748.904   
6828026        6.1   2040          6400             6400          748.904   
6828027        6.1   2040          6400             6400          748.904   
6828028        6.1   2040          6400             6400          748.904   
6828029        6.1   2040          6400             6400          748.904   

         DOWFACFC             SsnGrp    SsnATGroup     SsnVolCls  Vol_From  \
0        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
1        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
2        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
3        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
4        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
...           ...                ...           ...           ...       ...   
6828025  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6828026  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6828027  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6828028  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6828029  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   

          Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0           2500             SNP     M01-Jan         0.815             0   
1           2500             SNP     M01-Jan         0.815             0   
2           2500             SNP     M

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
7017835   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
7017836   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
7017837   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
7017838   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   
7017839   WFRC_8219       2.0       13113.3  Arterial    1.0  D2    1.0  3.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
...                            ...     ...     ...  ..     ...        ...   
7017835       Minor Arterial           939  0.5083  EV  0.1864       15.8   
7017836       Minor Arterial           939  0.5083  EV  0.1864       15.8   
7017837       Minor Arterial           939  0.5083  EV  0.1864       15.8   
7017838       Minor Arterial           939  0.5083  EV  0.1864       15.8   
7017839       Minor Arterial           939  0.5083  EV  0.1864       15.8   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              5.9   2050          2100             2100       1260.00000   
1              5.9   2050          2100             2100       1260.00000   
2              5.9   2050          2100             2100       1260.00000   
3              5.9   2050          2100             2100       1260.00000   
4              5.9   2050          2100             2100       1260.00000   
...            ...    ...           ...              ...              ...   
7017835        7.5   2050         13500            13500       1279.08612   
7017836        7.5   2050         13500            13500       1279.08612   
7017837        7.5   2050         13500            13500       1279.08612   
7017838        7.5   2050         13500            13500       1279.08612   
7017839        7.5   2050         13500            13500       1279.08612   

         DOWFACFC             SsnGrp    SsnATGroup     SsnVolCls  Vol_From  \
0        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
1        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
2        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
3        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
4        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
...           ...                ...           ...           ...       ...   
7017835  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7017836  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7017837  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7017838  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7017839  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   

          Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0           2500             SNP     M01-Jan         0.815          1026   
1           2500             SNP     M01-Jan         0.815          1026   
2           2500             SNP     M

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0        0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
1        0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
2        0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
3        0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
4        0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0   2.0   
...             ...       ...           ...       ...    ...  ..    ...   ...   
6460375   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
6460376   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
6460377   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
6460378   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   
6460379   WFRC_8218       3.0       38507.2   CD Road    1.0  D2    1.0  31.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
...                            ...     ...     ...  ..     ...        ...   
6460375           Freeway             1473  0.5189  EV  0.2358       15.0   
6460376           Freeway             1473  0.5189  EV  0.2358       15.0   
6460377           Freeway             1473  0.5189  EV  0.2358       15.0   
6460378           Freeway             1473  0.5189  EV  0.2358       15.0   
6460379           Freeway             1473  0.5189  EV  0.2358       15.0   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              6.1   2040             0                0          0.00000   
1              6.1   2040             0                0          0.00000   
2              6.1   2040             0                0          0.00000   
3              6.1   2040             0                0          0.00000   
4              6.1   2040             0                0          0.00000   
...            ...    ...           ...              ...              ...   
6460375        7.9   2040         33500            34500       4221.30339   
6460376        7.9   2040         33500            34500       4221.30339   
6460377        7.9   2040         33500            34500       4221.30339   
6460378        7.9   2040         33500            34500       4221.30339   
6460379        7.9   2040         33500            34500       4221.30339   

            DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  \
0           Arterial  StatewideArterial         1-Rural    UTRuralLow   
1           Arterial  StatewideArterial         1-Rural    UTRuralLow   
2           Arterial  StatewideArterial         1-Rural    UTRuralLow   
3           Arterial  StatewideArterial         1-Rural    UTRuralLow   
4           Arterial  StatewideArterial         1-Rural    UTRuralLow   
...              ...                ...             ...           ...   
6460375  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460376  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460377  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460378  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460379  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   

         Vol_From   Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  \
0               0     2500             SNP     M01-Jan         0.815   
1               0     2500             SNP     M01-Jan         0.815   
2               0     2500             SNP     M01-Jan         0.815   
3               0     2500

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES    FT  \
0        0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
1        0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
2        0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
3        0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
4        0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0   2.0   
...             ...       ...           ...       ...    ...  ..    ...   ...   
6460375   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
6460376   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
6460377   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
6460378   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   
6460379   WFRC_8218       3.0       42469.0   CD Road    1.0  D2    1.0  31.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
...                            ...     ...     ...  ..     ...        ...   
6460375           Freeway             1473  0.5178  EV  0.2427       14.9   
6460376           Freeway             1473  0.5178  EV  0.2427       14.9   
6460377           Freeway             1473  0.5178  EV  0.2427       14.9   
6460378           Freeway             1473  0.5178  EV  0.2427       14.9   
6460379           Freeway             1473  0.5178  EV  0.2427       14.9   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              6.0   2050          2100             2100       1260.00000   
1              6.0   2050          2100             2100       1260.00000   
2              6.0   2050          2100             2100       1260.00000   
3              6.0   2050          2100             2100       1260.00000   
4              6.0   2050          2100             2100       1260.00000   
...            ...    ...           ...              ...              ...   
6460375        7.9   2050         37500            37500       4712.62725   
6460376        7.9   2050         37500            37500       4712.62725   
6460377        7.9   2050         37500            37500       4712.62725   
6460378        7.9   2050         37500            37500       4712.62725   
6460379        7.9   2050         37500            37500       4712.62725   

            DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  \
0           Arterial  StatewideArterial         1-Rural    UTRuralLow   
1           Arterial  StatewideArterial         1-Rural    UTRuralLow   
2           Arterial  StatewideArterial         1-Rural    UTRuralLow   
3           Arterial  StatewideArterial         1-Rural    UTRuralLow   
4           Arterial  StatewideArterial         1-Rural    UTRuralLow   
...              ...                ...             ...           ...   
6460375  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460376  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460377  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460378  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   
6460379  FreewayI215        FreewayI215  0-AllAreaTypes  0-AllVolumes   

         Vol_From   Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  \
0               0     2500             SNP     M01-Jan         0.815   
1               0     2500             SNP     M01-Jan         0.815   
2               0     2500             SNP     M01-Jan         0.815   
3               0     2500

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
6663865   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
6663866   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
6663867   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
6663868   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   
6663869   WFRC_8219       2.0        4519.2  Arterial    1.0  D2    1.0  3.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.7   
...                            ...     ...     ...  ..     ...        ...   
6663865       Minor Arterial           939  0.4893  EV  0.2431        9.6   
6663866       Minor Arterial           939  0.4893  EV  0.2431        9.6   
6663867       Minor Arterial           939  0.4893  EV  0.2431        9.6   
6663868       Minor Arterial           939  0.4893  EV  0.2431        9.6   
6663869       Minor Arterial           939  0.4893  EV  0.2431        9.6   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              5.9   2030             0                0          0.00000   
1              5.9   2030             0                0          0.00000   
2              5.9   2030             0                0          0.00000   
3              5.9   2030             0                0          0.00000   
4              5.9   2030             0                0          0.00000   
...            ...    ...           ...              ...              ...   
6663865        5.9   2030          6200             6000        713.69298   
6663866        5.9   2030          6200             6000        713.69298   
6663867        5.9   2030          6200             6000        713.69298   
6663868        5.9   2030          6200             6000        713.69298   
6663869        5.9   2030          6200             6000        713.69298   

         DOWFACFC             SsnGrp    SsnATGroup     SsnVolCls  Vol_From  \
0        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
1        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
2        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
3        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
4        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
...           ...                ...           ...           ...       ...   
6663865  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6663866  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6663867  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6663868  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6663869  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   

          Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0           2500             SNP     M01-Jan         0.815             0   
1           2500             SNP     M01-Jan         0.815             0   
2           2500             SNP     M

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
6850255   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
6850256   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
6850257   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
6850258   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   
6850259   WFRC_8219       2.0        4955.3  Arterial    1.0  D2    1.0  3.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
...                            ...     ...     ...  ..     ...        ...   
6850255       Minor Arterial           939  0.4949  EV  0.2391       10.2   
6850256       Minor Arterial           939  0.4949  EV  0.2391       10.2   
6850257       Minor Arterial           939  0.4949  EV  0.2391       10.2   
6850258       Minor Arterial           939  0.4949  EV  0.2391       10.2   
6850259       Minor Arterial           939  0.4949  EV  0.2391       10.2   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              5.9   2040             0                0         0.000000   
1              5.9   2040             0                0         0.000000   
2              5.9   2040             0                0         0.000000   
3              5.9   2040             0                0         0.000000   
4              5.9   2040             0                0         0.000000   
...            ...    ...           ...              ...              ...   
6850255        5.4   2040          6400             6400       757.315776   
6850256        5.4   2040          6400             6400       757.315776   
6850257        5.4   2040          6400             6400       757.315776   
6850258        5.4   2040          6400             6400       757.315776   
6850259        5.4   2040          6400             6400       757.315776   

         DOWFACFC             SsnGrp    SsnATGroup     SsnVolCls  Vol_From  \
0        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
1        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
2        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
3        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
4        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
...           ...                ...           ...           ...       ...   
6850255  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6850256  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6850257  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6850258  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
6850259  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   

          Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0           2500             SNP     M01-Jan         0.815             0   
1           2500             SNP     M01-Jan         0.815             0   
2           2500             SNP     M

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0        0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
1        0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
2        0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
3        0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
4        0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
...             ...       ...           ...       ...    ...  ..    ...  ...   
7022965   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
7022966   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
7022967   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
7022968   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   
7022969   WFRC_8219       2.0       13363.9  Arterial    1.0  D2    1.0  3.0   

                           FTCLASS  CAP1HL    DFAC Prd  PRDFAC  MDPERCENT  \
0           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
1           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
2           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
3           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
4           Principal Arterial        1065  0.6000  DY  1.0000        7.9   
...                            ...     ...     ...  ..     ...        ...   
7022965       Minor Arterial           939  0.5164  EV  0.2034       15.4   
7022966       Minor Arterial           939  0.5164  EV  0.2034       15.4   
7022967       Minor Arterial           939  0.5164  EV  0.2034       15.4   
7022968       Minor Arterial           939  0.5164  EV  0.2034       15.4   
7022969       Minor Arterial           939  0.5164  EV  0.2034       15.4   

         HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0              5.9   2050          2100             2100       1260.00000   
1              5.9   2050          2100             2100       1260.00000   
2              5.9   2050          2100             2100       1260.00000   
3              5.9   2050          2100             2100       1260.00000   
4              5.9   2050          2100             2100       1260.00000   
...            ...    ...           ...              ...              ...   
7022965        7.0   2050         13500            14000       1470.50064   
7022966        7.0   2050         13500            14000       1470.50064   
7022967        7.0   2050         13500            14000       1470.50064   
7022968        7.0   2050         13500            14000       1470.50064   
7022969        7.0   2050         13500            14000       1470.50064   

         DOWFACFC             SsnGrp    SsnATGroup     SsnVolCls  Vol_From  \
0        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
1        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
2        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
3        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
4        Arterial  StatewideArterial       1-Rural    UTRuralLow         0   
...           ...                ...           ...           ...       ...   
7022965  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7022966  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7022967  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7022968  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   
7022969  Arterial  StatewideArterial  2-Transition  0-AllVolumes         0   

          Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0           2500             SNP     M01-Jan         0.815          1026   
1           2500             SNP     M01-Jan         0.815          1026   
2           2500             SNP     M

In [60]:
#add tod factor

dfs_PrdForecasts_Season_DOW_TOD_wGroups = []

for df_PrdForecasts_Season_DOW in dfs_PrdForecasts_Season_DOW: 
    
    df_PrdForecasts_Season_DOW = df_PrdForecasts_Season_DOW.rename(columns={namePrd: namePrd + '_TDM'})
    #joing forecasts data with season factors
    
    df_TODFactors_Prd = df_TODFactors[df_TODFactors['HrPctOf'] == 'Prd']
    df_TODFactors_DY  = df_TODFactors[df_TODFactors['HrPctOf'] == 'DY']
    
    #get peak Hr as a Pct of Prd
    df_PrdForecasts_Season_DOW_TOD_Prd = pd.DataFrame.merge(df_PrdForecasts_Season_DOW,df_TODFactors_Prd,left_on=('SiteGroupSeason','SeasonGroup','DOWGroup',namePrd+'_TDM'),right_on=('SiteGroupSeason','SeasonGroup','DOWGroup',namePrd))
    
    #get peak Hr as a Pct of DY
    df_PrdForecasts_Season_DOW_TOD_DY = pd.DataFrame.merge(df_PrdForecasts_Season_DOW,df_TODFactors_DY,left_on=('SiteGroupSeason','SeasonGroup','DOWGroup',namePrd+'_TDM'),right_on=('SiteGroupSeason','SeasonGroup','DOWGroup','HrPctOf'))
 
    df_PrdForecasts_Season_DOW_TOD = pd.concat([df_PrdForecasts_Season_DOW_TOD_Prd, df_PrdForecasts_Season_DOW_TOD_DY])

    #display(df_PrdForecasts_Season_DOW_TOD)
    
    #filter by vc groups
    df_PrdForecasts_Season_DOW_TOD_wGroups = pd.DataFrame.merge(df_PrdForecasts_Season_DOW_TOD,df_VCGroups,on=('SeasonGroup','DOWGroup','HrPctOf','Prd'))
    
    dfs_PrdForecasts_Season_DOW_TOD_wGroups.append(df_PrdForecasts_Season_DOW_TOD_wGroups)
    
    display(df_PrdForecasts_Season_DOW_TOD_wGroups)


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1392.3  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1510.9  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1510.9  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1717.9  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
758467  1084_001.0       1.0         914.1  Arterial    1.0  D2    1.0  5.0   
758468  2865_001.3       2.0        2329.2  Arterial    1.0  D1    1.0  4.0   
758469  2865_001.3       2.0        2329.2  Arterial    1.0  D2    1.0  4.0   
758470  3004_000.9       2.0         222.1  Arterial    1.0  D1    1.0  4.0   
758471  3004_000.9       2.0         222.1  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5004      AM  0.1829        6.3   
1          Principal Arterial        1065  0.4996      AM  0.1829        6.4   
2          Principal Arterial        1065  0.5384      AM  0.1612       17.6   
3          Principal Arterial        1065  0.4616      AM  0.1612       20.2   
4          Principal Arterial        1065  0.5654      AM  0.1599       16.1   
...                           ...     ...     ...     ...     ...        ...   
758467          Collector             572  0.6000      DY  1.0000       21.6   
758468          Collector             785  0.6000      DY  1.0000        1.6   
758469          Collector             785  0.6000      DY  1.0000        1.6   
758470          Collector             785  0.6000      DY  1.0000        7.0   
758471          Collector             785  0.6000      DY  1.0000        7.4   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.5   2019             0                0              0.0   
1             4.5   2019             0                0              0.0   
2            14.6   2019             0                0              0.0   
3            16.9   2019             0                0              0.0   
4            13.2   2019             0                0              0.0   
...           ...    ...           ...              ...              ...   
758467       16.2   2019           350              350            210.0   
758468        1.3   2019             0                0              0.0   
758469        1.3   2019             0                0              0.0   
758470        3.7   2019             0                0              0.0   
758471        3.9   2019             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
758467  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758468  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758469  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758470  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758471  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1465.9  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1632.9  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1632.9  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1848.0  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
770707  1084_001.0       1.0         884.1  Arterial    1.0  D2    1.0  5.0   
770708  2865_001.3       2.0        2523.7  Arterial    1.0  D1    1.0  4.0   
770709  2865_001.3       2.0        2523.7  Arterial    1.0  D2    1.0  4.0   
770710  3004_000.9       2.0         552.4  Arterial    1.0  D1    1.0  4.0   
770711  3004_000.9       2.0         552.4  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4747      AM  0.1810        6.7   
1          Principal Arterial        1065  0.5253      AM  0.1810        6.1   
2          Principal Arterial        1065  0.5415      AM  0.1623       17.9   
3          Principal Arterial        1065  0.4585      AM  0.1623       20.4   
4          Principal Arterial        1065  0.5675      AM  0.1617       16.4   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       24.2   
770708          Collector             785  0.6000      DY  1.0000        1.7   
770709          Collector             785  0.6000      DY  1.0000        1.7   
770710          Collector             785  0.6000      DY  1.0000        9.6   
770711          Collector             785  0.6000      DY  1.0000       10.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.9   2024             0                0              0.0   
1             4.4   2024             0                0              0.0   
2            14.4   2024             0                0              0.0   
3            16.8   2024             0                0              0.0   
4            13.0   2024             0                0              0.0   
...           ...    ...           ...              ...              ...   
770707       18.3   2024           400              400            240.0   
770708        1.4   2024             0                0              0.0   
770709        1.4   2024             0                0              0.0   
770710        8.4   2024             0                0              0.0   
770711        8.7   2024             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1559.1  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1755.5  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1755.5  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1970.6  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
793555  1084_001.0       1.0         779.7  Arterial    1.0  D2    1.0  5.0   
793556  2865_001.3       2.0        2781.7  Arterial    1.0  D1    1.0  4.0   
793557  2865_001.3       2.0        2781.7  Arterial    1.0  D2    1.0  4.0   
793558  3004_000.9       2.0        2345.6  Arterial    1.0  D1    1.0  3.0   
793559  3004_000.9       2.0        2345.6  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4952      AM  0.1844        6.3   
1          Principal Arterial        1065  0.5048      AM  0.1844        6.2   
2          Principal Arterial        1065  0.4966      AM  0.1660       18.0   
3          Principal Arterial        1065  0.5034      AM  0.1660       17.7   
4          Principal Arterial        1065  0.5233      AM  0.1645       16.6   
...                           ...     ...     ...     ...     ...        ...   
793555          Collector             572  0.6000      DY  1.0000       26.3   
793556          Collector             785  0.6000      DY  1.0000        1.7   
793557          Collector             785  0.6000      DY  1.0000        1.7   
793558       Minor Arterial           939  0.6000      DY  1.0000        7.6   
793559       Minor Arterial           939  0.6000      DY  1.0000        8.5   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.6   2030             0                0              0.0   
1             4.5   2030             0                0              0.0   
2            14.3   2030             0                0              0.0   
3            14.2   2030             0                0              0.0   
4            13.2   2030             0                0              0.0   
...           ...    ...           ...              ...              ...   
793555       20.7   2030           500              500            300.0   
793556        1.3   2030             0                0              0.0   
793557        1.4   2030             0                0              0.0   
793558        3.5   2030             0                0              0.0   
793559        3.9   2030             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
793555  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793556  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793557  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793558  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793559  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1684.9  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        2230.4  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        2230.4  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        2456.4  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
814567  1084_001.0       1.0         892.6  Arterial    1.0  D2    1.0  5.0   
814568  2865_001.3       2.0        3188.5  Arterial    1.0  D1    1.0  4.0   
814569  2865_001.3       2.0        3188.5  Arterial    1.0  D2    1.0  4.0   
814570  3004_000.9       3.0        3966.8  Arterial    1.0  D1    1.0  3.0   
814571  3004_000.9       3.0        3966.8  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5225      AM  0.1855        5.9   
1          Principal Arterial        1065  0.4775      AM  0.1855        6.5   
2          Principal Arterial        1065  0.4736      AM  0.1615       18.1   
3          Principal Arterial        1065  0.5264      AM  0.1615       16.1   
4          Principal Arterial        1065  0.4974      AM  0.1598       16.9   
...                           ...     ...     ...     ...     ...        ...   
814567          Collector             572  0.6000      DY  1.0000       29.0   
814568          Collector             785  0.6000      DY  1.0000        1.8   
814569          Collector             785  0.6000      DY  1.0000        1.8   
814570       Minor Arterial           894  0.6000      DY  1.0000        9.5   
814571       Minor Arterial           894  0.6000      DY  1.0000        9.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.4   2040             0                0              0.0   
1             4.8   2040             0                0              0.0   
2            15.1   2040             0                0              0.0   
3            13.7   2040             0                0              0.0   
4            14.2   2040             0                0              0.0   
...           ...    ...           ...              ...              ...   
814567       29.3   2040           700              700            420.0   
814568        1.5   2040             0                0              0.0   
814569        1.5   2040             0                0              0.0   
814570        3.8   2040             0                0              0.0   
814571        4.1   2040             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
814567  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814568  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814569  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814570  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814571  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1811.9  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0         884.2  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0         884.2  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0         840.3  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837211  1084_001.0       1.0         647.5  Arterial    1.0  D2    1.0  5.0   
837212  2865_001.3       2.0        3583.6  Arterial    1.0  D1    1.0  4.0   
837213  2865_001.3       2.0        3583.6  Arterial    1.0  D2    1.0  4.0   
837214  3004_000.9       3.0       16315.5  Arterial    1.0  D1    1.0  3.0   
837215  3004_000.9       3.0       16315.5  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5715      AM  0.1879        5.4   
1          Principal Arterial        1065  0.4285      AM  0.1879        7.2   
2            Minor Arterial           983  0.5076      AM  0.1408       23.1   
3            Minor Arterial           983  0.4924      AM  0.1408       21.4   
4            Minor Arterial           983  0.5134      AM  0.1419       23.0   
...                           ...     ...     ...     ...     ...        ...   
837211          Collector             572  0.6000      DY  1.0000       20.5   
837212          Collector             785  0.6000      DY  1.0000        1.7   
837213          Collector             785  0.6000      DY  1.0000        1.7   
837214       Minor Arterial           894  0.6000      DY  1.0000       16.1   
837215       Minor Arterial           894  0.6000      DY  1.0000       13.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.0   2050          2100             2100       225.508185   
1             5.3   2050          2100             2100       169.081815   
2            35.6   2050          1200             1200        85.764096   
3            33.9   2050          1200             1200        83.195904   
4            35.5   2050          1500             1500       109.277190   
...           ...    ...           ...              ...              ...   
837211       19.6   2050           800              800       480.000000   
837212        1.6   2050          3800             3800      2280.000000   
837213        1.6   2050          3800             3800      2280.000000   
837214        6.5   2050         35500            35500     21300.000000   
837215        5.3   2050         35500            35500     21300.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837211  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837212  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837213  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837214  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837215  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           183   
1          2500             SNP     M01-Jan         0.815           137   
2          2500 

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1669.8  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        3098.9  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        3098.9  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        3352.3  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
770707  1084_001.0       1.0         875.9  Arterial    1.0  D2    1.0  5.0   
770708  2865_001.3       2.0        3159.1  Arterial    1.0  D1    1.0  4.0   
770709  2865_001.3       2.0        3159.1  Arterial    1.0  D2    1.0  4.0   
770710  3004_000.9       3.0         716.8  Arterial    1.0  D1    1.0  4.0   
770711  3004_000.9       3.0         716.8  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4754      AM  0.1817        6.9   
1          Principal Arterial        1065  0.5246      AM  0.1817        6.2   
2          Principal Arterial        1065  0.7235      AM  0.1945       10.9   
3          Principal Arterial        1065  0.2765      AM  0.1945       22.6   
4          Principal Arterial        1065  0.7256      AM  0.1916       10.8   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       28.6   
770708          Collector             785  0.6000      DY  1.0000        2.0   
770709          Collector             785  0.6000      DY  1.0000        2.0   
770710          Collector             748  0.6000      DY  1.0000        7.6   
770711          Collector             748  0.6000      DY  1.0000        8.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             5.0   2040             0                0         0.000000   
1             4.5   2040             0                0         0.000000   
2             7.8   2040             0              850       119.612638   
3            17.9   2040             0              850        45.712363   
4             7.8   2040             0              900       125.122464   
...           ...    ...           ...              ...              ...   
770707       26.6   2040           700              700       420.000000   
770708        1.3   2040             0                0         0.000000   
770709        1.3   2040             0                0         0.000000   
770710        3.9   2040             0                0         0.000000   
770711        4.1   2040             0                0         0.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1795.1  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0        3898.2  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0        3898.2  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0        3907.8  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
770707  1084_001.0       1.0         744.6  Arterial    1.0  D2    1.0  5.0   
770708  2865_001.3       2.0        3543.9  Arterial    1.0  D1    1.0  4.0   
770709  2865_001.3       2.0        3543.9  Arterial    1.0  D2    1.0  4.0   
770710  3004_000.9       3.0         778.5  Arterial    1.0  D1    1.0  4.0   
770711  3004_000.9       3.0         778.5  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4772      AM  0.1823        6.8   
1          Principal Arterial        1065  0.5228      AM  0.1823        6.2   
2            Minor Arterial           983  0.7239      AM  0.1981       14.4   
3            Minor Arterial           983  0.2761      AM  0.1981       22.2   
4            Minor Arterial           983  0.7258      AM  0.1978       14.3   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       22.7   
770708          Collector             785  0.6000      DY  1.0000        1.9   
770709          Collector             785  0.6000      DY  1.0000        1.9   
770710          Collector             748  0.6000      DY  1.0000        7.7   
770711          Collector             748  0.6000      DY  1.0000        7.7   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.9   2050          2100             2100       182.686476   
1             4.5   2050          2100             2100       200.143524   
2            15.4   2050          1200             4200       602.299278   
3            29.0   2050          1200             4200       229.720722   
4            15.3   2050          1500             4600       660.390904   
...           ...    ...           ...              ...              ...   
770707       19.6   2050           800              900       540.000000   
770708        1.5   2050          3800             3800      2280.000000   
770709        1.5   2050          3800             3800      2280.000000   
770710        3.6   2050         35500            20000     12000.000000   
770711        3.7   2050         35500            20000     12000.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           148   
1          2500             SNP     M01-Jan         0.815           163   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1559.2  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1757.1  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1757.1  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1971.4  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
794983  1084_001.0       1.0         815.4  Arterial    1.0  D2    1.0  5.0   
794984  2865_001.3       2.0        2783.7  Arterial    1.0  D1    1.0  4.0   
794985  2865_001.3       2.0        2783.7  Arterial    1.0  D2    1.0  4.0   
794986  3004_000.9       2.0        2312.0  Arterial    1.0  D1    1.0  3.0   
794987  3004_000.9       2.0        2312.0  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4957      AM  0.1845        6.3   
1          Principal Arterial        1065  0.5043      AM  0.1845        6.2   
2          Principal Arterial        1065  0.4973      AM  0.1661       17.9   
3          Principal Arterial        1065  0.5027      AM  0.1661       17.7   
4          Principal Arterial        1065  0.5234      AM  0.1645       16.5   
...                           ...     ...     ...     ...     ...        ...   
794983          Collector             572  0.6000      DY  1.0000       26.2   
794984          Collector             785  0.6000      DY  1.0000        1.7   
794985          Collector             785  0.6000      DY  1.0000        1.7   
794986       Minor Arterial           939  0.6000      DY  1.0000        7.6   
794987       Minor Arterial           939  0.6000      DY  1.0000        8.6   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.6   2030             0                0              0.0   
1             4.5   2030             0                0              0.0   
2            14.3   2030             0                0              0.0   
3            14.2   2030             0                0              0.0   
4            13.2   2030             0                0              0.0   
...           ...    ...           ...              ...              ...   
794983       20.5   2030           500              550            330.0   
794984        1.3   2030             0                0              0.0   
794985        1.4   2030             0                0              0.0   
794986        3.5   2030             0                0              0.0   
794987        3.8   2030             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
794983  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794984  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794985  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794986  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794987  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1686.0  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        2111.0  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        2111.0  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        2340.3  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
817219  1084_001.0       1.0         921.9  Arterial    1.0  D2    1.0  5.0   
817220  2865_001.3       2.0        3192.3  Arterial    1.0  D1    1.0  4.0   
817221  2865_001.3       2.0        3192.3  Arterial    1.0  D2    1.0  4.0   
817222  3004_000.9       3.0        5104.6  Arterial    1.0  D1    1.0  3.0   
817223  3004_000.9       3.0        5104.6  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5228      AM  0.1855        5.9   
1          Principal Arterial        1065  0.4772      AM  0.1855        6.5   
2          Principal Arterial        1065  0.4810      AM  0.1643       18.0   
3          Principal Arterial        1065  0.5190      AM  0.1643       16.5   
4          Principal Arterial        1065  0.5058      AM  0.1627       16.7   
...                           ...     ...     ...     ...     ...        ...   
817219          Collector             572  0.6000      DY  1.0000       29.1   
817220          Collector             785  0.6000      DY  1.0000        1.8   
817221          Collector             785  0.6000      DY  1.0000        1.8   
817222       Minor Arterial           894  0.6000      DY  1.0000       11.0   
817223       Minor Arterial           894  0.6000      DY  1.0000        9.2   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.4   2040             0                0              0.0   
1             4.8   2040             0                0              0.0   
2            15.3   2040             0                0              0.0   
3            14.2   2040             0                0              0.0   
4            14.3   2040             0                0              0.0   
...           ...    ...           ...              ...              ...   
817219       30.4   2040           700              750            450.0   
817220        1.5   2040             0                0              0.0   
817221        1.5   2040             0                0              0.0   
817222        4.8   2040             0             1100            660.0   
817223        3.9   2040             0             1100            660.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
817219  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817220  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817221  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817222  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817223  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1813.3  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0         870.4  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0         870.4  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0         837.8  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837823  1084_001.0       1.0         572.5  Arterial    1.0  D2    1.0  5.0   
837824  2865_001.3       2.0        3583.6  Arterial    1.0  D1    1.0  4.0   
837825  2865_001.3       2.0        3583.6  Arterial    1.0  D2    1.0  4.0   
837826  3004_000.9       3.0        8477.5  Arterial    1.0  D1    1.0  3.0   
837827  3004_000.9       3.0        8477.5  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5723      AM  0.1884        5.4   
1          Principal Arterial        1065  0.4277      AM  0.1884        7.2   
2            Minor Arterial           983  0.5086      AM  0.1410       23.1   
3            Minor Arterial           983  0.4914      AM  0.1410       21.4   
4            Minor Arterial           983  0.5152      AM  0.1416       22.9   
...                           ...     ...     ...     ...     ...        ...   
837823          Collector             572  0.6000      DY  1.0000       19.4   
837824          Collector             785  0.6000      DY  1.0000        1.7   
837825          Collector             785  0.6000      DY  1.0000        1.7   
837826       Minor Arterial           894  0.6000      DY  1.0000        9.4   
837827       Minor Arterial           894  0.6000      DY  1.0000        6.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             3.9   2050          2100             2100       226.424772   
1             5.3   2050          2100             2100       169.215228   
2            35.6   2050          1200             1200        86.055120   
3            34.2   2050          1200             1200        83.144880   
4            35.2   2050          1500             1500       109.428480   
...           ...    ...           ...              ...              ...   
837823       19.3   2050           800              700       420.000000   
837824        1.6   2050          3800             3800      2280.000000   
837825        1.6   2050          3800             3800      2280.000000   
837826        4.3   2050         35500            27500     16500.000000   
837827        3.0   2050         35500            27500     16500.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837823  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837824  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837825  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837826  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837827  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           184   
1          2500             SNP     M01-Jan         0.815           137   
2          2500 

In [61]:
#df_PrdForecasts_Season_DOW_TOD_DY[(df_PrdForecasts_Season_DOW_TOD_DY['SEGID']=='0006_146.9') & (df_PrdForecasts_Season_DOW_TOD_DY['DOWGroup']=='6-Saturday')].head(20)

In [62]:
#df_PrdForecasts_Season_DOW_TOD[df_PrdForecasts_Season_DOW_TOD['SEGID']=='0006_146.9'].head(20)

In [63]:
#dftemp = dfs_PrdForecasts_Season_DOW_TOD_wGroups[0].groupby(['VCGroupCode']).agg({'VolMaxHrPct':[np.size]})
df_TODFactors_DY[df_TODFactors_DY['SeasonGroup']=='S00-Ann']

SiteGroupSeason SeasonGroup    DOWGroup Prd HrPctOf  VolPkHrPct
25020             SN0     S00-Ann    1-Monday  AM      DY      0.0386
25021             SN0     S00-Ann    1-Monday  DY      DY      0.1144
25022             SN0     S00-Ann    1-Monday  EV      DY      0.0969
25023             SN0     S00-Ann    1-Monday  MD      DY      0.0769
25024             SN0     S00-Ann    1-Monday  PM      DY      0.0926
...               ...         ...         ...  ..     ...         ...
57955             XX4     S00-Ann  W2-Weekend  AM      DY      0.0608
57956             XX4     S00-Ann  W2-Weekend  DY      DY      0.0872
57957             XX4     S00-Ann  W2-Weekend  EV      DY      0.0617
57958             XX4     S00-Ann  W2-Weekend  MD      DY      0.0658
57959             XX4     S00-Ann  W2-Weekend  PM      DY      0.0867

[1710 rows x 6 columns]

In [64]:
dfs_PkHrForecasts = []

for df_PrdForecasts_Season_DOW_TOD_wGroups in dfs_PrdForecasts_Season_DOW_TOD_wGroups: 
    
    df_PkHrForecasts = pd.DataFrame.merge(df_PrdForecasts_Season_DOW_TOD_wGroups,df_PrdDuration,on='Prd',how='left')   
    
    df_PkHrForecasts['AvgSsnDOWPkHrVol'] = df_PkHrForecasts['AvgSsnDOWPrdVol'] * df_PkHrForecasts['VolPkHrPct']

    #add truck Pctage adjustments
    #PCE for medium and heavy trucks from HCM 2000 Exhibit 23-8
    Emd = 1.2 #same as RVs
    Ehv = 1.5
    df_PkHrForecasts['TrkFac'] = 1 + (df_PkHrForecasts[nameMDPct]/100 * (Emd-1)) + (df_PkHrForecasts[nameHVPct]/100 * (Ehv-1))
    
    #calculate PCE
    df_PkHrForecasts['PrdPCEFlow' ] = (df_PkHrForecasts['AvgSsnDOWPrdVol' ] *  df_PkHrForecasts['TrkFac']) /  df_PkHrForecasts['PrdHrs']
    df_PkHrForecasts['PkHrPCEFlow'] =  df_PkHrForecasts['AvgSsnDOWPkHrVol'] *  df_PkHrForecasts['TrkFac']
    df_PkHrForecasts['PrdVC'      ] =  df_PkHrForecasts['PrdPCEFlow'      ] / (df_PkHrForecasts[nameCap1HL] * df_PkHrForecasts[nameLanes])
    df_PkHrForecasts['PkHrVC'     ] =  df_PkHrForecasts['PkHrPCEFlow'     ] / (df_PkHrForecasts[nameCap1HL] * df_PkHrForecasts[nameLanes])
    
    display(df_PkHrForecasts)
    
    dfs_PkHrForecasts.append(df_PkHrForecasts)

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1392.3  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1392.3  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1510.9  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1510.9  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1717.9  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
758467  1084_001.0       1.0         914.1  Arterial    1.0  D2    1.0  5.0   
758468  2865_001.3       2.0        2329.2  Arterial    1.0  D1    1.0  4.0   
758469  2865_001.3       2.0        2329.2  Arterial    1.0  D2    1.0  4.0   
758470  3004_000.9       2.0         222.1  Arterial    1.0  D1    1.0  4.0   
758471  3004_000.9       2.0         222.1  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5004      AM  0.1829        6.3   
1          Principal Arterial        1065  0.4996      AM  0.1829        6.4   
2          Principal Arterial        1065  0.5384      AM  0.1612       17.6   
3          Principal Arterial        1065  0.4616      AM  0.1612       20.2   
4          Principal Arterial        1065  0.5654      AM  0.1599       16.1   
...                           ...     ...     ...     ...     ...        ...   
758467          Collector             572  0.6000      DY  1.0000       21.6   
758468          Collector             785  0.6000      DY  1.0000        1.6   
758469          Collector             785  0.6000      DY  1.0000        1.6   
758470          Collector             785  0.6000      DY  1.0000        7.0   
758471          Collector             785  0.6000      DY  1.0000        7.4   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.5   2019             0                0              0.0   
1             4.5   2019             0                0              0.0   
2            14.6   2019             0                0              0.0   
3            16.9   2019             0                0              0.0   
4            13.2   2019             0                0              0.0   
...           ...    ...           ...              ...              ...   
758467       16.2   2019           350              350            210.0   
758468        1.3   2019             0                0              0.0   
758469        1.3   2019             0                0              0.0   
758470        3.7   2019             0                0              0.0   
758471        3.9   2019             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
758467  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758468  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758469  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758470  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758471  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1465.9  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1465.9  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1632.9  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1632.9  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1848.0  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
770707  1084_001.0       1.0         884.1  Arterial    1.0  D2    1.0  5.0   
770708  2865_001.3       2.0        2523.7  Arterial    1.0  D1    1.0  4.0   
770709  2865_001.3       2.0        2523.7  Arterial    1.0  D2    1.0  4.0   
770710  3004_000.9       2.0         552.4  Arterial    1.0  D1    1.0  4.0   
770711  3004_000.9       2.0         552.4  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4747      AM  0.1810        6.7   
1          Principal Arterial        1065  0.5253      AM  0.1810        6.1   
2          Principal Arterial        1065  0.5415      AM  0.1623       17.9   
3          Principal Arterial        1065  0.4585      AM  0.1623       20.4   
4          Principal Arterial        1065  0.5675      AM  0.1617       16.4   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       24.2   
770708          Collector             785  0.6000      DY  1.0000        1.7   
770709          Collector             785  0.6000      DY  1.0000        1.7   
770710          Collector             785  0.6000      DY  1.0000        9.6   
770711          Collector             785  0.6000      DY  1.0000       10.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.9   2024             0                0              0.0   
1             4.4   2024             0                0              0.0   
2            14.4   2024             0                0              0.0   
3            16.8   2024             0                0              0.0   
4            13.0   2024             0                0              0.0   
...           ...    ...           ...              ...              ...   
770707       18.3   2024           400              400            240.0   
770708        1.4   2024             0                0              0.0   
770709        1.4   2024             0                0              0.0   
770710        8.4   2024             0                0              0.0   
770711        8.7   2024             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1559.1  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1559.1  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1755.5  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1755.5  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1970.6  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
793555  1084_001.0       1.0         779.7  Arterial    1.0  D2    1.0  5.0   
793556  2865_001.3       2.0        2781.7  Arterial    1.0  D1    1.0  4.0   
793557  2865_001.3       2.0        2781.7  Arterial    1.0  D2    1.0  4.0   
793558  3004_000.9       2.0        2345.6  Arterial    1.0  D1    1.0  3.0   
793559  3004_000.9       2.0        2345.6  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4952      AM  0.1844        6.3   
1          Principal Arterial        1065  0.5048      AM  0.1844        6.2   
2          Principal Arterial        1065  0.4966      AM  0.1660       18.0   
3          Principal Arterial        1065  0.5034      AM  0.1660       17.7   
4          Principal Arterial        1065  0.5233      AM  0.1645       16.6   
...                           ...     ...     ...     ...     ...        ...   
793555          Collector             572  0.6000      DY  1.0000       26.3   
793556          Collector             785  0.6000      DY  1.0000        1.7   
793557          Collector             785  0.6000      DY  1.0000        1.7   
793558       Minor Arterial           939  0.6000      DY  1.0000        7.6   
793559       Minor Arterial           939  0.6000      DY  1.0000        8.5   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.6   2030             0                0              0.0   
1             4.5   2030             0                0              0.0   
2            14.3   2030             0                0              0.0   
3            14.2   2030             0                0              0.0   
4            13.2   2030             0                0              0.0   
...           ...    ...           ...              ...              ...   
793555       20.7   2030           500              500            300.0   
793556        1.3   2030             0                0              0.0   
793557        1.4   2030             0                0              0.0   
793558        3.5   2030             0                0              0.0   
793559        3.9   2030             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
793555  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793556  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793557  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793558  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793559  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1684.9  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1684.9  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        2230.4  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        2230.4  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        2456.4  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
814567  1084_001.0       1.0         892.6  Arterial    1.0  D2    1.0  5.0   
814568  2865_001.3       2.0        3188.5  Arterial    1.0  D1    1.0  4.0   
814569  2865_001.3       2.0        3188.5  Arterial    1.0  D2    1.0  4.0   
814570  3004_000.9       3.0        3966.8  Arterial    1.0  D1    1.0  3.0   
814571  3004_000.9       3.0        3966.8  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5225      AM  0.1855        5.9   
1          Principal Arterial        1065  0.4775      AM  0.1855        6.5   
2          Principal Arterial        1065  0.4736      AM  0.1615       18.1   
3          Principal Arterial        1065  0.5264      AM  0.1615       16.1   
4          Principal Arterial        1065  0.4974      AM  0.1598       16.9   
...                           ...     ...     ...     ...     ...        ...   
814567          Collector             572  0.6000      DY  1.0000       29.0   
814568          Collector             785  0.6000      DY  1.0000        1.8   
814569          Collector             785  0.6000      DY  1.0000        1.8   
814570       Minor Arterial           894  0.6000      DY  1.0000        9.5   
814571       Minor Arterial           894  0.6000      DY  1.0000        9.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.4   2040             0                0              0.0   
1             4.8   2040             0                0              0.0   
2            15.1   2040             0                0              0.0   
3            13.7   2040             0                0              0.0   
4            14.2   2040             0                0              0.0   
...           ...    ...           ...              ...              ...   
814567       29.3   2040           700              700            420.0   
814568        1.5   2040             0                0              0.0   
814569        1.5   2040             0                0              0.0   
814570        3.8   2040             0                0              0.0   
814571        4.1   2040             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
814567  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814568  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814569  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814570  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814571  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1811.9  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1811.9  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0         884.2  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0         884.2  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0         840.3  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837211  1084_001.0       1.0         647.5  Arterial    1.0  D2    1.0  5.0   
837212  2865_001.3       2.0        3583.6  Arterial    1.0  D1    1.0  4.0   
837213  2865_001.3       2.0        3583.6  Arterial    1.0  D2    1.0  4.0   
837214  3004_000.9       3.0       16315.5  Arterial    1.0  D1    1.0  3.0   
837215  3004_000.9       3.0       16315.5  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5715      AM  0.1879        5.4   
1          Principal Arterial        1065  0.4285      AM  0.1879        7.2   
2            Minor Arterial           983  0.5076      AM  0.1408       23.1   
3            Minor Arterial           983  0.4924      AM  0.1408       21.4   
4            Minor Arterial           983  0.5134      AM  0.1419       23.0   
...                           ...     ...     ...     ...     ...        ...   
837211          Collector             572  0.6000      DY  1.0000       20.5   
837212          Collector             785  0.6000      DY  1.0000        1.7   
837213          Collector             785  0.6000      DY  1.0000        1.7   
837214       Minor Arterial           894  0.6000      DY  1.0000       16.1   
837215       Minor Arterial           894  0.6000      DY  1.0000       13.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.0   2050          2100             2100       225.508185   
1             5.3   2050          2100             2100       169.081815   
2            35.6   2050          1200             1200        85.764096   
3            33.9   2050          1200             1200        83.195904   
4            35.5   2050          1500             1500       109.277190   
...           ...    ...           ...              ...              ...   
837211       19.6   2050           800              800       480.000000   
837212        1.6   2050          3800             3800      2280.000000   
837213        1.6   2050          3800             3800      2280.000000   
837214        6.5   2050         35500            35500     21300.000000   
837215        5.3   2050         35500            35500     21300.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837211  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837212  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837213  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837214  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837215  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           183   
1          2500             SNP     M01-Jan         0.815           137   
2          2500 

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1669.8  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1669.8  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        3098.9  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        3098.9  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        3352.3  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
770707  1084_001.0       1.0         875.9  Arterial    1.0  D2    1.0  5.0   
770708  2865_001.3       2.0        3159.1  Arterial    1.0  D1    1.0  4.0   
770709  2865_001.3       2.0        3159.1  Arterial    1.0  D2    1.0  4.0   
770710  3004_000.9       3.0         716.8  Arterial    1.0  D1    1.0  4.0   
770711  3004_000.9       3.0         716.8  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4754      AM  0.1817        6.9   
1          Principal Arterial        1065  0.5246      AM  0.1817        6.2   
2          Principal Arterial        1065  0.7235      AM  0.1945       10.9   
3          Principal Arterial        1065  0.2765      AM  0.1945       22.6   
4          Principal Arterial        1065  0.7256      AM  0.1916       10.8   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       28.6   
770708          Collector             785  0.6000      DY  1.0000        2.0   
770709          Collector             785  0.6000      DY  1.0000        2.0   
770710          Collector             748  0.6000      DY  1.0000        7.6   
770711          Collector             748  0.6000      DY  1.0000        8.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             5.0   2040             0                0         0.000000   
1             4.5   2040             0                0         0.000000   
2             7.8   2040             0              850       119.612638   
3            17.9   2040             0              850        45.712363   
4             7.8   2040             0              900       125.122464   
...           ...    ...           ...              ...              ...   
770707       26.6   2040           700              700       420.000000   
770708        1.3   2040             0                0         0.000000   
770709        1.3   2040             0                0         0.000000   
770710        3.9   2040             0                0         0.000000   
770711        4.1   2040             0                0         0.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1795.1  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1795.1  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0        3898.2  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0        3898.2  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0        3907.8  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
770707  1084_001.0       1.0         744.6  Arterial    1.0  D2    1.0  5.0   
770708  2865_001.3       2.0        3543.9  Arterial    1.0  D1    1.0  4.0   
770709  2865_001.3       2.0        3543.9  Arterial    1.0  D2    1.0  4.0   
770710  3004_000.9       3.0         778.5  Arterial    1.0  D1    1.0  4.0   
770711  3004_000.9       3.0         778.5  Arterial    1.0  D2    1.0  4.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4772      AM  0.1823        6.8   
1          Principal Arterial        1065  0.5228      AM  0.1823        6.2   
2            Minor Arterial           983  0.7239      AM  0.1981       14.4   
3            Minor Arterial           983  0.2761      AM  0.1981       22.2   
4            Minor Arterial           983  0.7258      AM  0.1978       14.3   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       22.7   
770708          Collector             785  0.6000      DY  1.0000        1.9   
770709          Collector             785  0.6000      DY  1.0000        1.9   
770710          Collector             748  0.6000      DY  1.0000        7.7   
770711          Collector             748  0.6000      DY  1.0000        7.7   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.9   2050          2100             2100       182.686476   
1             4.5   2050          2100             2100       200.143524   
2            15.4   2050          1200             4200       602.299278   
3            29.0   2050          1200             4200       229.720722   
4            15.3   2050          1500             4600       660.390904   
...           ...    ...           ...              ...              ...   
770707       19.6   2050           800              900       540.000000   
770708        1.5   2050          3800             3800      2280.000000   
770709        1.5   2050          3800             3800      2280.000000   
770710        3.6   2050         35500            20000     12000.000000   
770711        3.7   2050         35500            20000     12000.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           148   
1          2500             SNP     M01-Jan         0.815           163   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1559.2  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1559.2  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        1757.1  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        1757.1  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        1971.4  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
794983  1084_001.0       1.0         815.4  Arterial    1.0  D2    1.0  5.0   
794984  2865_001.3       2.0        2783.7  Arterial    1.0  D1    1.0  4.0   
794985  2865_001.3       2.0        2783.7  Arterial    1.0  D2    1.0  4.0   
794986  3004_000.9       2.0        2312.0  Arterial    1.0  D1    1.0  3.0   
794987  3004_000.9       2.0        2312.0  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4957      AM  0.1845        6.3   
1          Principal Arterial        1065  0.5043      AM  0.1845        6.2   
2          Principal Arterial        1065  0.4973      AM  0.1661       17.9   
3          Principal Arterial        1065  0.5027      AM  0.1661       17.7   
4          Principal Arterial        1065  0.5234      AM  0.1645       16.5   
...                           ...     ...     ...     ...     ...        ...   
794983          Collector             572  0.6000      DY  1.0000       26.2   
794984          Collector             785  0.6000      DY  1.0000        1.7   
794985          Collector             785  0.6000      DY  1.0000        1.7   
794986       Minor Arterial           939  0.6000      DY  1.0000        7.6   
794987       Minor Arterial           939  0.6000      DY  1.0000        8.6   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.6   2030             0                0              0.0   
1             4.5   2030             0                0              0.0   
2            14.3   2030             0                0              0.0   
3            14.2   2030             0                0              0.0   
4            13.2   2030             0                0              0.0   
...           ...    ...           ...              ...              ...   
794983       20.5   2030           500              550            330.0   
794984        1.3   2030             0                0              0.0   
794985        1.4   2030             0                0              0.0   
794986        3.5   2030             0                0              0.0   
794987        3.8   2030             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
794983  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794984  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794985  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794986  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794987  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1686.0  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1686.0  Arterial    1.0  D2    1.0  2.0   
2       0006_149.9       1.0        2111.0  Arterial    1.0  D1    1.0  2.0   
3       0006_149.9       1.0        2111.0  Arterial    1.0  D2    1.0  2.0   
4       0006_150.6       1.0        2340.3  Arterial    1.0  D1    1.0  2.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
817219  1084_001.0       1.0         921.9  Arterial    1.0  D2    1.0  5.0   
817220  2865_001.3       2.0        3192.3  Arterial    1.0  D1    1.0  4.0   
817221  2865_001.3       2.0        3192.3  Arterial    1.0  D2    1.0  4.0   
817222  3004_000.9       3.0        5104.6  Arterial    1.0  D1    1.0  3.0   
817223  3004_000.9       3.0        5104.6  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5228      AM  0.1855        5.9   
1          Principal Arterial        1065  0.4772      AM  0.1855        6.5   
2          Principal Arterial        1065  0.4810      AM  0.1643       18.0   
3          Principal Arterial        1065  0.5190      AM  0.1643       16.5   
4          Principal Arterial        1065  0.5058      AM  0.1627       16.7   
...                           ...     ...     ...     ...     ...        ...   
817219          Collector             572  0.6000      DY  1.0000       29.1   
817220          Collector             785  0.6000      DY  1.0000        1.8   
817221          Collector             785  0.6000      DY  1.0000        1.8   
817222       Minor Arterial           894  0.6000      DY  1.0000       11.0   
817223       Minor Arterial           894  0.6000      DY  1.0000        9.2   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.4   2040             0                0              0.0   
1             4.8   2040             0                0              0.0   
2            15.3   2040             0                0              0.0   
3            14.2   2040             0                0              0.0   
4            14.3   2040             0                0              0.0   
...           ...    ...           ...              ...              ...   
817219       30.4   2040           700              750            450.0   
817220        1.5   2040             0                0              0.0   
817221        1.5   2040             0                0              0.0   
817222        4.8   2040             0             1100            660.0   
817223        3.9   2040             0             1100            660.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
817219  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817220  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817221  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817222  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817223  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815             0   
1          2500             SNP     M01-Jan         0.815             0   
2          2500 

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
0       0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
1       0006_146.9       1.0        1813.3  Arterial    1.0  D2    1.0  2.0   
2       0147_003.1       1.0         870.4  Arterial    1.0  D1    1.0  3.0   
3       0147_003.1       1.0         870.4  Arterial    1.0  D2    1.0  3.0   
4       0147_003.9       1.0         837.8  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837823  1084_001.0       1.0         572.5  Arterial    1.0  D2    1.0  5.0   
837824  2865_001.3       2.0        3583.6  Arterial    1.0  D1    1.0  4.0   
837825  2865_001.3       2.0        3583.6  Arterial    1.0  D2    1.0  4.0   
837826  3004_000.9       3.0        8477.5  Arterial    1.0  D1    1.0  3.0   
837827  3004_000.9       3.0        8477.5  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5723      AM  0.1884        5.4   
1          Principal Arterial        1065  0.4277      AM  0.1884        7.2   
2            Minor Arterial           983  0.5086      AM  0.1410       23.1   
3            Minor Arterial           983  0.4914      AM  0.1410       21.4   
4            Minor Arterial           983  0.5152      AM  0.1416       22.9   
...                           ...     ...     ...     ...     ...        ...   
837823          Collector             572  0.6000      DY  1.0000       19.4   
837824          Collector             785  0.6000      DY  1.0000        1.7   
837825          Collector             785  0.6000      DY  1.0000        1.7   
837826       Minor Arterial           894  0.6000      DY  1.0000        9.4   
837827       Minor Arterial           894  0.6000      DY  1.0000        6.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             3.9   2050          2100             2100       226.424772   
1             5.3   2050          2100             2100       169.215228   
2            35.6   2050          1200             1200        86.055120   
3            34.2   2050          1200             1200        83.144880   
4            35.2   2050          1500             1500       109.428480   
...           ...    ...           ...              ...              ...   
837823       19.3   2050           800              700       420.000000   
837824        1.6   2050          3800             3800      2280.000000   
837825        1.6   2050          3800             3800      2280.000000   
837826        4.3   2050         35500            27500     16500.000000   
837827        3.0   2050         35500            27500     16500.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837823  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837824  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837825  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837826  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837827  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan         0.815           184   
1          2500             SNP     M01-Jan         0.815           137   
2          2500 

In [65]:
df_PkHrForecasts.columns

Index(['SEGID', 'AREATYPE', 'SegDYVol_TDM', 'FUNCGROUP', 'FGFAC', 'Dir',
       'LANES', 'FT', 'FTCLASS', 'CAP1HL', 'DFAC', 'Prd_TDM', 'PRDFAC',
       'MDPERCENT', 'HVPERCENT', 'FYEAR', 'ForecastAADT', 'ForecastAADTAdj',
       'AvgAnnualPrdVol', 'DOWFACFC', 'SsnGrp', 'SsnATGroup', 'SsnVolCls',
       'Vol_From', 'Vol_To', 'SiteGroupSeason', 'SeasonGroup', 'SeasonFactor',
       'AvgSsnPrdVol', 'SiteGroupDOW', 'DOWGroup', 'DOWFactor',
       'AvgSsnDOWPrdVol', 'Prd', 'HrPctOf', 'VolPkHrPct', 'SeasonType',
       'VCGroupCode', 'PrdHrs', 'AvgSsnDOWPkHrVol', 'TrkFac', 'PrdPCEFlow',
       'PkHrPCEFlow', 'PrdVC', 'PkHrVC'],
      dtype='object')

In [66]:
df_PkHrForecasts[df_PkHrForecasts['SeasonGroup']=='S00-Ann']

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES   FT  \
131424  0006_146.9       1.0        1813.3  Arterial    1.0  D1    1.0  2.0   
131425  0006_146.9       1.0        1813.3  Arterial    1.0  D2    1.0  2.0   
131426  0147_003.1       1.0         870.4  Arterial    1.0  D1    1.0  3.0   
131427  0147_003.1       1.0         870.4  Arterial    1.0  D2    1.0  3.0   
131428  0147_003.9       1.0         837.8  Arterial    1.0  D1    1.0  3.0   
...            ...       ...           ...       ...    ...  ..    ...  ...   
837823  1084_001.0       1.0         572.5  Arterial    1.0  D2    1.0  5.0   
837824  2865_001.3       2.0        3583.6  Arterial    1.0  D1    1.0  4.0   
837825  2865_001.3       2.0        3583.6  Arterial    1.0  D2    1.0  4.0   
837826  3004_000.9       3.0        8477.5  Arterial    1.0  D1    1.0  3.0   
837827  3004_000.9       3.0        8477.5  Arterial    1.0  D2    1.0  3.0   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
131424     Principal Arterial        1065  0.5723      AM  0.1884        5.4   
131425     Principal Arterial        1065  0.4277      AM  0.1884        7.2   
131426       Minor Arterial           983  0.5086      AM  0.1410       23.1   
131427       Minor Arterial           983  0.4914      AM  0.1410       21.4   
131428       Minor Arterial           983  0.5152      AM  0.1416       22.9   
...                           ...     ...     ...     ...     ...        ...   
837823          Collector             572  0.6000      DY  1.0000       19.4   
837824          Collector             785  0.6000      DY  1.0000        1.7   
837825          Collector             785  0.6000      DY  1.0000        1.7   
837826       Minor Arterial           894  0.6000      DY  1.0000        9.4   
837827       Minor Arterial           894  0.6000      DY  1.0000        6.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
131424        3.9   2050          2100             2100       226.424772   
131425        5.3   2050          2100             2100       169.215228   
131426       35.6   2050          1200             1200        86.055120   
131427       34.2   2050          1200             1200        83.144880   
131428       35.2   2050          1500             1500       109.428480   
...           ...    ...           ...              ...              ...   
837823       19.3   2050           800              700       420.000000   
837824        1.6   2050          3800             3800      2280.000000   
837825        1.6   2050          3800             3800      2280.000000   
837826        4.3   2050         35500            27500     16500.000000   
837827        3.0   2050         35500            27500     16500.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
131424  Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
131425  Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
131426  Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
131427  Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
131428  Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837823  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837824  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837825  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837826  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837827  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
131424     2500             SNP     S00-Ann           1.0           226   
131425     2500             SNP     S00-Ann           1.0           169   
131426     2500 

In [67]:
#15-Min Analysis

dfs_VC = []

for df_PkHrForecasts in dfs_PkHrForecasts:

    df_VC = df_PkHrForecasts
    
    #PHF conditions (from Chad's spreadsheet for Urban (0.92,0.95,0.97,0.98). HCM2000 Exhibit 9.2 says default PHF for Urban Areas is 0.92, Rural is 0.88. Rural estimated at (0.88,0.91,0.93,0.95)
    conditions = [
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] <= 0.85),
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] >  0.85) & (df_VC['PkHrVC'] <= 0.95),
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] >  0.95) & (df_VC['PkHrVC'] <= 1.00),
        (df_VC[nameAT] >= 3) & (df_VC['PkHrVC'] >  1.00),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] <= 0.85),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] >  0.85) & (df_VC['PkHrVC'] <= 0.95),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] >  0.95) & (df_VC['PkHrVC'] <= 1.00),
        (df_VC[nameAT] <= 2) & (df_VC['PkHrVC'] >  1.00)
    ]
    choices = [0.92,0.95,0.97,0.98,0.88,0.91,0.93,0.95]

    df_VC['PHF'] = np.select(conditions, choices, default=0)


    #15-min volume and v/c calcs
    df_VC['Pk15PCEFlow'] = df_VC['PkHrPCEFlow']  / df_VC['PHF']
    df_VC['Pk15VC'     ] = df_VC['Pk15PCEFlow'] / (df_VC[nameCap1HL] * df_VC[nameLanes])

    #effective K-factor
    #df_VC['kFactor_effective']  = df_VC['ForecastPkHr']  / df_VC['ForecastAADT']

    #convert to int and round columns after calcs
    df_VC = df_VC.fillna(0)
    df_VC['AREATYPE'       ] = df_VC['AREATYPE'       ].astype(int)
    df_VC['FT'             ] = df_VC['FT'             ].astype(int)
    df_VC['LANES'          ] = df_VC['LANES'          ].astype(int)
    df_VC['ForecastAADT'   ] = df_VC['ForecastAADT'   ].astype(int)
    df_VC['ForecastAADTAdj'] = df_VC['ForecastAADTAdj'].astype(int)
    df_VC['PrdPCEFlow'     ] = df_VC['PrdPCEFlow'     ].astype(int)
    df_VC['PkHrPCEFlow'    ] = df_VC['PkHrPCEFlow'    ].astype(int)
    df_VC['Pk15PCEFlow'    ] = df_VC['Pk15PCEFlow'    ].astype(int)
    df_VC = df_VC.round({'SeasonFactor':2,'DOWFactor':2,'PrdVC':2,'PkHrVC':2,'Pk15VC':2,nameMDPct:2,nameHVPct:2,'VolMaxHrPct':2,'FactorTrucks':2})
    
    pd.set_option('display.max_columns', None)
    
    display(df_VC)
    
    dfs_VC.append(df_VC)
    

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1392.3  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1392.3  Arterial    1.0  D2      1   2   
2       0006_149.9         1        1510.9  Arterial    1.0  D1      1   2   
3       0006_149.9         1        1510.9  Arterial    1.0  D2      1   2   
4       0006_150.6         1        1717.9  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
758467  1084_001.0         1         914.1  Arterial    1.0  D2      1   5   
758468  2865_001.3         2        2329.2  Arterial    1.0  D1      1   4   
758469  2865_001.3         2        2329.2  Arterial    1.0  D2      1   4   
758470  3004_000.9         2         222.1  Arterial    1.0  D1      1   4   
758471  3004_000.9         2         222.1  Arterial    1.0  D2      1   4   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5004      AM  0.1829        6.3   
1          Principal Arterial        1065  0.4996      AM  0.1829        6.4   
2          Principal Arterial        1065  0.5384      AM  0.1612       17.6   
3          Principal Arterial        1065  0.4616      AM  0.1612       20.2   
4          Principal Arterial        1065  0.5654      AM  0.1599       16.1   
...                           ...     ...     ...     ...     ...        ...   
758467          Collector             572  0.6000      DY  1.0000       21.6   
758468          Collector             785  0.6000      DY  1.0000        1.6   
758469          Collector             785  0.6000      DY  1.0000        1.6   
758470          Collector             785  0.6000      DY  1.0000        7.0   
758471          Collector             785  0.6000      DY  1.0000        7.4   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.5   2019             0                0              0.0   
1             4.5   2019             0                0              0.0   
2            14.6   2019             0                0              0.0   
3            16.9   2019             0                0              0.0   
4            13.2   2019             0                0              0.0   
...           ...    ...           ...              ...              ...   
758467       16.2   2019           350              350            210.0   
758468        1.3   2019             0                0              0.0   
758469        1.3   2019             0                0              0.0   
758470        3.7   2019             0                0              0.0   
758471        3.9   2019             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
758467  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758468  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758469  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758470  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
758471  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1465.9  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1465.9  Arterial    1.0  D2      1   2   
2       0006_149.9         1        1632.9  Arterial    1.0  D1      1   2   
3       0006_149.9         1        1632.9  Arterial    1.0  D2      1   2   
4       0006_150.6         1        1848.0  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
770707  1084_001.0         1         884.1  Arterial    1.0  D2      1   5   
770708  2865_001.3         2        2523.7  Arterial    1.0  D1      1   4   
770709  2865_001.3         2        2523.7  Arterial    1.0  D2      1   4   
770710  3004_000.9         2         552.4  Arterial    1.0  D1      1   4   
770711  3004_000.9         2         552.4  Arterial    1.0  D2      1   4   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4747      AM  0.1810        6.7   
1          Principal Arterial        1065  0.5253      AM  0.1810        6.1   
2          Principal Arterial        1065  0.5415      AM  0.1623       17.9   
3          Principal Arterial        1065  0.4585      AM  0.1623       20.4   
4          Principal Arterial        1065  0.5675      AM  0.1617       16.4   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       24.2   
770708          Collector             785  0.6000      DY  1.0000        1.7   
770709          Collector             785  0.6000      DY  1.0000        1.7   
770710          Collector             785  0.6000      DY  1.0000        9.6   
770711          Collector             785  0.6000      DY  1.0000       10.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.9   2024             0                0              0.0   
1             4.4   2024             0                0              0.0   
2            14.4   2024             0                0              0.0   
3            16.8   2024             0                0              0.0   
4            13.0   2024             0                0              0.0   
...           ...    ...           ...              ...              ...   
770707       18.3   2024           400              400            240.0   
770708        1.4   2024             0                0              0.0   
770709        1.4   2024             0                0              0.0   
770710        8.4   2024             0                0              0.0   
770711        8.7   2024             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1559.1  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1559.1  Arterial    1.0  D2      1   2   
2       0006_149.9         1        1755.5  Arterial    1.0  D1      1   2   
3       0006_149.9         1        1755.5  Arterial    1.0  D2      1   2   
4       0006_150.6         1        1970.6  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
793555  1084_001.0         1         779.7  Arterial    1.0  D2      1   5   
793556  2865_001.3         2        2781.7  Arterial    1.0  D1      1   4   
793557  2865_001.3         2        2781.7  Arterial    1.0  D2      1   4   
793558  3004_000.9         2        2345.6  Arterial    1.0  D1      1   3   
793559  3004_000.9         2        2345.6  Arterial    1.0  D2      1   3   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4952      AM  0.1844        6.3   
1          Principal Arterial        1065  0.5048      AM  0.1844        6.2   
2          Principal Arterial        1065  0.4966      AM  0.1660       18.0   
3          Principal Arterial        1065  0.5034      AM  0.1660       17.7   
4          Principal Arterial        1065  0.5233      AM  0.1645       16.6   
...                           ...     ...     ...     ...     ...        ...   
793555          Collector             572  0.6000      DY  1.0000       26.3   
793556          Collector             785  0.6000      DY  1.0000        1.7   
793557          Collector             785  0.6000      DY  1.0000        1.7   
793558       Minor Arterial           939  0.6000      DY  1.0000        7.6   
793559       Minor Arterial           939  0.6000      DY  1.0000        8.5   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.6   2030             0                0              0.0   
1             4.5   2030             0                0              0.0   
2            14.3   2030             0                0              0.0   
3            14.2   2030             0                0              0.0   
4            13.2   2030             0                0              0.0   
...           ...    ...           ...              ...              ...   
793555       20.7   2030           500              500            300.0   
793556        1.3   2030             0                0              0.0   
793557        1.4   2030             0                0              0.0   
793558        3.5   2030             0                0              0.0   
793559        3.9   2030             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
793555  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793556  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793557  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793558  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
793559  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1684.9  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1684.9  Arterial    1.0  D2      1   2   
2       0006_149.9         1        2230.4  Arterial    1.0  D1      1   2   
3       0006_149.9         1        2230.4  Arterial    1.0  D2      1   2   
4       0006_150.6         1        2456.4  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
814567  1084_001.0         1         892.6  Arterial    1.0  D2      1   5   
814568  2865_001.3         2        3188.5  Arterial    1.0  D1      1   4   
814569  2865_001.3         2        3188.5  Arterial    1.0  D2      1   4   
814570  3004_000.9         3        3966.8  Arterial    1.0  D1      1   3   
814571  3004_000.9         3        3966.8  Arterial    1.0  D2      1   3   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5225      AM  0.1855        5.9   
1          Principal Arterial        1065  0.4775      AM  0.1855        6.5   
2          Principal Arterial        1065  0.4736      AM  0.1615       18.1   
3          Principal Arterial        1065  0.5264      AM  0.1615       16.1   
4          Principal Arterial        1065  0.4974      AM  0.1598       16.9   
...                           ...     ...     ...     ...     ...        ...   
814567          Collector             572  0.6000      DY  1.0000       29.0   
814568          Collector             785  0.6000      DY  1.0000        1.8   
814569          Collector             785  0.6000      DY  1.0000        1.8   
814570       Minor Arterial           894  0.6000      DY  1.0000        9.5   
814571       Minor Arterial           894  0.6000      DY  1.0000        9.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.4   2040             0                0              0.0   
1             4.8   2040             0                0              0.0   
2            15.1   2040             0                0              0.0   
3            13.7   2040             0                0              0.0   
4            14.2   2040             0                0              0.0   
...           ...    ...           ...              ...              ...   
814567       29.3   2040           700              700            420.0   
814568        1.5   2040             0                0              0.0   
814569        1.5   2040             0                0              0.0   
814570        3.8   2040             0                0              0.0   
814571        4.1   2040             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
814567  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814568  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814569  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814570  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
814571  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1811.9  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1811.9  Arterial    1.0  D2      1   2   
2       0147_003.1         1         884.2  Arterial    1.0  D1      1   3   
3       0147_003.1         1         884.2  Arterial    1.0  D2      1   3   
4       0147_003.9         1         840.3  Arterial    1.0  D1      1   3   
...            ...       ...           ...       ...    ...  ..    ...  ..   
837211  1084_001.0         1         647.5  Arterial    1.0  D2      1   5   
837212  2865_001.3         2        3583.6  Arterial    1.0  D1      1   4   
837213  2865_001.3         2        3583.6  Arterial    1.0  D2      1   4   
837214  3004_000.9         3       16315.5  Arterial    1.0  D1      1   3   
837215  3004_000.9         3       16315.5  Arterial    1.0  D2      1   3   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5715      AM  0.1879        5.4   
1          Principal Arterial        1065  0.4285      AM  0.1879        7.2   
2            Minor Arterial           983  0.5076      AM  0.1408       23.1   
3            Minor Arterial           983  0.4924      AM  0.1408       21.4   
4            Minor Arterial           983  0.5134      AM  0.1419       23.0   
...                           ...     ...     ...     ...     ...        ...   
837211          Collector             572  0.6000      DY  1.0000       20.5   
837212          Collector             785  0.6000      DY  1.0000        1.7   
837213          Collector             785  0.6000      DY  1.0000        1.7   
837214       Minor Arterial           894  0.6000      DY  1.0000       16.1   
837215       Minor Arterial           894  0.6000      DY  1.0000       13.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.0   2050          2100             2100       225.508185   
1             5.3   2050          2100             2100       169.081815   
2            35.6   2050          1200             1200        85.764096   
3            33.9   2050          1200             1200        83.195904   
4            35.5   2050          1500             1500       109.277190   
...           ...    ...           ...              ...              ...   
837211       19.6   2050           800              800       480.000000   
837212        1.6   2050          3800             3800      2280.000000   
837213        1.6   2050          3800             3800      2280.000000   
837214        6.5   2050         35500            35500     21300.000000   
837215        5.3   2050         35500            35500     21300.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837211  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837212  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837213  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837214  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837215  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82           183   
1          2500             SNP     M01-Jan          0.82           137   
2          2500             

...

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1669.8  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1669.8  Arterial    1.0  D2      1   2   
2       0006_149.9         1        3098.9  Arterial    1.0  D1      1   2   
3       0006_149.9         1        3098.9  Arterial    1.0  D2      1   2   
4       0006_150.6         1        3352.3  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
770707  1084_001.0         1         875.9  Arterial    1.0  D2      1   5   
770708  2865_001.3         2        3159.1  Arterial    1.0  D1      1   4   
770709  2865_001.3         2        3159.1  Arterial    1.0  D2      1   4   
770710  3004_000.9         3         716.8  Arterial    1.0  D1      1   4   
770711  3004_000.9         3         716.8  Arterial    1.0  D2      1   4   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4754      AM  0.1817        6.9   
1          Principal Arterial        1065  0.5246      AM  0.1817        6.2   
2          Principal Arterial        1065  0.7235      AM  0.1945       10.9   
3          Principal Arterial        1065  0.2765      AM  0.1945       22.6   
4          Principal Arterial        1065  0.7256      AM  0.1916       10.8   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       28.6   
770708          Collector             785  0.6000      DY  1.0000        2.0   
770709          Collector             785  0.6000      DY  1.0000        2.0   
770710          Collector             748  0.6000      DY  1.0000        7.6   
770711          Collector             748  0.6000      DY  1.0000        8.0   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             5.0   2040             0                0         0.000000   
1             4.5   2040             0                0         0.000000   
2             7.8   2040             0              850       119.612638   
3            17.9   2040             0              850        45.712363   
4             7.8   2040             0              900       125.122464   
...           ...    ...           ...              ...              ...   
770707       26.6   2040           700              700       420.000000   
770708        1.3   2040             0                0         0.000000   
770709        1.3   2040             0                0         0.000000   
770710        3.9   2040             0                0         0.000000   
770711        4.1   2040             0                0         0.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1795.1  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1795.1  Arterial    1.0  D2      1   2   
2       0147_003.1         1        3898.2  Arterial    1.0  D1      1   3   
3       0147_003.1         1        3898.2  Arterial    1.0  D2      1   3   
4       0147_003.9         1        3907.8  Arterial    1.0  D1      1   3   
...            ...       ...           ...       ...    ...  ..    ...  ..   
770707  1084_001.0         1         744.6  Arterial    1.0  D2      1   5   
770708  2865_001.3         2        3543.9  Arterial    1.0  D1      1   4   
770709  2865_001.3         2        3543.9  Arterial    1.0  D2      1   4   
770710  3004_000.9         3         778.5  Arterial    1.0  D1      1   4   
770711  3004_000.9         3         778.5  Arterial    1.0  D2      1   4   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4772      AM  0.1823        6.8   
1          Principal Arterial        1065  0.5228      AM  0.1823        6.2   
2            Minor Arterial           983  0.7239      AM  0.1981       14.4   
3            Minor Arterial           983  0.2761      AM  0.1981       22.2   
4            Minor Arterial           983  0.7258      AM  0.1978       14.3   
...                           ...     ...     ...     ...     ...        ...   
770707          Collector             572  0.6000      DY  1.0000       22.7   
770708          Collector             785  0.6000      DY  1.0000        1.9   
770709          Collector             785  0.6000      DY  1.0000        1.9   
770710          Collector             748  0.6000      DY  1.0000        7.7   
770711          Collector             748  0.6000      DY  1.0000        7.7   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.9   2050          2100             2100       182.686476   
1             4.5   2050          2100             2100       200.143524   
2            15.4   2050          1200             4200       602.299278   
3            29.0   2050          1200             4200       229.720722   
4            15.3   2050          1500             4600       660.390904   
...           ...    ...           ...              ...              ...   
770707       19.6   2050           800              900       540.000000   
770708        1.5   2050          3800             3800      2280.000000   
770709        1.5   2050          3800             3800      2280.000000   
770710        3.6   2050         35500            20000     12000.000000   
770711        3.7   2050         35500            20000     12000.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
770707  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770708  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770709  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770710  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
770711  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82           148   
1          2500             SNP     M01-Jan          0.82           163   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1559.2  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1559.2  Arterial    1.0  D2      1   2   
2       0006_149.9         1        1757.1  Arterial    1.0  D1      1   2   
3       0006_149.9         1        1757.1  Arterial    1.0  D2      1   2   
4       0006_150.6         1        1971.4  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
794983  1084_001.0         1         815.4  Arterial    1.0  D2      1   5   
794984  2865_001.3         2        2783.7  Arterial    1.0  D1      1   4   
794985  2865_001.3         2        2783.7  Arterial    1.0  D2      1   4   
794986  3004_000.9         2        2312.0  Arterial    1.0  D1      1   3   
794987  3004_000.9         2        2312.0  Arterial    1.0  D2      1   3   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.4957      AM  0.1845        6.3   
1          Principal Arterial        1065  0.5043      AM  0.1845        6.2   
2          Principal Arterial        1065  0.4973      AM  0.1661       17.9   
3          Principal Arterial        1065  0.5027      AM  0.1661       17.7   
4          Principal Arterial        1065  0.5234      AM  0.1645       16.5   
...                           ...     ...     ...     ...     ...        ...   
794983          Collector             572  0.6000      DY  1.0000       26.2   
794984          Collector             785  0.6000      DY  1.0000        1.7   
794985          Collector             785  0.6000      DY  1.0000        1.7   
794986       Minor Arterial           939  0.6000      DY  1.0000        7.6   
794987       Minor Arterial           939  0.6000      DY  1.0000        8.6   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.6   2030             0                0              0.0   
1             4.5   2030             0                0              0.0   
2            14.3   2030             0                0              0.0   
3            14.2   2030             0                0              0.0   
4            13.2   2030             0                0              0.0   
...           ...    ...           ...              ...              ...   
794983       20.5   2030           500              550            330.0   
794984        1.3   2030             0                0              0.0   
794985        1.4   2030             0                0              0.0   
794986        3.5   2030             0                0              0.0   
794987        3.8   2030             0                0              0.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
794983  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794984  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794985  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794986  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
794987  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1686.0  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1686.0  Arterial    1.0  D2      1   2   
2       0006_149.9         1        2111.0  Arterial    1.0  D1      1   2   
3       0006_149.9         1        2111.0  Arterial    1.0  D2      1   2   
4       0006_150.6         1        2340.3  Arterial    1.0  D1      1   2   
...            ...       ...           ...       ...    ...  ..    ...  ..   
817219  1084_001.0         1         921.9  Arterial    1.0  D2      1   5   
817220  2865_001.3         2        3192.3  Arterial    1.0  D1      1   4   
817221  2865_001.3         2        3192.3  Arterial    1.0  D2      1   4   
817222  3004_000.9         3        5104.6  Arterial    1.0  D1      1   3   
817223  3004_000.9         3        5104.6  Arterial    1.0  D2      1   3   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5228      AM  0.1855        5.9   
1          Principal Arterial        1065  0.4772      AM  0.1855        6.5   
2          Principal Arterial        1065  0.4810      AM  0.1643       18.0   
3          Principal Arterial        1065  0.5190      AM  0.1643       16.5   
4          Principal Arterial        1065  0.5058      AM  0.1627       16.7   
...                           ...     ...     ...     ...     ...        ...   
817219          Collector             572  0.6000      DY  1.0000       29.1   
817220          Collector             785  0.6000      DY  1.0000        1.8   
817221          Collector             785  0.6000      DY  1.0000        1.8   
817222       Minor Arterial           894  0.6000      DY  1.0000       11.0   
817223       Minor Arterial           894  0.6000      DY  1.0000        9.2   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             4.4   2040             0                0              0.0   
1             4.8   2040             0                0              0.0   
2            15.3   2040             0                0              0.0   
3            14.2   2040             0                0              0.0   
4            14.3   2040             0                0              0.0   
...           ...    ...           ...              ...              ...   
817219       30.4   2040           700              750            450.0   
817220        1.5   2040             0                0              0.0   
817221        1.5   2040             0                0              0.0   
817222        4.8   2040             0             1100            660.0   
817223        3.9   2040             0             1100            660.0   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
817219  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817220  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817221  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817222  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
817223  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82             0   
1          2500             SNP     M01-Jan          0.82             0   
2          2500             

SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP  FGFAC Dir  LANES  FT  \
0       0006_146.9         1        1813.3  Arterial    1.0  D1      1   2   
1       0006_146.9         1        1813.3  Arterial    1.0  D2      1   2   
2       0147_003.1         1         870.4  Arterial    1.0  D1      1   3   
3       0147_003.1         1         870.4  Arterial    1.0  D2      1   3   
4       0147_003.9         1         837.8  Arterial    1.0  D1      1   3   
...            ...       ...           ...       ...    ...  ..    ...  ..   
837823  1084_001.0         1         572.5  Arterial    1.0  D2      1   5   
837824  2865_001.3         2        3583.6  Arterial    1.0  D1      1   4   
837825  2865_001.3         2        3583.6  Arterial    1.0  D2      1   4   
837826  3004_000.9         3        8477.5  Arterial    1.0  D1      1   3   
837827  3004_000.9         3        8477.5  Arterial    1.0  D2      1   3   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
0          Principal Arterial        1065  0.5723      AM  0.1884        5.4   
1          Principal Arterial        1065  0.4277      AM  0.1884        7.2   
2            Minor Arterial           983  0.5086      AM  0.1410       23.1   
3            Minor Arterial           983  0.4914      AM  0.1410       21.4   
4            Minor Arterial           983  0.5152      AM  0.1416       22.9   
...                           ...     ...     ...     ...     ...        ...   
837823          Collector             572  0.6000      DY  1.0000       19.4   
837824          Collector             785  0.6000      DY  1.0000        1.7   
837825          Collector             785  0.6000      DY  1.0000        1.7   
837826       Minor Arterial           894  0.6000      DY  1.0000        9.4   
837827       Minor Arterial           894  0.6000      DY  1.0000        6.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
0             3.9   2050          2100             2100       226.424772   
1             5.3   2050          2100             2100       169.215228   
2            35.6   2050          1200             1200        86.055120   
3            34.2   2050          1200             1200        83.144880   
4            35.2   2050          1500             1500       109.428480   
...           ...    ...           ...              ...              ...   
837823       19.3   2050           800              700       420.000000   
837824        1.6   2050          3800             3800      2280.000000   
837825        1.6   2050          3800             3800      2280.000000   
837826        4.3   2050         35500            27500     16500.000000   
837827        3.0   2050         35500            27500     16500.000000   

        DOWFACFC             SsnGrp      SsnATGroup     SsnVolCls  Vol_From  \
0       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
1       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
2       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
3       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
4       Arterial  StatewideArterial         1-Rural    UTRuralLow         0   
...          ...                ...             ...           ...       ...   
837823  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837824  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837825  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837826  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   
837827  Arterial     RuralRecLowVol  0-AllAreaTypes  0-AllVolumes         0   

         Vol_To SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol  \
0          2500             SNP     M01-Jan          0.82           184   
1          2500             SNP     M01-Jan          0.82           137   
2          2500             

In [68]:
df = dfs_VC[10]

df = df[(df[nameSegID]=='0015_282.2') * (df['VCGroupCode']=='AnnWkPM')]

df

C:\Program Files\ArcGIS\Pro\bin\Python\envs\arcgispro-py3\lib\site-packages\pandas\core\computation\expressions.py:178: UserWarning: evaluating in Python space because the '*' operator is not supported by numexpr for the bool dtype, use '&' instead
  f"evaluating in Python space because the {repr(op_str)} "


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP   FGFAC Dir  LANES  FT  \
414340  0015_282.2         4      251700.9  Arterial  0.0507  D1      2   3   
414341  0015_282.2         4      251700.9  Arterial  0.0507  D2      2   3   
418364  0015_282.2         4      251700.9   Freeway  0.6973  D1      5  23   
418365  0015_282.2         4      251700.9   Freeway  0.6973  D2      5  23   
418366  0015_282.2         4      251700.9   Managed  0.0952  D1      1  38   
418367  0015_282.2         4      251700.9   Managed  0.0952  D2      1  38   
418368  0015_282.2         4      251700.9   CD Road  0.1567  D1      2  21   
418369  0015_282.2         4      251700.9   CD Road  0.1567  D2      2  21   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
414340       Minor Arterial           978  0.5159      PM  0.2931       11.9   
414341       Minor Arterial           972  0.4841      PM  0.2931        9.4   
418364           Freeway             1995  0.5574      PM  0.2394       12.9   
418365           Freeway             1995  0.4426      PM  0.2394       10.2   
418366           Freeway             1767  0.3612      PM  0.2929        0.0   
418367           Freeway             1767  0.6388      PM  0.2929        0.0   
418368           Freeway             1473  0.5343      PM  0.3157        5.3   
418369           Freeway             1473  0.4657      PM  0.3157        6.7   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
414340        3.8   2050        307000           309000      2368.905766   
414341        3.3   2050        307000           309000      2222.886764   
418364        6.4   2050        307000           309000     28752.079134   
418365        5.9   2050        307000           309000     22830.409446   
418366        0.0   2050        307000           309000      3112.164476   
418367        0.0   2050        307000           309000      5504.016244   
418368        1.9   2050        307000           309000      8167.464058   
418369        2.4   2050        307000           309000      7118.824652   

          DOWFACFC      SsnGrp SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
414340  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
414341  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418364  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418365  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418366  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418367  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418368  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418369  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
414340             SNU     S00-Ann           1.0          2368          WD3   
414341             SNU     S00-Ann           1.0          2222          WD3   
418364             SN7     S00-Ann           1.0         28752          WDA   
418365             SN7     S00-Ann           1.0         22830          WDA   
418366             SN7     S00-Ann           1.0          3112          WDA   
418367             SN7     S00-Ann           1.0          5504          WDA   
418368             SN7     S00-Ann           1.0          8167          WDA   
418369             SN7     S00-Ann           1.0          7118          WDA   

          DOWGroup  DOWFactor  AvgSsnDOWPrdVol Prd HrPctOf  VolPkHrPct  \
414340  W1-Weekday       1.07             2543  PM     Prd      0.3638   
414341  W1-Weekday       1.07             2386  PM     Prd      0.3638   
418364  W1-Weekday       1.06            30390  PM     Prd      0.3499   
418365  W1-Weekday       1.06            24131  PM     Prd      0.3499   
418366  W1-Weekday       1.06             3289  PM     Prd      0.3499   
418367  W1-Weekday       1.06       

In [69]:
df_VC.columns

Index(['SEGID', 'AREATYPE', 'SegDYVol_TDM', 'FUNCGROUP', 'FGFAC', 'Dir',
       'LANES', 'FT', 'FTCLASS', 'CAP1HL', 'DFAC', 'Prd_TDM', 'PRDFAC',
       'MDPERCENT', 'HVPERCENT', 'FYEAR', 'ForecastAADT', 'ForecastAADTAdj',
       'AvgAnnualPrdVol', 'DOWFACFC', 'SsnGrp', 'SsnATGroup', 'SsnVolCls',
       'Vol_From', 'Vol_To', 'SiteGroupSeason', 'SeasonGroup', 'SeasonFactor',
       'AvgSsnPrdVol', 'SiteGroupDOW', 'DOWGroup', 'DOWFactor',
       'AvgSsnDOWPrdVol', 'Prd', 'HrPctOf', 'VolPkHrPct', 'SeasonType',
       'VCGroupCode', 'PrdHrs', 'AvgSsnDOWPkHrVol', 'TrkFac', 'PrdPCEFlow',
       'PkHrPCEFlow', 'PrdVC', 'PkHrVC', 'PHF', 'Pk15PCEFlow', 'Pk15VC'],
      dtype='object')

In [70]:
dfs_VC_MaxDirFG = []

for df_VC in dfs_VC:

    df_VC_MaxDirFG = df_VC.groupby([nameSegID,namePrd,'SeasonGroup','DOWGroup','HrPctOf','VCGroupCode'], as_index=False).agg({nameDir:[np.size],nameCap1HL:[np.sum],'PrdPCEFlow':[np.sum],'PkHrPCEFlow':[np.sum],'Pk15PCEFlow':[np.sum],'PrdVC':[np.max],'PkHrVC':[np.max],'Pk15VC':[np.max]})

    df_VC_MaxDirFG.columns = ([nameSegID,namePrd,'SeasonGroup','DOWGroup','HrPctOf','VCGroupCode','numRecords',nameCap1HL+'Sum','PrdPCEFlowSum','PkHrPCEFlowSum','Pk15PCEFlowSum','PrdVCMax','PkHrVCMax','Pk15VCMax'])
    
    dfs_VC_MaxDirFG.append(df_VC_MaxDirFG)
    
    display(df_VC_MaxDirFG)
                                            
    #df_Peak_VC_wGroups = pd.DataFrame.merge(df_VCGroups,df_Peak_VC,on=('SeasonGroup','DOWGroup','Prd','HrPctOf'))

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
369031   WFRC_8218  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
369032   WFRC_8218  PM     S03-Sum    5-Friday      DY     SumFrPM   
369033   WFRC_8218  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
369034   WFRC_8218  PM     S04-Fal    5-Friday      DY     FalFrPM   
369035   WFRC_8218  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
369031           2       2946           2628            2922            2997   
369032           2       2946          12619            3225            3291   
369033           2       2946           2621            2923            2998   
369034           2       2946          12507            3263            3330   
369035           2       2946           2597            2868            2972   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
369031      0.92       1.03       1.05  
369032      4.28       1.10       1.12  
369033      0.92       1.03       1.05  
369034      4.25       1.11       1.13  
369035      0.91       1.01       1.03  

[369036 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
373723   WFRC_8218  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
373724   WFRC_8218  PM     S03-Sum    5-Friday      DY     SumFrPM   
373725   WFRC_8218  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
373726   WFRC_8218  PM     S04-Fal    5-Friday      DY     FalFrPM   
373727   WFRC_8218  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
373723           2       2946           2823            3139            3204   
373724           2       2946          13636            3484            3556   
373725           2       2946           2816            3140            3205   
373726           2       2946          13514            3526            3598   
373727           2       2946           2790            3082            3145   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
373723      0.98       1.09       1.11  
373724      4.63       1.18       1.21  
373725      0.97       1.09       1.11  
373726      4.59       1.20       1.22  
373727      0.96       1.07       1.09  

[373728 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
382393   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
382394   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
382395   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
382396   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
382397   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
382393           2       1878            631             720             817   
382394           2       1878           3126             837             951   
382395           2       1878            657             762             865   
382396           2       1878           3021             839             953   
382397           2       1878            635             726             826   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
382393      0.34       0.39       0.44  
382394      1.67       0.45       0.51  
382395      0.35       0.41       0.47  
382396      1.61       0.45       0.51  
382397      0.34       0.39       0.45  

[382398 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
387595   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
387596   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
387597   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
387598   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
387599   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
387595           2       1878            620             708             803   
387596           2       1878           3232             864             984   
387597           2       1878            645             748             849   
387598           2       1878           3124             868             986   
387599           2       1878            624             715             812   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
387595      0.34       0.39       0.44  
387596      1.72       0.46       0.52  
387597      0.35       0.41       0.47  
387598      1.66       0.46       0.53  
387599      0.34       0.39       0.45  

[387600 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
396571   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
396572   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
396573   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
396574   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
396575   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130            102             127             144   
1                2       2130            109             135             154   
2                2       2130            120             148             169   
3                2       2130            128             160             182   
4                2       2130            135             167             190   
...            ...        ...            ...             ...             ...   
396571           2       1878           1629            1855            1995   
396572           2       1878           6956            1863            2003   
396573           2       1878           1693            1962            2087   
396574           2       1878           6726            1868            2009   
396575           2       1878           1636            1873            1992   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.06       0.07       0.08  
1           0.06       0.07       0.08  
2           0.06       0.08       0.09  
3           0.07       0.09       0.10  
4           0.07       0.09       0.10  
...          ...        ...        ...  
396571      0.91       1.04       1.09  
396572      3.71       0.99       1.07  
396573      0.94       1.09       1.15  
396574      3.58       1.00       1.07  
396575      0.91       1.04       1.10  

[396576 rows x 14 columns]

...

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
373723   WFRC_8218  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
373724   WFRC_8218  PM     S03-Sum    5-Friday      DY     SumFrPM   
373725   WFRC_8218  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
373726   WFRC_8218  PM     S04-Fal    5-Friday      DY     FalFrPM   
373727   WFRC_8218  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
373723           2       2946           3416            3799            3876   
373724           2       2946          17132            4378            4467   
373725           2       2946           3407            3801            3878   
373726           2       2946          16980            4431            4521   
373727           2       2946           3377            3729            3805   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
373723      1.18       1.31       1.34  
373724      5.82       1.49       1.52  
373725      1.18       1.31       1.34  
373726      5.77       1.50       1.54  
373727      1.17       1.29       1.32  

[373728 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
373723   WFRC_8218  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
373724   WFRC_8218  PM     S03-Sum    5-Friday      DY     SumFrPM   
373725   WFRC_8218  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
373726   WFRC_8218  PM     S04-Fal    5-Friday      DY     FalFrPM   
373727   WFRC_8218  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130             99             123             140   
1                2       2130            105             132             149   
2                2       2130            117             144             163   
3                2       2130            125             155             178   
4                2       2130            132             163             184   
...            ...        ...            ...             ...             ...   
373723           2       2946           3467            3854            3933   
373724           2       2946          18619            4758            4856   
373725           2       2946           3457            3856            3935   
373726           2       2946          18454            4816            4914   
373727           2       2946           3426            3783            3860   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.05       0.06       0.07  
1           0.05       0.06       0.07  
2           0.06       0.07       0.08  
3           0.06       0.08       0.09  
4           0.07       0.08       0.09  
...          ...        ...        ...  
373723      1.19       1.32       1.35  
373724      6.32       1.62       1.65  
373725      1.19       1.32       1.35  
373726      6.27       1.64       1.67  
373727      1.18       1.30       1.33  

[373728 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
382597   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
382598   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
382599   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
382600   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
382601   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
382597           2       1878            582             663             754   
382598           2       1878           3024             810             920   
382599           2       1878            604             700             796   
382600           2       1878           2924             812             922   
382601           2       1878            585             669             760   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
382597      0.32       0.37       0.42  
382598      1.61       0.43       0.49  
382599      0.34       0.39       0.44  
382600      1.56       0.43       0.49  
382601      0.33       0.37       0.42  

[382602 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
387901   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
387902   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
387903   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
387904   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
387905   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130              0               0               0   
1                2       2130              0               0               0   
2                2       2130              0               0               0   
3                2       2130              0               0               0   
4                2       2130              0               0               0   
...            ...        ...            ...             ...             ...   
387901           2       1878            629             717             815   
387902           2       1878           3224             862             980   
387903           2       1878            654             758             861   
387904           2       1878           3116             866             984   
387905           2       1878            632             724             822   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.00       0.00       0.00  
1           0.00       0.00       0.00  
2           0.00       0.00       0.00  
3           0.00       0.00       0.00  
4           0.00       0.00       0.00  
...          ...        ...        ...  
387901      0.34       0.39       0.44  
387902      1.72       0.46       0.52  
387903      0.36       0.41       0.47  
387904      1.66       0.46       0.52  
387905      0.34       0.39       0.45  

[387906 rows x 14 columns]

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  \
0       0006_146.9  AM     M01-Jan  W1-Weekday     Prd     JanWkAM   
1       0006_146.9  AM     M02-Feb  W1-Weekday     Prd     FebWkAM   
2       0006_146.9  AM     M03-Mar  W1-Weekday     Prd     MarWkAM   
3       0006_146.9  AM     M04-Apr  W1-Weekday     Prd     AprWkAM   
4       0006_146.9  AM     M05-May  W1-Weekday     Prd     MayWkAM   
...            ...  ..         ...         ...     ...         ...   
396877   WFRC_8219  PM     S02-Spr  W1-Weekday     Prd     SprWkPM   
396878   WFRC_8219  PM     S03-Sum    5-Friday      DY     SumFrPM   
396879   WFRC_8219  PM     S03-Sum  W1-Weekday     Prd     SumWkPM   
396880   WFRC_8219  PM     S04-Fal    5-Friday      DY     FalFrPM   
396881   WFRC_8219  PM     S04-Fal  W1-Weekday     Prd     FalWkPM   

        numRecords  CAP1HLSum  PrdPCEFlowSum  PkHrPCEFlowSum  Pk15PCEFlowSum  \
0                2       2130            103             128             145   
1                2       2130            109             135             154   
2                2       2130            120             148             169   
3                2       2130            130             161             183   
4                2       2130            136             168             191   
...            ...        ...            ...             ...             ...   
396877           2       1878           1535            1750            1901   
396878           2       1878           7183            1923            2025   
396879           2       1878           1596            1850            1989   
396880           2       1878           6945            1929            2030   
396881           2       1878           1542            1765            1918   

        PrdVCMax  PkHrVCMax  Pk15VCMax  
0           0.06       0.07       0.08  
1           0.06       0.07       0.08  
2           0.06       0.08       0.09  
3           0.07       0.09       0.10  
4           0.07       0.09       0.10  
...          ...        ...        ...  
396877      0.85       0.97       1.04  
396878      3.83       1.03       1.08  
396879      0.89       1.03       1.08  
396880      3.70       1.03       1.08  
396881      0.86       0.98       1.05  

[396882 rows x 14 columns]

In [71]:
display(df_Scenarios)

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [72]:
df = dfs_VC[10]

df = df[(df[nameSegID]=='0015_295.6') * (df['VCGroupCode']=='AnnWkPM')]

display(df)

df = dfs_VC_MaxDirFG[10]

df = df[(df[nameSegID]=='0015_295.6')]

pd.set_option('display.max_columns', None)

display(df)

C:\Program Files\ArcGIS\Pro\bin\Python\envs\arcgispro-py3\lib\site-packages\pandas\core\computation\expressions.py:178: UserWarning: evaluating in Python space because the '*' operator is not supported by numexpr for the bool dtype, use '&' instead
  f"evaluating in Python space because the {repr(op_str)} "


SEGID  AREATYPE  SegDYVol_TDM FUNCGROUP   FGFAC Dir  LANES  FT  \
418422  0015_295.6         4      387718.0   Freeway  0.7087  D1      5  24   
418423  0015_295.6         4      387718.0   Freeway  0.7087  D2      5  24   
418424  0015_295.6         4      387718.0   Managed  0.0824  D1      2  38   
418425  0015_295.6         4      387718.0   Managed  0.0824  D2      2  38   
418426  0015_295.6         4      387718.0   CD Road  0.2089  D1      2  31   
418427  0015_295.6         4      387718.0   CD Road  0.2089  D2      2  31   

                          FTCLASS  CAP1HL    DFAC Prd_TDM  PRDFAC  MDPERCENT  \
418422           Freeway             2135  0.4781      PM  0.1990       14.2   
418423           Freeway             2135  0.5219      PM  0.1990       10.3   
418424           Freeway             1767  0.3572      PM  0.3413        0.0   
418425           Freeway             1767  0.6428      PM  0.3413        0.0   
418426           Freeway             1473  0.5895      PM  0.1892       11.2   
418427           Freeway             1473  0.4105      PM  0.1892       10.8   

        HVPERCENT  FYEAR  ForecastAADT  ForecastAADTAdj  AvgAnnualPrdVol  \
418422        7.1   2050        327500           325000     21913.795972   
418423        5.2   2050        327500           325000     23921.376528   
418424        0.0   2050        327500           325000      3264.813001   
418425        0.0   2050        327500           325000      5875.200999   
418426        4.8   2050        327500           325000      7572.281360   
418427        4.7   2050        327500           325000      5272.979641   

          DOWFACFC      SsnGrp SsnATGroup     SsnVolCls  Vol_From   Vol_To  \
418422  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418423  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418424  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418425  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418426  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   
418427  FreewayI15  FreewayI15    4-Urban  0-AllVolumes         0  1000000   

       SiteGroupSeason SeasonGroup  SeasonFactor  AvgSsnPrdVol SiteGroupDOW  \
418422             SN7     S00-Ann           1.0         21913          WDA   
418423             SN7     S00-Ann           1.0         23921          WDA   
418424             SN7     S00-Ann           1.0          3264          WDA   
418425             SN7     S00-Ann           1.0          5875          WDA   
418426             SN7     S00-Ann           1.0          7572          WDA   
418427             SN7     S00-Ann           1.0          5272          WDA   

          DOWGroup  DOWFactor  AvgSsnDOWPrdVol Prd HrPctOf  VolPkHrPct  \
418422  W1-Weekday       1.06            23162  PM     Prd      0.3499   
418423  W1-Weekday       1.06            25284  PM     Prd      0.3499   
418424  W1-Weekday       1.06             3450  PM     Prd      0.3499   
418425  W1-Weekday       1.06             6209  PM     Prd      0.3499   
418426  W1-Weekday       1.06             8003  PM     Prd      0.3499   
418427  W1-Weekday       1.06             5572  PM     Prd      0.3499   

       SeasonType VCGroupCode  PrdHrs  AvgSsnDOWPkHrVol  TrkFac  PrdPCEFlow  \
418422     Season     AnnWkPM       3         8104.3838  1.0639        8214   
418423     Season     AnnWkPM       3         8846.8716  1.0466        8820   
418424     Season     AnnWkPM       3         1207.1550  1.0000        1150   
418425     Season     AnnWkPM       3         2172.5291  1.0000        2069   
418426     Season     AnnWkPM       3         2800.2497  1.0464        2791   
418427     Season     AnnWkPM       3         1949.6428  1.0451        1941   

        PkHrPCEFlow  PrdVC  PkHrVC   PHF  Pk15PCEFlow  Pk15VC  
418422         8622   0.77    0.81  0.92         9372    0.88  
418423         9259   0.83    0.87  0.95         9746    0.91  

SEGID Prd SeasonGroup    DOWGroup HrPctOf VCGroupCode  numRecords  \
7650  0015_295.6  AM     M01-Jan  W1-Weekday     Prd     JanWkAM           6   
7651  0015_295.6  AM     M02-Feb  W1-Weekday     Prd     FebWkAM           6   
7652  0015_295.6  AM     M03-Mar  W1-Weekday     Prd     MarWkAM           6   
7653  0015_295.6  AM     M04-Apr  W1-Weekday     Prd     AprWkAM           6   
7654  0015_295.6  AM     M05-May  W1-Weekday     Prd     MayWkAM           6   
7655  0015_295.6  AM     M06-Jun  W1-Weekday     Prd     JunWkAM           6   
7656  0015_295.6  AM     M07-Jul  W1-Weekday     Prd     JulWkAM           6   
7657  0015_295.6  AM     M08-Aug  W1-Weekday     Prd     AugWkAM           6   
7658  0015_295.6  AM     M09-Sep  W1-Weekday     Prd     SepWkAM           6   
7659  0015_295.6  AM     M10-Oct  W1-Weekday     Prd     OctWkAM           6   
7660  0015_295.6  AM     M11-Nov  W1-Weekday     Prd     NovWkAM           6   
7661  0015_295.6  AM     M12-Dec  W1-Weekday     Prd     DecWkAM           6   
7662  0015_295.6  AM     S00-Ann  W1-Weekday     Prd     AnnWkAM           6   
7663  0015_295.6  AM     S01-Win  W1-Weekday     Prd     WinWkAM           6   
7664  0015_295.6  AM     S02-Spr  W1-Weekday     Prd     SprWkAM           6   
7665  0015_295.6  AM     S03-Sum  W1-Weekday     Prd     SumWkAM           6   
7666  0015_295.6  AM     S04-Fal  W1-Weekday     Prd     FalWkAM           6   
7667  0015_295.6  DY     M01-Jan  6-Saturday      DY     JanSaDY           6   
7668  0015_295.6  DY     M01-Jan    7-Sunday      DY     JanSuDY           6   
7669  0015_295.6  DY     M02-Feb  6-Saturday      DY     FebSaDY           6   
7670  0015_295.6  DY     M02-Feb    7-Sunday      DY     FebSuDY           6   
7671  0015_295.6  DY     M03-Mar  6-Saturday      DY     MarSaDY           6   
7672  0015_295.6  DY     M03-Mar    7-Sunday      DY     MarSuDY           6   
7673  0015_295.6  DY     M04-Apr  6-Saturday      DY     AprSaDY           6   
7674  0015_295.6  DY     M04-Apr    7-Sunday      DY     AprSuDY           6   
7675  0015_295.6  DY     M05-May  6-Saturday      DY     MaySaDY           6   
7676  0015_295.6  DY     M05-May    7-Sunday      DY     MaySuDY           6   
7677  0015_295.6  DY     M06-Jun  6-Saturday      DY     JunSaDY           6   
7678  0015_295.6  DY     M06-Jun    7-Sunday      DY     JunSuDY           6   
7679  0015_295.6  DY     M07-Jul  6-Saturday      DY     JulSaDY           6   
7680  0015_295.6  DY     M07-Jul    7-Sunday      DY     JulSuDY           6   
7681  0015_295.6  DY     M08-Aug  6-Saturday      DY     AugSaDY           6   
7682  0015_295.6  DY     M08-Aug    7-Sunday      DY     AugSuDY           6   
7683  0015_295.6  DY     M09-Sep  6-Saturday      DY     SepSaDY           6   
7684  0015_295.6  DY     M09-Sep    7-Sunday      DY     SepSuDY           6   
7685  0015_295.6  DY     M10-Oct  6-Saturday      DY     OctSaDY           6   
7686  0015_295.6  DY     M10-Oct    7-Sunday      DY     OctSuDY           6   
7687  0015_295.6  DY     M11-Nov  6-Saturday      DY     NovSaDY           6   
7688  0015_295.6  DY     M11-Nov    7-Sunday      DY     NovSuDY           6   
7689  0015_295.6  DY     M12-Dec  6-Saturday      DY     DecSaDY           6   
7690  0015_295.6  DY     M12-Dec    7-Sunday      DY     DecSuDY           6   
7691  0015_295.6  DY     S00-Ann  6-Saturday      DY     AnnSaDY           6   
7692  0015_295.6  DY     S00-Ann    7-Sunday      DY     AnnSuDY           6   
7693  0015_295.6  DY     S01-Win  6-Saturday      DY     WinSaDY           6   
7694  0015_295.6  DY     S01-Win    7-Sunday      DY     WinSuDY           6   
7695  0015_295.6  DY     S02-Spr  6-Saturday      DY     SprSaDY           6   
7696  0015_295.6  DY     S02-Spr    7-Sunday      DY     SprSuDY           6   
7697  0015_295.6  DY     S03-Sum  6-Saturday      DY     SumSaDY           6   
7698  0015_295.6  DY     S03-Sum    7-Sunday      DY     SumSuDY           6   
7699  0015_

# VC Groups as Columns

In [73]:
df_VCGroups

SeasonGroup SeasonType    DOWGroup HrPctOf Prd VCGroupCode
VCGroupID                                                           
0             S00-Ann     Season  W1-Weekday     Prd  AM     AnnWkAM
1             S01-Win     Season  W1-Weekday     Prd  AM     WinWkAM
2             S02-Spr     Season  W1-Weekday     Prd  AM     SprWkAM
3             S03-Sum     Season  W1-Weekday     Prd  AM     SumWkAM
4             S04-Fal     Season  W1-Weekday     Prd  AM     FalWkAM
5             M01-Jan      Month  W1-Weekday     Prd  AM     JanWkAM
6             M02-Feb      Month  W1-Weekday     Prd  AM     FebWkAM
7             M03-Mar      Month  W1-Weekday     Prd  AM     MarWkAM
8             M04-Apr      Month  W1-Weekday     Prd  AM     AprWkAM
9             M05-May      Month  W1-Weekday     Prd  AM     MayWkAM
10            M06-Jun      Month  W1-Weekday     Prd  AM     JunWkAM
11            M07-Jul      Month  W1-Weekday     Prd  AM     JulWkAM
12            M08-Aug      Month  W1-Weekday     Prd  AM     AugWkAM
13            M09-Sep      Month  W1-Weekday     Prd  AM     SepWkAM
14            M10-Oct      Month  W1-Weekday     Prd  AM     OctWkAM
15            M11-Nov      Month  W1-Weekday     Prd  AM     NovWkAM
16            M12-Dec      Month  W1-Weekday     Prd  AM     DecWkAM
17            S00-Ann     Season  W1-Weekday     Prd  MD     AnnWkMD
18            S01-Win     Season  W1-Weekday     Prd  MD     WinWkMD
19            S02-Spr     Season  W1-Weekday     Prd  MD     SprWkMD
20            S03-Sum     Season  W1-Weekday     Prd  MD     SumWkMD
21            S04-Fal     Season  W1-Weekday     Prd  MD     FalWkMD
22            M01-Jan      Month  W1-Weekday     Prd  MD     JanWkMD
23            M02-Feb      Month  W1-Weekday     Prd  MD     FebWkMD
24            M03-Mar      Month  W1-Weekday     Prd  MD     MarWkMD
25            M04-Apr      Month  W1-Weekday     Prd  MD     AprWkMD
26            M05-May      Month  W1-Weekday     Prd  MD     MayWkMD
27            M06-Jun      Month  W1-Weekday     Prd  MD     JunWkMD
28            M07-Jul      Month  W1-Weekday     Prd  MD     JulWkMD
29            M08-Aug      Month  W1-Weekday     Prd  MD     AugWkMD
30            M09-Sep      Month  W1-Weekday     Prd  MD     SepWkMD
31            M10-Oct      Month  W1-Weekday     Prd  MD     OctWkMD
32            M11-Nov      Month  W1-Weekday     Prd  MD     NovWkMD
33            M12-Dec      Month  W1-Weekday     Prd  MD     DecWkMD
34            S00-Ann     Season  W1-Weekday     Prd  PM     AnnWkPM
35            S01-Win     Season  W1-Weekday     Prd  PM     WinWkPM
36            S02-Spr     Season  W1-Weekday     Prd  PM     SprWkPM
37            S03-Sum     Season  W1-Weekday     Prd  PM     SumWkPM
38            S04-Fal     Season  W1-Weekday     Prd  PM     FalWkPM
39            M01-Jan      Month  W1-Weekday     Prd  PM     JanWkPM
40            M02-Feb      Month  W1-Weekday     Prd  PM     FebWkPM
41            M03-Mar      Month  W1-Weekday     Prd  PM     MarWkPM
42            M04-Apr      Month  W1-Weekday     Prd  PM     AprWkPM
43            M05-May      Month  W1-Weekday     Prd  PM     MayWkPM
44            M06-Jun      Month  W1-Weekday     Prd  PM     JunWkPM
45            M07-Jul      Month  W1-Weekday     Prd  PM     JulWkPM
46            M08-Aug      Month  W1-Weekday     Prd  PM     AugWkPM
47            M09-Sep      Month  W1-Weekday     Prd  PM     SepWkPM
48            M10-Oct      Month  W1-Weekday     Prd  PM     OctWkPM
49            M11-Nov      Month  W1-Weekday     Prd  PM     NovWkPM
50            M12-Dec      Month  W1-Weekday     Prd  PM     DecWkPM
51            S00-Ann     Season    5-Friday      DY  PM     AnnFrPM
52            S01-Win     Season    5-Friday      DY  PM     WinFrPM
53            S02-Spr     Season    5-Friday      DY  PM     SprFrPM
54            S03-Sum     Season    5-Friday      DY  PM     SumFrPM
55            S04-Fal     Season    5-Friday      DY  PM     FalFrPM
56      

In [74]:
dfs_VC_MaxDirFG_wVCGroups_15 = []

for df_VC_MaxDirFG in dfs_VC_MaxDirFG:

    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG[['VCGroupCode','SEGID','Pk15VCMax']].copy()
    
    df_VC_MaxDirFG_wVCGroups_15['VCGroupCode'] = df_VC_MaxDirFG_wVCGroups_15['VCGroupCode'] + "15"
    
    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG_wVCGroups_15.round({'Pk15VC': 2})
    
    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG_wVCGroups_15.pivot(index='SEGID', columns="VCGroupCode",values='Pk15VCMax')
    
    df_VC_MaxDirFG_wVCGroups_15 = df_VC_MaxDirFG_wVCGroups_15.reset_index()
    
    dfs_VC_MaxDirFG_wVCGroups_15.append(df_VC_MaxDirFG_wVCGroups_15)

    display(df_VC_MaxDirFG_wVCGroups_15)
    

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3613          WFRC_8208       0.00       0.00       0.00       0.00   
3614          WFRC_8209       0.04       0.03       0.02       0.03   
3615          WFRC_8213       0.06       0.05       0.03       0.03   
3616          WFRC_8215       0.18       0.12       0.09       0.13   
3617          WFRC_8218       1.12       0.70       0.56       0.82   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.05       0.07       0.05       0.03       0.03   
3616              0.11       0.17       0.18       0.12       0.09       0.13   
3617              0.71       1.03       1.13       0.71       0.58       0.84   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.06       0.06       0.05       0.03       0.03   
3616              0.11       0.17       0.18       0.12       0.09       0.13   
3617              0.72       1.05       1.13       0.68       0.55       0.83   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.06       0.06       0.05       0.03       0.03   
3616              0.11       0.18       0.17       0.12       0.09       0.12   
3617              0.71       1.04       1.08       0.71       0.57       0.81   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.08       0.06       0.04       0.04   
3660          WFRC_8215       0.23       0.18       0.16       0.16   
3661          WFRC_8216       0.34       0.12       0.09       0.35   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.21       0.75       0.61       0.90   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.07       0.08       0.06       0.04       0.04   
3660              0.12       0.24       0.24       0.19       0.16       0.16   
3661              0.16       0.46       0.34       0.12       0.09       0.36   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.77       1.09       1.22       0.77       0.62       0.92   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.07       0.08       0.06       0.04       0.04   
3660              0.12       0.24       0.25       0.19       0.17       0.17   
3661              0.16       0.46       0.36       0.11       0.09       0.37   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.78       1.11       1.23       0.73       0.59       0.91   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.07       0.08       0.06       0.04       0.04   
3660              0.12       0.26       0.22       0.18       0.15       0.15   
3661              0.17       0.47       0.31       0.12       0.09       0.33   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.77       1.10       1.17       0.77       0.62       0.91   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3744          WFRC_8215       0.30       0.20       0.16       0.24   
3745          WFRC_8216       0.40       0.14       0.11       0.39   
3746          WFRC_8217       0.00       0.00       0.00       0.00   
3747          WFRC_8218       1.32       0.82       0.66       0.99   
3748          WFRC_8219       0.49       0.39       0.34       0.32   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.18       0.31       0.31       0.20       0.16       0.25   
3745              0.20       0.52       0.40       0.14       0.11       0.40   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.85       1.18       1.33       0.84       0.68       0.99   
3748              0.23       0.44       0.50       0.39       0.35       0.32   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.19       0.32       0.31       0.20       0.16       0.25   
3745              0.20       0.53       0.43       0.14       0.11       0.41   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.87       1.21       1.33       0.80       0.64       1.00   
3748              0.23       0.44       0.52       0.40       0.35       0.33   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.19       0.33       0.29       0.20       0.16       0.23   
3745              0.20       0.54       0.38       0.14       0.10       0.37   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.85       1.20       1.27       0.83       0.67       0.97   
3748              0.24       0.47       0.46       0.38       0.33       0.30   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3795          WFRC_8215       0.42       0.28       0.22       0.35   
3796          WFRC_8216       0.51       0.17       0.14       0.47   
3797          WFRC_8217       0.00       0.00       0.00       0.00   
3798          WFRC_8218       1.48       0.92       0.74       1.09   
3799          WFRC_8219       0.51       0.40       0.35       0.32   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.25       0.44       0.42       0.28       0.22       0.36   
3796              0.26       0.57       0.51       0.18       0.14       0.48   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.95       1.21       1.49       0.91       0.76       1.12   
3799              0.24       0.44       0.52       0.41       0.36       0.32   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.25       0.45       0.43       0.27       0.21       0.36   
3796              0.27       0.57       0.54       0.17       0.13       0.50   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.97       1.24       1.50       0.89       0.72       1.10   
3799              0.25       0.44       0.54       0.41       0.36       0.33   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.26       0.46       0.41       0.27       0.22       0.34   
3796              0.27       0.59       0.47       0.18       0.13       0.44   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.95       1.23       1.43       0.90       0.75       1.07   
3799              0.26       0.47       0.47       0.39       0.34       0.29   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.09   
1            0006_149.9       0.31       0.29       0.27       0.21   
2            0006_150.6       0.31       0.29       0.27       0.20   
3            0006_152.6       0.34       0.32       0.30       0.21   
4            0006_152.9       0.47       0.31       0.24       0.39   
...                 ...        ...        ...        ...        ...   
3883          WFRC_8215       0.55       0.36       0.29       0.47   
3884          WFRC_8216       0.63       0.22       0.17       0.59   
3885          WFRC_8217       1.68       1.11       0.90       1.08   
3886          WFRC_8218       1.66       1.00       0.83       1.20   
3887          WFRC_8219       1.03       0.86       0.75       0.68   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.10   
1                 0.15       0.27       0.30       0.28       0.27       0.20   
2                 0.15       0.26       0.30       0.28       0.27       0.19   
3                 0.17       0.24       0.32       0.30       0.29       0.20   
4                 0.29       0.45       0.47       0.32       0.25       0.40   
...                ...        ...        ...        ...        ...        ...   
3883              0.33       0.58       0.55       0.37       0.29       0.48   
3884              0.32       0.76       0.63       0.22       0.18       0.60   
3885              1.00       1.33       1.68       1.12       0.91       1.10   
3886              1.03       1.33       1.67       1.00       0.85       1.23   
3887              0.50       1.08       1.05       0.87       0.77       0.69   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.12       0.15       0.15       0.14       0.10   
1                 0.15       0.27       0.35       0.32       0.31       0.23   
2                 0.15       0.26       0.35       0.32       0.31       0.22   
3                 0.16       0.24       0.38       0.35       0.34       0.23   
4                 0.29       0.45       0.48       0.30       0.24       0.40   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.58       0.56       0.36       0.28       0.48   
3884              0.32       0.76       0.67       0.21       0.17       0.62   
3885              1.01       1.34       1.71       1.08       0.91       1.10   
3886              1.05       1.36       1.68       0.97       0.81       1.21   
3887              0.51       1.09       1.08       0.89       0.78       0.71   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.17       0.31       0.28       0.27       0.25       0.18   
2                 0.17       0.30       0.28       0.27       0.25       0.17   
3                 0.19       0.28       0.31       0.29       0.27       0.18   
4                 0.29       0.47       0.46       0.31       0.24       0.38   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.60       0.54       0.36       0.28       0.45   
3884              0.32       0.79       0.59       0.22       0.16       0.56   
3885              1.02       1.39       1.63       1.10       0.92       1.04   
3886              1.03       1.35       1.60       0.99       0.84       1.18   
3887              0.53       1.16       0.99       0.84       0.72       0.63   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.10       0.15       0.14       0.14       0.10   
1                 0.13       0.24       0.31       0.29       0.28

...

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.06       0.06       0.06       0.05   
2            0006_150.6       0.06       0.06       0.06       0.05   
3            0006_152.6       0.08       0.08       0.08       0.07   
4            0006_152.9       0.10       0.08       0.07       0.09   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.09       0.07       0.05       0.05   
3660          WFRC_8215       0.39       0.26       0.20       0.33   
3661          WFRC_8216       0.52       0.18       0.14       0.50   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.52       0.91       0.77       1.09   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.07       0.07       0.06       0.06       0.05   
2                 0.03       0.07       0.07       0.06       0.07       0.06   
3                 0.04       0.09       0.09       0.08       0.09       0.07   
4                 0.05       0.11       0.10       0.08       0.07       0.09   
...                ...        ...        ...        ...        ...        ...   
3659              0.06       0.10       0.09       0.07       0.05       0.05   
3660              0.23       0.42       0.39       0.26       0.21       0.34   
3661              0.27       0.66       0.52       0.18       0.15       0.51   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.95       1.32       1.54       0.93       0.78       1.11   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.07       0.06       0.06       0.06       0.06   
2                 0.03       0.07       0.07       0.07       0.06       0.06   
3                 0.04       0.09       0.09       0.09       0.08       0.08   
4                 0.05       0.11       0.11       0.08       0.07       0.09   
...                ...        ...        ...        ...        ...        ...   
3659              0.06       0.10       0.09       0.07       0.05       0.05   
3660              0.23       0.42       0.40       0.25       0.20       0.34   
3661              0.28       0.66       0.55       0.18       0.14       0.53   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.97       1.35       1.54       0.92       0.74       1.09   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.08       0.05       0.05       0.05       0.05   
2                 0.04       0.08       0.06       0.06       0.05       0.05   
3                 0.05       0.10       0.07       0.07       0.07       0.06   
4                 0.05       0.12       0.09       0.08       0.07       0.08   
...                ...        ...        ...        ...        ...        ...   
3659              0.06       0.10       0.09       0.07       0.05       0.04   
3660              0.24       0.43       0.38       0.26       0.20       0.32   
3661              0.28       0.68       0.49       0.18       0.13       0.47   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.95       1.34       1.47       0.93       0.78       1.07   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.06       0.06       0.06       0.06

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.08   
1            0006_149.9       0.39       0.36       0.34       0.33   
2            0006_150.6       0.39       0.37       0.35       0.33   
3            0006_152.6       0.46       0.43       0.41       0.40   
4            0006_152.9       0.59       0.39       0.31       0.62   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.12       0.09       0.06       0.06   
3660          WFRC_8215       0.48       0.32       0.25       0.40   
3661          WFRC_8216       0.63       0.21       0.17       0.61   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.65       0.99       0.83       1.19   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.09   
1                 0.18       0.39       0.37       0.35       0.33       0.33   
2                 0.19       0.39       0.37       0.35       0.34       0.33   
3                 0.22       0.45       0.44       0.41       0.40       0.39   
4                 0.35       0.72       0.59       0.40       0.31       0.64   
...                ...        ...        ...        ...        ...        ...   
3659              0.08       0.15       0.12       0.09       0.07       0.07   
3660              0.28       0.52       0.48       0.32       0.25       0.41   
3661              0.33       0.79       0.63       0.22       0.18       0.62   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.03       1.33       1.67       0.99       0.85       1.21   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.11       0.15       0.15       0.14       0.09   
1                 0.18       0.38       0.43       0.40       0.38       0.38   
2                 0.18       0.38       0.44       0.41       0.39       0.38   
3                 0.21       0.44       0.52       0.48       0.45       0.45   
4                 0.35       0.72       0.60       0.38       0.30       0.64   
...                ...        ...        ...        ...        ...        ...   
3659              0.08       0.15       0.12       0.09       0.06       0.06   
3660              0.29       0.52       0.49       0.31       0.25       0.41   
3661              0.34       0.80       0.67       0.21       0.17       0.64   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.04       1.36       1.67       0.97       0.81       1.19   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.21       0.45       0.35       0.33       0.31       0.29   
2                 0.22       0.45       0.35       0.34       0.31       0.30   
3                 0.25       0.52       0.41       0.39       0.37       0.35   
4                 0.36       0.75       0.57       0.39       0.30       0.60   
...                ...        ...        ...        ...        ...        ...   
3659              0.08       0.15       0.12       0.09       0.07       0.06   
3660              0.29       0.54       0.47       0.31       0.25       0.39   
3661              0.34       0.83       0.59       0.22       0.16       0.57   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.03       1.35       1.60       0.99       0.84       1.16   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.09       0.15       0.14       0.14       0.09   
1                 0.16       0.34       0.39       0.36       0.35

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3746          WFRC_8215       0.27       0.18       0.14       0.21   
3747          WFRC_8216       0.39       0.13       0.10       0.37   
3748          WFRC_8217       0.00       0.00       0.00       0.00   
3749          WFRC_8218       1.32       0.82       0.66       0.98   
3750          WFRC_8219       0.47       0.38       0.33       0.30   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.16       0.27       0.27       0.18       0.14       0.21   
3747              0.19       0.47       0.39       0.14       0.11       0.37   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.84       1.18       1.33       0.84       0.68       0.98   
3750              0.23       0.41       0.48       0.38       0.34       0.30   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.17       0.27       0.28       0.17       0.14       0.21   
3747              0.19       0.47       0.41       0.13       0.10       0.39   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.86       1.21       1.33       0.80       0.64       0.99   
3750              0.23       0.42       0.51       0.39       0.34       0.31   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.17       0.29       0.26       0.18       0.14       0.20   
3747              0.20       0.49       0.36       0.13       0.10       0.35   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.84       1.20       1.27       0.83       0.67       0.96   
3750              0.24       0.45       0.44       0.36       0.31       0.28   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3798          WFRC_8215       0.41       0.27       0.21       0.33   
3799          WFRC_8216       0.56       0.19       0.15       0.52   
3800          WFRC_8217       0.00       0.00       0.00       0.00   
3801          WFRC_8218       1.50       0.90       0.75       1.09   
3802          WFRC_8219       0.50       0.40       0.35       0.31   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.25       0.42       0.41       0.27       0.22       0.34   
3799              0.28       0.67       0.57       0.20       0.16       0.52   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.95       1.31       1.51       0.92       0.77       1.12   
3802              0.24       0.44       0.52       0.40       0.36       0.31   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.25       0.42       0.42       0.26       0.21       0.33   
3799              0.28       0.67       0.60       0.19       0.15       0.54   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.96       1.34       1.52       0.91       0.73       1.10   
3802              0.25       0.44       0.54       0.41       0.36       0.32   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.25       0.44       0.40       0.27       0.21       0.32   
3799              0.28       0.70       0.52       0.19       0.15       0.48   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.94       1.33       1.45       0.92       0.76       1.07   
3802              0.26       0.47       0.47       0.39       0.34       0.28   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.09   
1            0006_149.9       0.31       0.29       0.27       0.21   
2            0006_150.6       0.31       0.29       0.27       0.20   
3            0006_152.6       0.34       0.32       0.30       0.20   
4            0006_152.9       0.47       0.31       0.24       0.39   
...                 ...        ...        ...        ...        ...   
3886          WFRC_8215       0.53       0.35       0.27       0.43   
3887          WFRC_8216       0.63       0.22       0.17       0.55   
3888          WFRC_8217       1.64       1.08       0.91       1.07   
3889          WFRC_8218       1.66       1.00       0.83       1.20   
3890          WFRC_8219       1.06       0.89       0.78       0.71   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.10   
1                 0.15       0.27       0.30       0.28       0.27       0.21   
2                 0.15       0.26       0.30       0.28       0.27       0.20   
3                 0.17       0.24       0.32       0.30       0.29       0.20   
4                 0.29       0.45       0.47       0.32       0.25       0.39   
...                ...        ...        ...        ...        ...        ...   
3886              0.32       0.54       0.53       0.35       0.28       0.44   
3887              0.32       0.73       0.63       0.22       0.18       0.55   
3888              1.00       1.34       1.65       1.10       0.92       1.09   
3889              1.03       1.32       1.67       1.00       0.85       1.23   
3890              0.54       1.03       1.07       0.90       0.80       0.73   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.12       0.15       0.15       0.14       0.10   
1                 0.15       0.26       0.35       0.32       0.31       0.24   
2                 0.15       0.26       0.35       0.32       0.31       0.23   
3                 0.16       0.24       0.38       0.35       0.33       0.23   
4                 0.29       0.45       0.48       0.30       0.24       0.39   
...                ...        ...        ...        ...        ...        ...   
3886              0.32       0.55       0.54       0.34       0.27       0.44   
3887              0.32       0.74       0.67       0.21       0.17       0.57   
3888              1.01       1.34       1.67       1.06       0.89       1.09   
3889              1.05       1.35       1.68       0.97       0.81       1.21   
3890              0.54       1.04       1.12       0.92       0.80       0.75   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.17       0.31       0.28       0.27       0.25       0.19   
2                 0.17       0.30       0.28       0.27       0.25       0.18   
3                 0.19       0.28       0.31       0.29       0.27       0.18   
4                 0.29       0.47       0.46       0.31       0.24       0.37   
...                ...        ...        ...        ...        ...        ...   
3886              0.33       0.57       0.51       0.35       0.27       0.41   
3887              0.33       0.76       0.59       0.22       0.16       0.51   
3888              1.02       1.40       1.59       1.07       0.90       1.03   
3889              1.03       1.34       1.60       0.99       0.84       1.18   
3890              0.57       1.09       1.02       0.86       0.75       0.66   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.10       0.15       0.14       0.14       0.10   
1                 0.13       0.24       0.31       0.29       0.28

In [75]:
df_VC_MaxDirFG.columns

Index(['SEGID', 'Prd', 'SeasonGroup', 'DOWGroup', 'HrPctOf', 'VCGroupCode',
       'numRecords', 'CAP1HLSum', 'PrdPCEFlowSum', 'PkHrPCEFlowSum',
       'Pk15PCEFlowSum', 'PrdVCMax', 'PkHrVCMax', 'Pk15VCMax'],
      dtype='object')

In [76]:
dfs_VC_MaxDirFG_wVCGroups_Hr = []

for df_VC_MaxDirFG in dfs_VC_MaxDirFG:

    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG[['VCGroupCode','SEGID','PkHrVCMax']].copy()
    
    df_VC_MaxDirFG_wVCGroups_Hr['VCGroupCode'] = df_VC_MaxDirFG_wVCGroups_Hr['VCGroupCode'] + "Hr"
    
    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG_wVCGroups_Hr.round({'PkHrVC': 2})
    
    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG_wVCGroups_Hr.pivot(index='SEGID', columns="VCGroupCode",values='PkHrVCMax')
    
    df_VC_MaxDirFG_wVCGroups_Hr = df_VC_MaxDirFG_wVCGroups_Hr.reset_index()
    
    dfs_VC_MaxDirFG_wVCGroups_Hr.append(df_VC_MaxDirFG_wVCGroups_Hr)

    display(df_VC_MaxDirFG_wVCGroups_Hr)
    

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3613          WFRC_8208       0.00       0.00       0.00       0.00   
3614          WFRC_8209       0.04       0.03       0.02       0.03   
3615          WFRC_8213       0.06       0.04       0.03       0.03   
3616          WFRC_8215       0.17       0.11       0.09       0.12   
3617          WFRC_8218       1.10       0.64       0.52       0.76   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.02       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.05       0.06       0.05       0.03       0.03   
3616              0.10       0.16       0.17       0.11       0.09       0.12   
3617              0.65       1.01       1.11       0.65       0.53       0.77   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.02       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.05       0.06       0.04       0.03       0.03   
3616              0.10       0.16       0.17       0.11       0.08       0.12   
3617              0.66       1.03       1.11       0.62       0.50       0.76   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.02       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.05       0.06       0.04       0.03       0.03   
3616              0.10       0.16       0.16       0.11       0.08       0.11   
3617              0.65       1.02       1.06       0.65       0.53       0.74   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.07       0.05       0.04       0.03   
3660          WFRC_8215       0.20       0.16       0.14       0.14   
3661          WFRC_8216       0.30       0.10       0.08       0.31   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.19       0.69       0.56       0.86   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.06       0.07       0.05       0.04       0.03   
3660              0.10       0.21       0.21       0.16       0.14       0.14   
3661              0.14       0.40       0.30       0.10       0.08       0.31   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.71       1.07       1.20       0.71       0.57       0.88   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.06       0.07       0.05       0.04       0.03   
3660              0.10       0.21       0.22       0.17       0.15       0.15   
3661              0.15       0.40       0.31       0.10       0.08       0.33   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.72       1.09       1.20       0.67       0.54       0.86   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.06       0.07       0.05       0.04       0.03   
3660              0.11       0.23       0.19       0.16       0.14       0.13   
3661              0.15       0.42       0.28       0.10       0.08       0.29   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.71       1.08       1.15       0.70       0.57       0.84   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3744          WFRC_8215       0.28       0.18       0.14       0.22   
3745          WFRC_8216       0.37       0.13       0.10       0.36   
3746          WFRC_8217       0.00       0.00       0.00       0.00   
3747          WFRC_8218       1.29       0.75       0.61       0.94   
3748          WFRC_8219       0.43       0.34       0.30       0.28   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.17       0.29       0.28       0.19       0.15       0.23   
3745              0.18       0.48       0.37       0.13       0.10       0.37   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.78       1.16       1.30       0.77       0.62       0.96   
3748              0.20       0.38       0.44       0.35       0.31       0.29   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.17       0.29       0.28       0.18       0.14       0.23   
3745              0.18       0.48       0.39       0.12       0.10       0.38   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.80       1.18       1.31       0.73       0.59       0.95   
3748              0.20       0.39       0.46       0.35       0.31       0.29   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.17       0.30       0.27       0.18       0.14       0.21   
3745              0.18       0.50       0.35       0.13       0.10       0.34   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.78       1.17       1.25       0.77       0.62       0.92   
3748              0.21       0.41       0.40       0.33       0.29       0.26   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3795          WFRC_8215       0.39       0.25       0.20       0.32   
3796          WFRC_8216       0.47       0.16       0.12       0.44   
3797          WFRC_8217       0.00       0.00       0.00       0.00   
3798          WFRC_8218       1.45       0.84       0.68       1.07   
3799          WFRC_8219       0.45       0.35       0.31       0.28   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.23       0.41       0.39       0.26       0.20       0.33   
3796              0.24       0.52       0.47       0.16       0.13       0.44   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.91       1.18       1.46       0.86       0.70       1.10   
3799              0.22       0.38       0.46       0.36       0.32       0.28   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.23       0.41       0.39       0.25       0.20       0.33   
3796              0.24       0.53       0.50       0.16       0.12       0.46   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.92       1.21       1.47       0.82       0.66       1.08   
3799              0.22       0.39       0.48       0.36       0.32       0.29   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.24       0.43       0.37       0.25       0.20       0.31   
3796              0.25       0.55       0.44       0.16       0.12       0.41   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.90       1.20       1.40       0.86       0.69       1.05   
3799              0.23       0.41       0.42       0.34       0.30       0.26   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.13       0.12       0.12       0.08   
1            0006_149.9       0.27       0.26       0.24       0.18   
2            0006_150.6       0.27       0.26       0.24       0.17   
3            0006_152.6       0.30       0.28       0.26       0.18   
4            0006_152.9       0.44       0.29       0.23       0.36   
...                 ...        ...        ...        ...        ...   
3883          WFRC_8215       0.51       0.34       0.26       0.43   
3884          WFRC_8216       0.58       0.20       0.15       0.55   
3885          WFRC_8217       1.65       1.09       0.85       1.06   
3886          WFRC_8218       1.62       0.95       0.77       1.18   
3887          WFRC_8219       0.96       0.76       0.66       0.59   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.06       0.10       0.14       0.13       0.13       0.09   
1                 0.13       0.24       0.26       0.24       0.24       0.18   
2                 0.13       0.23       0.26       0.24       0.24       0.17   
3                 0.15       0.22       0.28       0.27       0.26       0.18   
4                 0.26       0.41       0.44       0.29       0.23       0.36   
...                ...        ...        ...        ...        ...        ...   
3883              0.31       0.53       0.51       0.34       0.27       0.44   
3884              0.29       0.70       0.58       0.20       0.16       0.55   
3885              0.97       1.30       1.65       1.10       0.86       1.08   
3886              1.01       1.30       1.64       0.97       0.78       1.20   
3887              0.44       1.02       0.98       0.77       0.68       0.61   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.06       0.10       0.13       0.13       0.12       0.09   
1                 0.13       0.23       0.31       0.28       0.27       0.21   
2                 0.13       0.23       0.31       0.28       0.27       0.20   
3                 0.14       0.21       0.34       0.31       0.29       0.20   
4                 0.27       0.41       0.44       0.28       0.22       0.36   
...                ...        ...        ...        ...        ...        ...   
3883              0.31       0.53       0.52       0.33       0.26       0.44   
3884              0.29       0.70       0.61       0.19       0.15       0.57   
3885              0.98       1.31       1.67       1.06       0.84       1.08   
3886              1.03       1.33       1.64       0.92       0.75       1.18   
3887              0.45       1.03       1.03       0.79       0.68       0.63   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.07       0.11       0.11       0.11       0.10       0.07   
1                 0.15       0.28       0.25       0.23       0.22       0.16   
2                 0.15       0.27       0.25       0.23       0.22       0.15   
3                 0.17       0.25       0.27       0.26       0.24       0.16   
4                 0.27       0.43       0.42       0.28       0.22       0.35   
...                ...        ...        ...        ...        ...        ...   
3883              0.31       0.55       0.49       0.33       0.26       0.41   
3884              0.30       0.73       0.54       0.20       0.15       0.51   
3885              0.99       1.37       1.59       1.08       0.84       1.02   
3886              1.01       1.32       1.57       0.96       0.78       1.15   
3887              0.47       1.10       0.90       0.74       0.64       0.55   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.05       0.09       0.13       0.12       0.12       0.09   
1                 0.12       0.21       0.28       0.26       0.25

...

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.05       0.05       0.05       0.05   
2            0006_150.6       0.06       0.05       0.05       0.05   
3            0006_152.6       0.07       0.07       0.07       0.06   
4            0006_152.9       0.09       0.07       0.06       0.08   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.08       0.06       0.04       0.04   
3660          WFRC_8215       0.36       0.24       0.19       0.30   
3661          WFRC_8216       0.48       0.16       0.13       0.46   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.49       0.87       0.70       1.07   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.06       0.06       0.05       0.05       0.05   
2                 0.03       0.06       0.06       0.06       0.06       0.05   
3                 0.04       0.08       0.08       0.07       0.08       0.07   
4                 0.04       0.10       0.09       0.07       0.06       0.08   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.09       0.08       0.06       0.05       0.04   
3660              0.21       0.38       0.36       0.24       0.19       0.31   
3661              0.25       0.60       0.48       0.17       0.13       0.47   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.90       1.29       1.51       0.89       0.72       1.09   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.06       0.05       0.05       0.05       0.05   
2                 0.03       0.06       0.06       0.06       0.06       0.05   
3                 0.04       0.08       0.08       0.08       0.07       0.07   
4                 0.05       0.10       0.09       0.07       0.06       0.08   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.09       0.08       0.06       0.04       0.04   
3660              0.21       0.38       0.37       0.23       0.18       0.31   
3661              0.25       0.61       0.51       0.16       0.13       0.48   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.92       1.32       1.51       0.85       0.68       1.07   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.07       0.05       0.05       0.04       0.04   
2                 0.03       0.07       0.05       0.05       0.05       0.04   
3                 0.04       0.09       0.07       0.07       0.06       0.06   
4                 0.05       0.11       0.08       0.07       0.06       0.07   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.09       0.08       0.06       0.04       0.04   
3660              0.22       0.40       0.35       0.24       0.18       0.29   
3661              0.26       0.63       0.45       0.17       0.12       0.43   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.90       1.31       1.44       0.88       0.71       1.05   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.02       0.05       0.06       0.05       0.05

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.13       0.12       0.12       0.07   
1            0006_149.9       0.34       0.32       0.30       0.29   
2            0006_150.6       0.35       0.33       0.31       0.29   
3            0006_152.6       0.40       0.38       0.36       0.35   
4            0006_152.9       0.55       0.36       0.28       0.57   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.11       0.09       0.06       0.06   
3660          WFRC_8215       0.44       0.29       0.23       0.37   
3661          WFRC_8216       0.58       0.20       0.15       0.56   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.62       0.94       0.77       1.16   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.06       0.09       0.14       0.13       0.13       0.08   
1                 0.16       0.34       0.32       0.30       0.29       0.29   
2                 0.17       0.34       0.33       0.31       0.30       0.29   
3                 0.19       0.40       0.38       0.36       0.35       0.34   
4                 0.32       0.66       0.55       0.36       0.29       0.59   
...                ...        ...        ...        ...        ...        ...   
3659              0.07       0.13       0.11       0.09       0.06       0.06   
3660              0.26       0.48       0.44       0.30       0.23       0.38   
3661              0.31       0.73       0.58       0.20       0.16       0.57   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.00       1.30       1.64       0.97       0.78       1.19   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.06       0.10       0.13       0.13       0.12       0.08   
1                 0.16       0.33       0.38       0.35       0.34       0.33   
2                 0.16       0.34       0.39       0.36       0.34       0.33   
3                 0.19       0.39       0.45       0.42       0.40       0.40   
4                 0.32       0.67       0.55       0.35       0.28       0.59   
...                ...        ...        ...        ...        ...        ...   
3659              0.07       0.14       0.11       0.08       0.06       0.06   
3660              0.26       0.48       0.45       0.29       0.23       0.38   
3661              0.31       0.74       0.61       0.19       0.15       0.59   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.02       1.33       1.64       0.92       0.74       1.17   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.07       0.10       0.11       0.11       0.10       0.07   
1                 0.19       0.39       0.31       0.29       0.27       0.26   
2                 0.19       0.40       0.31       0.30       0.28       0.26   
3                 0.22       0.46       0.36       0.34       0.32       0.31   
4                 0.33       0.69       0.53       0.36       0.28       0.55   
...                ...        ...        ...        ...        ...        ...   
3659              0.07       0.14       0.11       0.09       0.06       0.06   
3660              0.27       0.50       0.43       0.29       0.23       0.36   
3661              0.31       0.76       0.54       0.20       0.15       0.53   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.00       1.32       1.57       0.96       0.78       1.14   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.06       0.08       0.13       0.12       0.12       0.08   
1                 0.14       0.30       0.34       0.32       0.30

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3746          WFRC_8215       0.25       0.16       0.13       0.19   
3747          WFRC_8216       0.36       0.12       0.10       0.34   
3748          WFRC_8217       0.00       0.00       0.00       0.00   
3749          WFRC_8218       1.29       0.75       0.61       0.93   
3750          WFRC_8219       0.42       0.33       0.29       0.26   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.15       0.25       0.25       0.17       0.13       0.19   
3747              0.18       0.43       0.36       0.13       0.10       0.34   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.78       1.16       1.30       0.77       0.62       0.95   
3750              0.20       0.36       0.43       0.33       0.30       0.27   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.15       0.25       0.25       0.16       0.13       0.19   
3747              0.18       0.43       0.38       0.12       0.10       0.36   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.79       1.18       1.31       0.73       0.59       0.94   
3750              0.20       0.37       0.45       0.34       0.30       0.28   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.15       0.26       0.24       0.16       0.13       0.18   
3747              0.18       0.45       0.33       0.12       0.09       0.32   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.77       1.17       1.25       0.77       0.62       0.92   
3750              0.21       0.39       0.39       0.32       0.28       0.24   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3798          WFRC_8215       0.38       0.25       0.20       0.30   
3799          WFRC_8216       0.52       0.18       0.14       0.48   
3800          WFRC_8217       0.00       0.00       0.00       0.00   
3801          WFRC_8218       1.47       0.86       0.69       1.07   
3802          WFRC_8219       0.44       0.35       0.31       0.27   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.23       0.39       0.38       0.25       0.20       0.31   
3799              0.26       0.62       0.52       0.18       0.15       0.48   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.90       1.28       1.48       0.88       0.71       1.09   
3802              0.21       0.39       0.45       0.36       0.31       0.27   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.23       0.39       0.38       0.24       0.19       0.31   
3799              0.26       0.62       0.55       0.17       0.14       0.50   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.92       1.31       1.49       0.83       0.67       1.08   
3802              0.22       0.39       0.48       0.36       0.32       0.28   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.23       0.41       0.37       0.25       0.19       0.29   
3799              0.26       0.64       0.48       0.18       0.13       0.45   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.90       1.30       1.42       0.87       0.70       1.05   
3802              0.23       0.42       0.42       0.34       0.30       0.25   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPMHr  AnnSaDYHr  AnnSuDYHr  AnnWkAMHr  \
0            0006_146.9       0.13       0.12       0.12       0.08   
1            0006_149.9       0.27       0.26       0.24       0.18   
2            0006_150.6       0.27       0.26       0.24       0.18   
3            0006_152.6       0.30       0.28       0.26       0.18   
4            0006_152.9       0.44       0.29       0.23       0.36   
...                 ...        ...        ...        ...        ...   
3886          WFRC_8215       0.49       0.32       0.25       0.39   
3887          WFRC_8216       0.58       0.20       0.15       0.50   
3888          WFRC_8217       1.61       1.06       0.83       1.05   
3889          WFRC_8218       1.62       0.95       0.77       1.18   
3890          WFRC_8219       0.99       0.79       0.68       0.63   

VCGroupCode  AnnWkMDHr  AnnWkPMHr  AprFrPMHr  AprSaDYHr  AprSuDYHr  AprWkAMHr  \
0                 0.06       0.10       0.14       0.13       0.13       0.09   
1                 0.13       0.24       0.26       0.24       0.24       0.18   
2                 0.13       0.23       0.26       0.24       0.24       0.17   
3                 0.15       0.21       0.28       0.27       0.26       0.18   
4                 0.26       0.41       0.44       0.29       0.23       0.36   
...                ...        ...        ...        ...        ...        ...   
3886              0.29       0.50       0.49       0.32       0.26       0.40   
3887              0.29       0.68       0.58       0.20       0.16       0.51   
3888              0.97       1.31       1.61       1.07       0.84       1.07   
3889              1.01       1.30       1.64       0.97       0.78       1.20   
3890              0.47       0.96       1.01       0.79       0.70       0.64   

VCGroupCode  AprWkMDHr  AprWkPMHr  AugFrPMHr  AugSaDYHr  AugSuDYHr  AugWkAMHr  \
0                 0.06       0.10       0.13       0.13       0.12       0.09   
1                 0.13       0.23       0.31       0.28       0.27       0.21   
2                 0.13       0.23       0.31       0.28       0.27       0.20   
3                 0.14       0.21       0.34       0.31       0.29       0.20   
4                 0.27       0.42       0.44       0.28       0.22       0.36   
...                ...        ...        ...        ...        ...        ...   
3886              0.30       0.50       0.49       0.31       0.25       0.40   
3887              0.30       0.68       0.62       0.19       0.15       0.53   
3888              0.98       1.32       1.64       1.04       0.82       1.07   
3889              1.03       1.32       1.64       0.92       0.75       1.18   
3890              0.48       0.97       1.06       0.81       0.71       0.66   

VCGroupCode  AugWkMDHr  AugWkPMHr  DecFrPMHr  DecSaDYHr  DecSuDYHr  DecWkAMHr  \
0                 0.07       0.11       0.11       0.11       0.10       0.07   
1                 0.15       0.27       0.25       0.23       0.22       0.16   
2                 0.15       0.27       0.25       0.23       0.22       0.16   
3                 0.17       0.25       0.27       0.26       0.24       0.16   
4                 0.27       0.43       0.42       0.28       0.22       0.34   
...                ...        ...        ...        ...        ...        ...   
3886              0.30       0.52       0.47       0.32       0.25       0.38   
3887              0.30       0.70       0.54       0.20       0.15       0.47   
3888              0.99       1.37       1.56       1.05       0.83       1.01   
3889              1.01       1.31       1.57       0.96       0.78       1.15   
3890              0.50       1.03       0.93       0.76       0.66       0.58   

VCGroupCode  DecWkMDHr  DecWkPMHr  FalFrPMHr  FalSaDYHr  FalSuDYHr  FalWkAMHr  \
0                 0.05       0.09       0.13       0.12       0.12       0.09   
1                 0.12       0.21       0.28       0.26       0.24

In [77]:
dfs_VC_MaxDirFG_wVCGroups_Prd = []

for df_VC_MaxDirFG in dfs_VC_MaxDirFG:

    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG[df_VC_MaxDirFG['HrPctOf'] == 'Prd'].copy()
    
    df_VC_MaxDirFG_wVCGroups_Prd['VCGroupCode'] = df_VC_MaxDirFG_wVCGroups_Prd['VCGroupCode'] + "Prd"
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd[['VCGroupCode','SEGID','PrdVCMax']]
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd.round({'PrdVC': 2})
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd.pivot(index='SEGID', columns="VCGroupCode",values='PrdVCMax')
    
    df_VC_MaxDirFG_wVCGroups_Prd = df_VC_MaxDirFG_wVCGroups_Prd.reset_index()
    
    dfs_VC_MaxDirFG_wVCGroups_Prd.append(df_VC_MaxDirFG_wVCGroups_Prd)

    display(df_VC_MaxDirFG_wVCGroups_Prd)

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.00        0.00        0.00        0.00   
2            0006_150.6        0.00        0.00        0.00        0.00   
3            0006_152.6        0.00        0.00        0.00        0.00   
4            0006_152.9        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3613          WFRC_8208        0.00        0.00        0.00        0.00   
3614          WFRC_8209        0.02        0.02        0.03        0.02   
3615          WFRC_8213        0.02        0.03        0.05        0.02   
3616          WFRC_8215        0.10        0.09        0.14        0.10   
3617          WFRC_8218        0.66        0.56        0.91        0.67   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3613               0.00        0.00        0.00        0.00        0.00   
3614               0.02        0.03        0.03        0.02        0.04   
3615               0.03        0.05        0.02        0.03        0.05   
3616               0.09        0.14        0.10        0.09        0.15   
3617               0.57        0.93        0.66        0.57        0.92   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3613               0.00        0.00        0.00        0.00        0.00   
3614               0.02        0.02        0.03        0.02        0.02   
3615               0.02        0.03        0.05        0.02        0.03   
3616               0.09        0.08        0.13        0.10        0.09   
3617               0.64        0.55        0.89        0.66        0.56   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3613               0.00        0.00        0.00        0.00        0.00   
3614               0.03        0.02        0.02        0.03        0.02   
3615               0.05        0.02        0.03        0.04        0.02   
3616               0.14        0.09        0.08        0.13        0.09   
3617               0.91        0.64        0.55        0.89        0.61   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.00        0.00        0.00        0.00   
2            0006_150.6        0.00        0.00        0.00        0.00   
3            0006_152.6        0.00        0.00        0.00        0.00   
4            0006_152.9        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3659          WFRC_8213        0.03        0.04        0.06        0.03   
3660          WFRC_8215        0.12        0.09        0.18        0.12   
3661          WFRC_8216        0.25        0.11        0.34        0.25   
3662          WFRC_8217        0.00        0.00        0.00        0.00   
3663          WFRC_8218        0.74        0.61        0.96        0.76   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3659               0.04        0.06        0.03        0.04        0.06   
3660               0.09        0.19        0.12        0.10        0.19   
3661               0.11        0.34        0.26        0.11        0.35   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.62        0.98        0.75        0.62        0.97   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3659               0.03        0.04        0.06        0.03        0.04   
3660               0.11        0.08        0.17        0.12        0.09   
3661               0.24        0.10        0.32        0.25        0.11   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.73        0.60        0.94        0.74        0.61   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3659               0.06        0.03        0.04        0.06        0.03   
3660               0.19        0.10        0.08        0.16        0.10   
3661               0.34        0.24        0.10        0.32        0.23   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.96        0.73        0.60        0.94        0.69   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.00        0.00        0.00        0.00   
2            0006_150.6        0.00        0.00        0.00        0.00   
3            0006_152.6        0.00        0.00        0.00        0.00   
4            0006_152.9        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3744          WFRC_8215        0.18        0.15        0.26        0.19   
3745          WFRC_8216        0.29        0.13        0.41        0.29   
3746          WFRC_8217        0.00        0.00        0.00        0.00   
3747          WFRC_8218        0.82        0.67        1.04        0.83   
3748          WFRC_8219        0.23        0.18        0.34        0.24   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3744               0.15        0.26        0.19        0.15        0.27   
3745               0.14        0.41        0.30        0.14        0.42   
3746               0.00        0.00        0.00        0.00        0.00   
3747               0.68        1.06        0.82        0.68        1.05   
3748               0.18        0.34        0.25        0.19        0.36   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3744               0.18        0.14        0.25        0.19        0.15   
3745               0.28        0.13        0.39        0.29        0.14   
3746               0.00        0.00        0.00        0.00        0.00   
3747               0.80        0.66        1.02        0.82        0.67   
3748               0.22        0.16        0.31        0.24        0.18   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3744               0.26        0.18        0.14        0.25        0.16   
3745               0.41        0.28        0.13        0.38        0.27   
3746               0.00        0.00        0.00        0.00        0.00   
3747               1.05        0.80        0.66        1.02        0.76   
3748               0.34        0.21        0.16        0.30        0.20   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.00        0.00        0.00        0.00   
2            0006_150.6        0.00        0.00        0.00        0.00   
3            0006_152.6        0.00        0.00        0.00        0.00   
4            0006_152.9        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3795          WFRC_8215        0.27        0.20        0.36        0.27   
3796          WFRC_8216        0.35        0.18        0.44        0.35   
3797          WFRC_8217        0.00        0.00        0.00        0.00   
3798          WFRC_8218        0.93        0.78        1.07        0.95   
3799          WFRC_8219        0.23        0.19        0.33        0.23   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3795               0.21        0.37        0.28        0.21        0.38   
3796               0.18        0.44        0.36        0.19        0.46   
3797               0.00        0.00        0.00        0.00        0.00   
3798               0.79        1.09        0.94        0.79        1.08   
3799               0.19        0.34        0.25        0.20        0.36   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3795               0.26        0.19        0.35        0.27        0.21   
3796               0.33        0.17        0.42        0.35        0.18   
3797               0.00        0.00        0.00        0.00        0.00   
3798               0.91        0.76        1.05        0.93        0.78   
3799               0.21        0.17        0.31        0.24        0.19   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3795               0.37        0.26        0.19        0.35        0.24   
3796               0.45        0.33        0.17        0.42        0.32   
3797               0.00        0.00        0.00        0.00        0.00   
3798               1.07        0.91        0.76        1.05        0.87   
3799               0.34        0.21        0.17        0.30        0.20   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.07        0.05        0.09        0.07   
1            0006_149.9        0.15        0.12        0.22        0.15   
2            0006_150.6        0.14        0.12        0.22        0.14   
3            0006_152.6        0.15        0.13        0.20        0.14   
4            0006_152.9        0.30        0.23        0.37        0.30   
...                 ...         ...         ...         ...         ...   
3883          WFRC_8215        0.36        0.27        0.47        0.36   
3884          WFRC_8216        0.44        0.22        0.59        0.44   
3885          WFRC_8217        0.88        0.85        1.17        0.89   
3886          WFRC_8218        1.02        0.87        1.18        1.04   
3887          WFRC_8219        0.49        0.39        0.89        0.50   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.05        0.09        0.07        0.06        0.10   
1                  0.11        0.22        0.17        0.13        0.26   
2                  0.11        0.21        0.16        0.13        0.25   
3                  0.13        0.19        0.17        0.15        0.23   
4                  0.23        0.37        0.31        0.24        0.38   
...                 ...         ...         ...         ...         ...   
3883               0.27        0.48        0.37        0.28        0.49   
3884               0.22        0.59        0.46        0.23        0.61   
3885               0.85        1.18        0.91        0.87        1.21   
3886               0.88        1.20        1.03        0.88        1.19   
3887               0.39        0.91        0.53        0.41        0.95   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.06        0.05        0.08        0.07        0.05   
1                  0.13        0.10        0.19        0.15        0.12   
2                  0.12        0.10        0.19        0.14        0.12   
3                  0.13        0.11        0.17        0.15        0.13   
4                  0.28        0.22        0.35        0.30        0.23   
...                 ...         ...         ...         ...         ...   
3883               0.34        0.26        0.45        0.36        0.27   
3884               0.42        0.21        0.56        0.44        0.22   
3885               0.84        0.81        1.12        0.90        0.86   
3886               1.00        0.85        1.15        1.02        0.87   
3887               0.46        0.36        0.83        0.50        0.40   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.09        0.06        0.04        0.08        0.06   
1                  0.22        0.12        0.10        0.18        0.12   
2                  0.22        0.12        0.10        0.18        0.11   
3                  0.20        0.12        0.11        0.17        0.11   
4                  0.38        0.28        0.22        0.35        0.26   
...                 ...         ...         ...         ...         ...   
3883               0.48        0.34        0.26        0.45        0.32   
3884               0.60        0.42        0.21        0.56        0.41   
3885               1.19        0.84        0.81        1.12        0.78   
3886               1.18        1.00        0.85        1.15        0.95   
3887               0.91        0.44        0.35        0.80        0.42   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.04        0.07        0.07        0.06        0.10   
1                  0.09        0.17        0.18        0.14        0.27   
2                  0.09        0.17        0.17        0.14        0.26   
3                  0.10        0.15        0.18        0.16        0.24   
4                  0.

...

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.04        0.02        0.06        0.04   
2            0006_150.6        0.04        0.02        0.06        0.04   
3            0006_152.6        0.05        0.03        0.07        0.05   
4            0006_152.9        0.06        0.04        0.09        0.07   
...                 ...         ...         ...         ...         ...   
3659          WFRC_8213        0.03        0.05        0.08        0.03   
3660          WFRC_8215        0.25        0.19        0.34        0.25   
3661          WFRC_8216        0.37        0.19        0.51        0.37   
3662          WFRC_8217        0.00        0.00        0.00        0.00   
3663          WFRC_8218        0.92        0.78        1.16        0.94   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.02        0.06        0.04        0.03        0.06   
2                  0.03        0.06        0.04        0.03        0.06   
3                  0.03        0.07        0.06        0.03        0.08   
4                  0.04        0.09        0.07        0.04        0.09   
...                 ...         ...         ...         ...         ...   
3659               0.05        0.08        0.03        0.05        0.08   
3660               0.19        0.35        0.26        0.19        0.35   
3661               0.19        0.51        0.39        0.20        0.53   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.79        1.19        0.93        0.79        1.18   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.03        0.02        0.05        0.04        0.02   
2                  0.03        0.02        0.05        0.04        0.03   
3                  0.05        0.03        0.06        0.05        0.03   
4                  0.06        0.04        0.08        0.07        0.04   
...                 ...         ...         ...         ...         ...   
3659               0.03        0.05        0.08        0.03        0.05   
3660               0.24        0.18        0.33        0.26        0.19   
3661               0.35        0.18        0.49        0.38        0.19   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.91        0.76        1.14        0.93        0.78   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.06        0.03        0.02        0.05        0.03   
2                  0.06        0.03        0.02        0.05        0.03   
3                  0.07        0.04        0.03        0.06        0.04   
4                  0.09        0.06        0.04        0.08        0.05   
...                 ...         ...         ...         ...         ...   
3659               0.08        0.03        0.04        0.08        0.03   
3660               0.35        0.24        0.18        0.33        0.22   
3661               0.52        0.35        0.18        0.48        0.34   
3662               0.00        0.00        0.00        0.00        0.00   
3663               1.17        0.91        0.76        1.14        0.86   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.02        0.05        0.04        0.02        0.06   
2                  0.02        0.05        0.04        0.03        0.06   
3                  0.03        0.06        0.06        0.03        0.08   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.06        0.05        0.08        0.06   
1            0006_149.9        0.24        0.14        0.32        0.23   
2            0006_150.6        0.24        0.15        0.32        0.24   
3            0006_152.6        0.29        0.17        0.37        0.28   
4            0006_152.9        0.48        0.28        0.59        0.48   
...                 ...         ...         ...         ...         ...   
3659          WFRC_8213        0.05        0.06        0.12        0.05   
3660          WFRC_8215        0.31        0.23        0.43        0.31   
3661          WFRC_8216        0.45        0.23        0.61        0.45   
3662          WFRC_8217        0.00        0.00        0.00        0.00   
3663          WFRC_8218        1.01        0.86        1.17        1.03   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.05        0.09        0.07        0.06        0.09   
1                  0.14        0.31        0.28        0.16        0.36   
2                  0.14        0.31        0.28        0.17        0.37   
3                  0.17        0.36        0.33        0.20        0.42   
4                  0.28        0.60        0.49        0.29        0.61   
...                 ...         ...         ...         ...         ...   
3659               0.06        0.12        0.05        0.06        0.12   
3660               0.23        0.43        0.32        0.24        0.44   
3661               0.23        0.62        0.47        0.24        0.64   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.88        1.20        1.02        0.87        1.19   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.05        0.05        0.07        0.06        0.06   
1                  0.21        0.13        0.28        0.24        0.14   
2                  0.21        0.13        0.28        0.24        0.15   
3                  0.25        0.15        0.32        0.29        0.17   
4                  0.45        0.27        0.57        0.48        0.29   
...                 ...         ...         ...         ...         ...   
3659               0.05        0.06        0.12        0.05        0.06   
3660               0.29        0.22        0.41        0.31        0.23   
3661               0.43        0.22        0.59        0.46        0.23   
3662               0.00        0.00        0.00        0.00        0.00   
3663               0.99        0.84        1.15        1.01        0.86   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.09        0.05        0.05        0.07        0.05   
1                  0.32        0.20        0.12        0.26        0.19   
2                  0.32        0.20        0.12        0.26        0.19   
3                  0.37        0.24        0.14        0.30        0.22   
4                  0.60        0.45        0.27        0.57        0.42   
...                 ...         ...         ...         ...         ...   
3659               0.12        0.05        0.06        0.12        0.05   
3660               0.43        0.29        0.22        0.41        0.27   
3661               0.62        0.43        0.22        0.58        0.42   
3662               0.00        0.00        0.00        0.00        0.00   
3663               1.18        0.99        0.84        1.15        0.94   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.04        0.07        0.07        0.06        0.09   
1                  0.11        0.25        0.29        0.17        0.38   
2                  0.11        0.25        0.29        0.18        0.38   
3                  0.13        0.28        0.35        0.21        0.44   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.00        0.00        0.00        0.00   
2            0006_150.6        0.00        0.00        0.00        0.00   
3            0006_152.6        0.00        0.00        0.00        0.00   
4            0006_152.9        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3746          WFRC_8215        0.16        0.13        0.23        0.16   
3747          WFRC_8216        0.27        0.13        0.36        0.28   
3748          WFRC_8217        0.00        0.00        0.00        0.00   
3749          WFRC_8218        0.81        0.67        1.04        0.82   
3750          WFRC_8219        0.22        0.18        0.32        0.22   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3746               0.13        0.23        0.16        0.14        0.23   
3747               0.13        0.37        0.29        0.14        0.38   
3748               0.00        0.00        0.00        0.00        0.00   
3749               0.68        1.06        0.82        0.68        1.05   
3750               0.18        0.32        0.23        0.19        0.34   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3746               0.15        0.13        0.22        0.16        0.13   
3747               0.26        0.13        0.35        0.28        0.13   
3748               0.00        0.00        0.00        0.00        0.00   
3749               0.79        0.66        1.02        0.81        0.67   
3750               0.20        0.16        0.29        0.22        0.18   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3746               0.23        0.15        0.13        0.22        0.14   
3747               0.37        0.26        0.13        0.34        0.25   
3748               0.00        0.00        0.00        0.00        0.00   
3749               1.05        0.79        0.66        1.02        0.75   
3750               0.33        0.20        0.16        0.28        0.19   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.00        0.00        0.00        0.00   
1            0006_149.9        0.00        0.00        0.00        0.00   
2            0006_150.6        0.00        0.00        0.00        0.00   
3            0006_152.6        0.00        0.00        0.00        0.00   
4            0006_152.9        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3798          WFRC_8215        0.25        0.20        0.35        0.25   
3799          WFRC_8216        0.38        0.19        0.52        0.38   
3800          WFRC_8217        0.00        0.00        0.00        0.00   
3801          WFRC_8218        0.93        0.77        1.16        0.94   
3802          WFRC_8219        0.22        0.19        0.34        0.23   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3798               0.20        0.35        0.26        0.21        0.36   
3799               0.19        0.52        0.40        0.20        0.54   
3800               0.00        0.00        0.00        0.00        0.00   
3801               0.79        1.18        0.94        0.78        1.17   
3802               0.19        0.34        0.24        0.20        0.36   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3798               0.24        0.19        0.33        0.26        0.20   
3799               0.37        0.18        0.50        0.39        0.19   
3800               0.00        0.00        0.00        0.00        0.00   
3801               0.91        0.76        1.14        0.93        0.77   
3802               0.21        0.17        0.31        0.23        0.19   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.00        0.00        0.00        0.00        0.00   
...                 ...         ...         ...         ...         ...   
3798               0.35        0.24        0.19        0.33        0.22   
3799               0.53        0.36        0.18        0.49        0.35   
3800               0.00        0.00        0.00        0.00        0.00   
3801               1.16        0.91        0.76        1.13        0.86   
3802               0.34        0.20        0.17        0.30        0.19   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.00        0.00        0.00        0.00        0.00   
1                  0.00        0.00        0.00        0.00        0.00   
2                  0.00        0.00        0.00        0.00        0.00   
3                  0.00        0.00        0.00        0.00        0.00   
4                  0.

VCGroupCode       SEGID  AnnWkAMPrd  AnnWkMDPrd  AnnWkPMPrd  AprWkAMPrd  \
0            0006_146.9        0.07        0.05        0.09        0.07   
1            0006_149.9        0.15        0.12        0.22        0.15   
2            0006_150.6        0.14        0.12        0.21        0.14   
3            0006_152.6        0.15        0.13        0.20        0.14   
4            0006_152.9        0.30        0.23        0.37        0.30   
...                 ...         ...         ...         ...         ...   
3886          WFRC_8215        0.33        0.26        0.45        0.33   
3887          WFRC_8216        0.40        0.22        0.57        0.41   
3888          WFRC_8217        0.87        0.85        1.17        0.88   
3889          WFRC_8218        1.02        0.87        1.17        1.04   
3890          WFRC_8219        0.52        0.41        0.84        0.53   

VCGroupCode  AprWkMDPrd  AprWkPMPrd  AugWkAMPrd  AugWkMDPrd  AugWkPMPrd  \
0                  0.05        0.09        0.07        0.06        0.10   
1                  0.11        0.22        0.17        0.13        0.25   
2                  0.11        0.21        0.17        0.13        0.25   
3                  0.13        0.19        0.17        0.15        0.23   
4                  0.23        0.38        0.30        0.24        0.38   
...                 ...         ...         ...         ...         ...   
3886               0.26        0.45        0.34        0.26        0.46   
3887               0.22        0.57        0.42        0.23        0.59   
3888               0.86        1.18        0.90        0.87        1.21   
3889               0.88        1.19        1.03        0.88        1.18   
3890               0.42        0.85        0.55        0.44        0.89   

VCGroupCode  DecWkAMPrd  DecWkMDPrd  DecWkPMPrd  FalWkAMPrd  FalWkMDPrd  \
0                  0.06        0.05        0.08        0.07        0.05   
1                  0.13        0.10        0.19        0.15        0.12   
2                  0.13        0.10        0.19        0.14        0.12   
3                  0.13        0.11        0.17        0.15        0.13   
4                  0.28        0.22        0.36        0.30        0.24   
...                 ...         ...         ...         ...         ...   
3886               0.31        0.24        0.43        0.33        0.26   
3887               0.39        0.21        0.54        0.41        0.22   
3888               0.83        0.81        1.12        0.88        0.86   
3889               1.00        0.85        1.15        1.02        0.87   
3890               0.48        0.38        0.78        0.53        0.42   

VCGroupCode  FalWkPMPrd  FebWkAMPrd  FebWkMDPrd  FebWkPMPrd  JanWkAMPrd  \
0                  0.09        0.06        0.04        0.08        0.06   
1                  0.22        0.13        0.10        0.18        0.12   
2                  0.21        0.12        0.10        0.18        0.11   
3                  0.20        0.12        0.11        0.16        0.11   
4                  0.38        0.28        0.22        0.35        0.26   
...                 ...         ...         ...         ...         ...   
3886               0.45        0.31        0.24        0.43        0.29   
3887               0.58        0.38        0.21        0.54        0.37   
3888               1.19        0.83        0.81        1.12        0.77   
3889               1.17        1.00        0.85        1.15        0.95   
3890               0.86        0.47        0.37        0.75        0.44   

VCGroupCode  JanWkMDPrd  JanWkPMPrd  JulWkAMPrd  JulWkMDPrd  JulWkPMPrd  \
0                  0.04        0.07        0.07        0.06        0.10   
1                  0.09        0.17        0.18        0.14        0.27   
2                  0.09        0.17        0.17        0.14        0.26   
3                  0.10        0.15        0.18        0.16        0.24   
4                  0.

In [78]:
df_Scenarios

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

In [79]:
dfs_VC_MaxDirFG_wVCGroups = []

for (idx, row) in df_Scenarios.iterrows():
    
    df_VC_MaxDirFG_wVCGroups = pd.DataFrame.merge(dfs_VC_MaxDirFG_wVCGroups_15[idx],dfs_VC_MaxDirFG_wVCGroups_Hr[idx],on='SEGID')
    df_VC_MaxDirFG_wVCGroups = pd.DataFrame.merge(df_VC_MaxDirFG_wVCGroups,dfs_VC_MaxDirFG_wVCGroups_Prd[idx],on='SEGID')
    dfs_VC_MaxDirFG_wVCGroups.append(df_VC_MaxDirFG_wVCGroups)
    display(df_VC_MaxDirFG_wVCGroups)

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3613          WFRC_8208       0.00       0.00       0.00       0.00   
3614          WFRC_8209       0.04       0.03       0.02       0.03   
3615          WFRC_8213       0.06       0.05       0.03       0.03   
3616          WFRC_8215       0.18       0.12       0.09       0.13   
3617          WFRC_8218       1.12       0.70       0.56       0.82   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.05       0.07       0.05       0.03       0.03   
3616              0.11       0.17       0.18       0.12       0.09       0.13   
3617              0.71       1.03       1.13       0.71       0.58       0.84   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.06       0.06       0.05       0.03       0.03   
3616              0.11       0.17       0.18       0.12       0.09       0.13   
3617              0.72       1.05       1.13       0.68       0.55       0.83   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.06       0.06       0.05       0.03       0.03   
3616              0.11       0.18       0.17       0.12       0.09       0.12   
3617              0.71       1.04       1.08       0.71       0.57       0.81   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.08       0.06       0.04       0.04   
3660          WFRC_8215       0.23       0.18       0.16       0.16   
3661          WFRC_8216       0.34       0.12       0.09       0.35   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.21       0.75       0.61       0.90   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.07       0.08       0.06       0.04       0.04   
3660              0.12       0.24       0.24       0.19       0.16       0.16   
3661              0.16       0.46       0.34       0.12       0.09       0.36   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.77       1.09       1.22       0.77       0.62       0.92   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.07       0.08       0.06       0.04       0.04   
3660              0.12       0.24       0.25       0.19       0.17       0.17   
3661              0.16       0.46       0.36       0.11       0.09       0.37   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.78       1.11       1.23       0.73       0.59       0.91   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3659              0.05       0.07       0.08       0.06       0.04       0.04   
3660              0.12       0.26       0.22       0.18       0.15       0.15   
3661              0.17       0.47       0.31       0.12       0.09       0.33   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.77       1.10       1.17       0.77       0.62       0.91   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3744          WFRC_8215       0.30       0.20       0.16       0.24   
3745          WFRC_8216       0.40       0.14       0.11       0.39   
3746          WFRC_8217       0.00       0.00       0.00       0.00   
3747          WFRC_8218       1.32       0.82       0.66       0.99   
3748          WFRC_8219       0.49       0.39       0.34       0.32   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.18       0.31       0.31       0.20       0.16       0.25   
3745              0.20       0.52       0.40       0.14       0.11       0.40   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.85       1.18       1.33       0.84       0.68       0.99   
3748              0.23       0.44       0.50       0.39       0.35       0.32   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.19       0.32       0.31       0.20       0.16       0.25   
3745              0.20       0.53       0.43       0.14       0.11       0.41   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.87       1.21       1.33       0.80       0.64       1.00   
3748              0.23       0.44       0.52       0.40       0.35       0.33   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3744              0.19       0.33       0.29       0.20       0.16       0.23   
3745              0.20       0.54       0.38       0.14       0.10       0.37   
3746              0.00       0.00       0.00       0.00       0.00       0.00   
3747              0.85       1.20       1.27       0.83       0.67       0.97   
3748              0.24       0.47       0.46       0.38       0.33       0.30   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3795          WFRC_8215       0.42       0.28       0.22       0.35   
3796          WFRC_8216       0.51       0.17       0.14       0.47   
3797          WFRC_8217       0.00       0.00       0.00       0.00   
3798          WFRC_8218       1.48       0.92       0.74       1.09   
3799          WFRC_8219       0.51       0.40       0.35       0.32   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.25       0.44       0.42       0.28       0.22       0.36   
3796              0.26       0.57       0.51       0.18       0.14       0.48   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.95       1.21       1.49       0.91       0.76       1.12   
3799              0.24       0.44       0.52       0.41       0.36       0.32   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.25       0.45       0.43       0.27       0.21       0.36   
3796              0.27       0.57       0.54       0.17       0.13       0.50   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.97       1.24       1.50       0.89       0.72       1.10   
3799              0.25       0.44       0.54       0.41       0.36       0.33   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3795              0.26       0.46       0.41       0.27       0.22       0.34   
3796              0.27       0.59       0.47       0.18       0.13       0.44   
3797              0.00       0.00       0.00       0.00       0.00       0.00   
3798              0.95       1.23       1.43       0.90       0.75       1.07   
3799              0.26       0.47       0.47       0.39       0.34       0.29   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.09   
1            0006_149.9       0.31       0.29       0.27       0.21   
2            0006_150.6       0.31       0.29       0.27       0.20   
3            0006_152.6       0.34       0.32       0.30       0.21   
4            0006_152.9       0.47       0.31       0.24       0.39   
...                 ...        ...        ...        ...        ...   
3883          WFRC_8215       0.55       0.36       0.29       0.47   
3884          WFRC_8216       0.63       0.22       0.17       0.59   
3885          WFRC_8217       1.68       1.11       0.90       1.08   
3886          WFRC_8218       1.66       1.00       0.83       1.20   
3887          WFRC_8219       1.03       0.86       0.75       0.68   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.10   
1                 0.15       0.27       0.30       0.28       0.27       0.20   
2                 0.15       0.26       0.30       0.28       0.27       0.19   
3                 0.17       0.24       0.32       0.30       0.29       0.20   
4                 0.29       0.45       0.47       0.32       0.25       0.40   
...                ...        ...        ...        ...        ...        ...   
3883              0.33       0.58       0.55       0.37       0.29       0.48   
3884              0.32       0.76       0.63       0.22       0.18       0.60   
3885              1.00       1.33       1.68       1.12       0.91       1.10   
3886              1.03       1.33       1.67       1.00       0.85       1.23   
3887              0.50       1.08       1.05       0.87       0.77       0.69   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.12       0.15       0.15       0.14       0.10   
1                 0.15       0.27       0.35       0.32       0.31       0.23   
2                 0.15       0.26       0.35       0.32       0.31       0.22   
3                 0.16       0.24       0.38       0.35       0.34       0.23   
4                 0.29       0.45       0.48       0.30       0.24       0.40   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.58       0.56       0.36       0.28       0.48   
3884              0.32       0.76       0.67       0.21       0.17       0.62   
3885              1.01       1.34       1.71       1.08       0.91       1.10   
3886              1.05       1.36       1.68       0.97       0.81       1.21   
3887              0.51       1.09       1.08       0.89       0.78       0.71   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.17       0.31       0.28       0.27       0.25       0.18   
2                 0.17       0.30       0.28       0.27       0.25       0.17   
3                 0.19       0.28       0.31       0.29       0.27       0.18   
4                 0.29       0.47       0.46       0.31       0.24       0.38   
...                ...        ...        ...        ...        ...        ...   
3883              0.34       0.60       0.54       0.36       0.28       0.45   
3884              0.32       0.79       0.59       0.22       0.16       0.56   
3885              1.02       1.39       1.63       1.10       0.92       1.04   
3886              1.03       1.35       1.60       0.99       0.84       1.18   
3887              0.53       1.16       0.99       0.84       0.72       0.63   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.10       0.15       0.14       0.14       0.10   
1                 0.13       0.24       0.31       0.29       0.28

...

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.06       0.06       0.06       0.05   
2            0006_150.6       0.06       0.06       0.06       0.05   
3            0006_152.6       0.08       0.08       0.08       0.07   
4            0006_152.9       0.10       0.08       0.07       0.09   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.09       0.07       0.05       0.05   
3660          WFRC_8215       0.39       0.26       0.20       0.33   
3661          WFRC_8216       0.52       0.18       0.14       0.50   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.52       0.91       0.77       1.09   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.07       0.07       0.06       0.06       0.05   
2                 0.03       0.07       0.07       0.06       0.07       0.06   
3                 0.04       0.09       0.09       0.08       0.09       0.07   
4                 0.05       0.11       0.10       0.08       0.07       0.09   
...                ...        ...        ...        ...        ...        ...   
3659              0.06       0.10       0.09       0.07       0.05       0.05   
3660              0.23       0.42       0.39       0.26       0.21       0.34   
3661              0.27       0.66       0.52       0.18       0.15       0.51   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.95       1.32       1.54       0.93       0.78       1.11   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.07       0.06       0.06       0.06       0.06   
2                 0.03       0.07       0.07       0.07       0.06       0.06   
3                 0.04       0.09       0.09       0.09       0.08       0.08   
4                 0.05       0.11       0.11       0.08       0.07       0.09   
...                ...        ...        ...        ...        ...        ...   
3659              0.06       0.10       0.09       0.07       0.05       0.05   
3660              0.23       0.42       0.40       0.25       0.20       0.34   
3661              0.28       0.66       0.55       0.18       0.14       0.53   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.97       1.35       1.54       0.92       0.74       1.09   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.08       0.05       0.05       0.05       0.05   
2                 0.04       0.08       0.06       0.06       0.05       0.05   
3                 0.05       0.10       0.07       0.07       0.07       0.06   
4                 0.05       0.12       0.09       0.08       0.07       0.08   
...                ...        ...        ...        ...        ...        ...   
3659              0.06       0.10       0.09       0.07       0.05       0.04   
3660              0.24       0.43       0.38       0.26       0.20       0.32   
3661              0.28       0.68       0.49       0.18       0.13       0.47   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              0.95       1.34       1.47       0.93       0.78       1.07   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.03       0.06       0.06       0.06       0.06

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.08   
1            0006_149.9       0.39       0.36       0.34       0.33   
2            0006_150.6       0.39       0.37       0.35       0.33   
3            0006_152.6       0.46       0.43       0.41       0.40   
4            0006_152.9       0.59       0.39       0.31       0.62   
...                 ...        ...        ...        ...        ...   
3659          WFRC_8213       0.12       0.09       0.06       0.06   
3660          WFRC_8215       0.48       0.32       0.25       0.40   
3661          WFRC_8216       0.63       0.21       0.17       0.61   
3662          WFRC_8217       0.00       0.00       0.00       0.00   
3663          WFRC_8218       1.65       0.99       0.83       1.19   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.09   
1                 0.18       0.39       0.37       0.35       0.33       0.33   
2                 0.19       0.39       0.37       0.35       0.34       0.33   
3                 0.22       0.45       0.44       0.41       0.40       0.39   
4                 0.35       0.72       0.59       0.40       0.31       0.64   
...                ...        ...        ...        ...        ...        ...   
3659              0.08       0.15       0.12       0.09       0.07       0.07   
3660              0.28       0.52       0.48       0.32       0.25       0.41   
3661              0.33       0.79       0.63       0.22       0.18       0.62   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.03       1.33       1.67       0.99       0.85       1.21   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.11       0.15       0.15       0.14       0.09   
1                 0.18       0.38       0.43       0.40       0.38       0.38   
2                 0.18       0.38       0.44       0.41       0.39       0.38   
3                 0.21       0.44       0.52       0.48       0.45       0.45   
4                 0.35       0.72       0.60       0.38       0.30       0.64   
...                ...        ...        ...        ...        ...        ...   
3659              0.08       0.15       0.12       0.09       0.06       0.06   
3660              0.29       0.52       0.49       0.31       0.25       0.41   
3661              0.34       0.80       0.67       0.21       0.17       0.64   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.04       1.36       1.67       0.97       0.81       1.19   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.21       0.45       0.35       0.33       0.31       0.29   
2                 0.22       0.45       0.35       0.34       0.31       0.30   
3                 0.25       0.52       0.41       0.39       0.37       0.35   
4                 0.36       0.75       0.57       0.39       0.30       0.60   
...                ...        ...        ...        ...        ...        ...   
3659              0.08       0.15       0.12       0.09       0.07       0.06   
3660              0.29       0.54       0.47       0.31       0.25       0.39   
3661              0.34       0.83       0.59       0.22       0.16       0.57   
3662              0.00       0.00       0.00       0.00       0.00       0.00   
3663              1.03       1.35       1.60       0.99       0.84       1.16   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.09       0.15       0.14       0.14       0.09   
1                 0.16       0.34       0.39       0.36       0.35

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3746          WFRC_8215       0.27       0.18       0.14       0.21   
3747          WFRC_8216       0.39       0.13       0.10       0.37   
3748          WFRC_8217       0.00       0.00       0.00       0.00   
3749          WFRC_8218       1.32       0.82       0.66       0.98   
3750          WFRC_8219       0.47       0.38       0.33       0.30   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.16       0.27       0.27       0.18       0.14       0.21   
3747              0.19       0.47       0.39       0.14       0.11       0.37   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.84       1.18       1.33       0.84       0.68       0.98   
3750              0.23       0.41       0.48       0.38       0.34       0.30   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.17       0.27       0.28       0.17       0.14       0.21   
3747              0.19       0.47       0.41       0.13       0.10       0.39   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.86       1.21       1.33       0.80       0.64       0.99   
3750              0.23       0.42       0.51       0.39       0.34       0.31   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3746              0.17       0.29       0.26       0.18       0.14       0.20   
3747              0.20       0.49       0.36       0.13       0.10       0.35   
3748              0.00       0.00       0.00       0.00       0.00       0.00   
3749              0.84       1.20       1.27       0.83       0.67       0.96   
3750              0.24       0.45       0.44       0.36       0.31       0.28   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3798          WFRC_8215       0.41       0.27       0.21       0.33   
3799          WFRC_8216       0.56       0.19       0.15       0.52   
3800          WFRC_8217       0.00       0.00       0.00       0.00   
3801          WFRC_8218       1.50       0.90       0.75       1.09   
3802          WFRC_8219       0.50       0.40       0.35       0.31   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.25       0.42       0.41       0.27       0.22       0.34   
3799              0.28       0.67       0.57       0.20       0.16       0.52   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.95       1.31       1.51       0.92       0.77       1.12   
3802              0.24       0.44       0.52       0.40       0.36       0.31   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.25       0.42       0.42       0.26       0.21       0.33   
3799              0.28       0.67       0.60       0.19       0.15       0.54   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.96       1.34       1.52       0.91       0.73       1.10   
3802              0.25       0.44       0.54       0.41       0.36       0.32   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3798              0.25       0.44       0.40       0.27       0.21       0.32   
3799              0.28       0.70       0.52       0.19       0.15       0.48   
3800              0.00       0.00       0.00       0.00       0.00       0.00   
3801              0.94       1.33       1.45       0.92       0.76       1.07   
3802              0.26       0.47       0.47       0.39       0.34       0.28   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.14       0.14       0.13       0.09   
1            0006_149.9       0.31       0.29       0.27       0.21   
2            0006_150.6       0.31       0.29       0.27       0.20   
3            0006_152.6       0.34       0.32       0.30       0.20   
4            0006_152.9       0.47       0.31       0.24       0.39   
...                 ...        ...        ...        ...        ...   
3886          WFRC_8215       0.53       0.35       0.27       0.43   
3887          WFRC_8216       0.63       0.22       0.17       0.55   
3888          WFRC_8217       1.64       1.08       0.91       1.07   
3889          WFRC_8218       1.66       1.00       0.83       1.20   
3890          WFRC_8219       1.06       0.89       0.78       0.71   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.07       0.11       0.16       0.14       0.15       0.10   
1                 0.15       0.27       0.30       0.28       0.27       0.21   
2                 0.15       0.26       0.30       0.28       0.27       0.20   
3                 0.17       0.24       0.32       0.30       0.29       0.20   
4                 0.29       0.45       0.47       0.32       0.25       0.39   
...                ...        ...        ...        ...        ...        ...   
3886              0.32       0.54       0.53       0.35       0.28       0.44   
3887              0.32       0.73       0.63       0.22       0.18       0.55   
3888              1.00       1.34       1.65       1.10       0.92       1.09   
3889              1.03       1.32       1.67       1.00       0.85       1.23   
3890              0.54       1.03       1.07       0.90       0.80       0.73   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.07       0.12       0.15       0.15       0.14       0.10   
1                 0.15       0.26       0.35       0.32       0.31       0.24   
2                 0.15       0.26       0.35       0.32       0.31       0.23   
3                 0.16       0.24       0.38       0.35       0.33       0.23   
4                 0.29       0.45       0.48       0.30       0.24       0.39   
...                ...        ...        ...        ...        ...        ...   
3886              0.32       0.55       0.54       0.34       0.27       0.44   
3887              0.32       0.74       0.67       0.21       0.17       0.57   
3888              1.01       1.34       1.67       1.06       0.89       1.09   
3889              1.05       1.35       1.68       0.97       0.81       1.21   
3890              0.54       1.04       1.12       0.92       0.80       0.75   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.08       0.12       0.13       0.13       0.12       0.08   
1                 0.17       0.31       0.28       0.27       0.25       0.19   
2                 0.17       0.30       0.28       0.27       0.25       0.18   
3                 0.19       0.28       0.31       0.29       0.27       0.18   
4                 0.29       0.47       0.46       0.31       0.24       0.37   
...                ...        ...        ...        ...        ...        ...   
3886              0.33       0.57       0.51       0.35       0.27       0.41   
3887              0.33       0.76       0.59       0.22       0.16       0.51   
3888              1.02       1.40       1.59       1.07       0.90       1.03   
3889              1.03       1.34       1.60       0.99       0.84       1.18   
3890              0.57       1.09       1.02       0.86       0.75       0.66   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.06       0.10       0.15       0.14       0.14       0.10   
1                 0.13       0.24       0.31       0.29       0.28

# Export final tables to CSV

In [80]:
if export_results: 
    df_Scenarios.to_csv(os.path.join(dirResults, r'scenarios.csv'),index=False)
    df_VCGroup_DOWPkHr.to_csv(os.path.join(dirResults, r'vcgroups_dowpeak.csv'),index=False)
    df_VCGroup_Seasons.to_csv(os.path.join(dirResults, r'vcgroups_seasons.csv'),index=False)
    df_VCGroups.to_csv(os.path.join(dirResults, r'vcgroups.csv'),index=False)

In [81]:
if export_results: 

    df_Scenarios_toExport = df_Scenarios.reset_index()
    
    for index, df_VC_MaxDirFG_wVCGroups in enumerate(dfs_VC_MaxDirFG_wVCGroups):    

        filename = os.path.join(dirResults,"3_VC_MaxDirFG_wVCGroups_" + df_Scenarios_toExport['ScenarioCode'].iloc[index] + '.csv')
        display('Exporting ' + filename)
        df_VC_MaxDirFG_wVCGroups.to_csv(filename, index=False)

    for index, df_VC_MaxDirFG in enumerate(dfs_VC_MaxDirFG):    

        filename = os.path.join(dirResults,"2_VC_MaxDirFG_" + df_Scenarios_toExport['ScenarioCode'].iloc[index] + '.csv')
        display('Exporting ' + filename)
        df_VC_MaxDirFG.to_csv(filename, index=False)

    for index, df_VC in enumerate(dfs_VC):    

        filename = os.path.join(dirResults,"1_VC_" + df_Scenarios_toExport['ScenarioCode'].iloc[index] + '.csv')
        display('Exporting ' + filename)
        df_VC.to_csv(filename, index=False)

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_Base19.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_TIP24.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_RTP30.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_RTP40.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\3_VC_MaxDirFG_wVCGroups_RTP50.csv'

...

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_NB40.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_NB50.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_UF30.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_UF40.csv'

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\1_VC_UF50.csv'

In [82]:
df = dfs_VC_MaxDirFG_wVCGroups[0]
df[df['SEGID']=='0079_003.0']
df

VCGroupCode       SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  \
0            0006_146.9       0.00       0.00       0.00       0.00   
1            0006_149.9       0.00       0.00       0.00       0.00   
2            0006_150.6       0.00       0.00       0.00       0.00   
3            0006_152.6       0.00       0.00       0.00       0.00   
4            0006_152.9       0.00       0.00       0.00       0.00   
...                 ...        ...        ...        ...        ...   
3613          WFRC_8208       0.00       0.00       0.00       0.00   
3614          WFRC_8209       0.04       0.03       0.02       0.03   
3615          WFRC_8213       0.06       0.05       0.03       0.03   
3616          WFRC_8215       0.18       0.12       0.09       0.13   
3617          WFRC_8218       1.12       0.70       0.56       0.82   

VCGroupCode  AnnWkMD15  AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.05       0.07       0.05       0.03       0.03   
3616              0.11       0.17       0.18       0.12       0.09       0.13   
3617              0.71       1.03       1.13       0.71       0.58       0.84   

VCGroupCode  AprWkMD15  AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.06       0.06       0.05       0.03       0.03   
3616              0.11       0.17       0.18       0.12       0.09       0.13   
3617              0.72       1.05       1.13       0.68       0.55       0.83   

VCGroupCode  AugWkMD15  AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00       0.00   
2                 0.00       0.00       0.00       0.00       0.00       0.00   
3                 0.00       0.00       0.00       0.00       0.00       0.00   
4                 0.00       0.00       0.00       0.00       0.00       0.00   
...                ...        ...        ...        ...        ...        ...   
3613              0.00       0.00       0.00       0.00       0.00       0.00   
3614              0.03       0.04       0.04       0.03       0.02       0.03   
3615              0.04       0.06       0.06       0.05       0.03       0.03   
3616              0.11       0.18       0.17       0.12       0.09       0.12   
3617              0.71       1.04       1.08       0.71       0.57       0.81   

VCGroupCode  DecWkMD15  DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  \
0                 0.00       0.00       0.00       0.00       0.00       0.00   
1                 0.00       0.00       0.00       0.00       0.00

In [83]:
df_Scenarios_toProcess

Process ScenarioCode ScenarioGroup   ScenarioName  ScenarioYear  \
ScenarioID                                                                   
0              Yes       Base19          Base      2019 Base          2019   
1              Yes        TIP24           TIP       2024 TIP          2024   
2              Yes        RTP30           RTP       2030 RTP          2030   
3              Yes        RTP40           RTP       2040 RTP          2040   
4              Yes        RTP50           RTP       2050 RTP          2050   
5              Yes         NB30      No Build  2030 No Build          2030   
6              Yes         NB40      No Build  2040 No Build          2040   
7              Yes         NB50      No Build  2050 No Build          2050   
8              Yes         UF30         Needs     2030 Needs          2030   
9              Yes         UF40         Needs     2040 Needs          2040   
10             Yes         UF50         Needs     2050 Needs          2050   

                                           SegSummaryCSV PrvScenarioCode  \
ScenarioID                                                                 
0             v831_SE19_Net19_Summary_SEGID_Detailed.csv             NaN   
1             v831_SE24_Net24_Summary_SEGID_Detailed.csv          Base19   
2             v831_SE30_Net30_Summary_SEGID_Detailed.csv           TIP24   
3             v831_SE40_Net40_Summary_SEGID_Detailed.csv           RTP30   
4             v831_SE50_Net50_Summary_SEGID_Detailed.csv           RTP40   
5             v831_SE30_Net24_Summary_SEGID_Detailed.csv           TIP24   
6             v831_SE40_Net24_Summary_SEGID_Detailed.csv            NB30   
7             v831_SE50_Net24_Summary_SEGID_Detailed.csv            NB40   
8           v831_SE30_Net30UF_Summary_SEGID_Detailed.csv           TIP24   
9           v831_SE40_Net40UF_Summary_SEGID_Detailed.csv            UF30   
10          v831_SE50_Net50UF_Summary_SEGID_Detailed.csv            UF40   

           AdjScenarioCode  
ScenarioID                  
0                      NaN  
1                      NaN  
2                      NaN  
3                      NaN  
4                      NaN  
5                    RTP30  
6                    RTP40  
7                    RTP50  
8                    RTP30  
9                    RTP40  
10                   RTP50

# Exports for WebApp

In [84]:
if export_results:
    
    df_Scenarios_json = df_Scenarios.copy()
    df_Scenarios_json = df_Scenarios_json[['ScenarioCode','ScenarioName']]
    df_Scenarios_json.columns = ('value','label')
    df_Scenarios_json['filename'] = "VC_" + df_Scenarios_json['value'] + '.json'
    
    df_VCGroup_Seasons_json = df_VCGroup_Seasons.copy()
    df_VCGroup_Seasons_json = df_VCGroup_Seasons_json[['SeasonCode','SeasonName','SeasonType']]
    df_VCGroup_Seasons_json.columns = ('value','label','SeasonType')
        
    df_VCGroup_DOWPkHr_json = df_VCGroup_DOWPkHr.copy()
    df_VCGroup_DOWPkHr_json = df_VCGroup_DOWPkHr_json[['DOWPkCode','DOWPkName']]
    df_VCGroup_DOWPkHr_json.columns = ('value','label')

    df_Scenarios_json.to_json(os.path.join(dirResults, r'WebAppData\scenarios.json'),orient='records')
    #df_Scenarios_json = df_Scenarios_json.reset_index()
    #df_Scenarios_json.to_json(os.path.join(dirResults, r'WebAppData\scenarios_test.json'))
    df_VCGroup_Seasons_json.to_json(os.path.join(dirResults, r'WebAppData\vcgroups_seasons.json'),orient='records')
    df_VCGroup_DOWPkHr_json.to_json(os.path.join(dirResults, r'WebAppData\vcgroups_dowpeaks.json'),orient='records')
    

In [85]:
df_Scenarios_json

value          label        filename
ScenarioID                                       
0           Base19      2019 Base  VC_Base19.json
1            TIP24       2024 TIP   VC_TIP24.json
2            RTP30       2030 RTP   VC_RTP30.json
3            RTP40       2040 RTP   VC_RTP40.json
4            RTP50       2050 RTP   VC_RTP50.json
5             NB30  2030 No Build    VC_NB30.json
6             NB40  2040 No Build    VC_NB40.json
7             NB50  2050 No Build    VC_NB50.json
8             UF30     2030 Needs    VC_UF30.json
9             UF40     2040 Needs    VC_UF40.json
10            UF50     2050 Needs    VC_UF50.json

In [87]:
if export_results:
    
    df_Scenarios_toExport = df_Scenarios_toProcess.reset_index()
    
    for index, df_VC_MaxDirFG_wVCGroups in enumerate(dfs_VC_MaxDirFG_wVCGroups):    

        filename = "WebAppData\VC_" + df_Scenarios_toExport['ScenarioCode'].iloc[index] + '.json'
        #display(filename)

        #df_Peak_VC_MaxDirFG_wVCGroups = df_Peak_VC_MaxDirFG_wVCGroups.rename(columns={"SEGID": 'S'})

        #export to csv in data-processed
        df_VC_MaxDirFG_wVCGroups.to_json(os.path.join(dirResults, filename),orient='records')

        display('Done exporting ' + filename)

'Done exporting WebAppData\\VC_Base19.json'

'Done exporting WebAppData\\VC_TIP24.json'

'Done exporting WebAppData\\VC_RTP30.json'

'Done exporting WebAppData\\VC_RTP40.json'

'Done exporting WebAppData\\VC_RTP50.json'

...

'Done exporting WebAppData\\VC_NB40.json'

'Done exporting WebAppData\\VC_NB50.json'

'Done exporting WebAppData\\VC_UF30.json'

'Done exporting WebAppData\\VC_UF40.json'

'Done exporting WebAppData\\VC_UF50.json'

# Temp

In [88]:
dfs_VC_MaxDirFG_wVCGroups =[]
df_TDMsf = []

display ('Scenario Codes:')

for (idx, row) in df_Scenarios.iterrows():    

    print(row.loc['ScenarioCode'])
    
    df_TDM = dfs_TDM[idx]
    df_TDMsf = df_TDM[['SEGID','FT']]
    
    df_TDMsfmax = df_TDMsf.groupby('SEGID', as_index=False).agg({'FT':[np.max]})
    df_TDMsfmax.columns = ['SEGID','FT']
    #df_TDMsf.append(df_TDMsf)
    
    df_VC_MaxDirFG_wVCGroups = pd.read_csv(os.path.join(dirResults, '3_VC_MaxDirFG_wVCGroups_' + row.loc['ScenarioCode'] + '.csv'))
    display(df_VC_MaxDirFG_wVCGroups)
    
    df_new = pd.DataFrame.merge(df_TDMsfmax,df_VC_MaxDirFG_wVCGroups,on=('SEGID'))
    display(df_new)
    
    filename = os.path.join(dirResults,r"temp\3_VC_MaxDirFG_wVCGroups_" + row.loc['ScenarioCode'] + '.csv')
    display('Exporting ' + filename)
    df_new.to_csv(filename,index=False)
    #dfs_VC_MaxDirFG_wVCGroups.append(dfs_Peak_VC_MaxDirFG_wVCGroups)


'Scenario Codes:'

Base19


SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9       0.00       0.00       0.00       0.00       0.00   
1     0006_149.9       0.00       0.00       0.00       0.00       0.00   
2     0006_150.6       0.00       0.00       0.00       0.00       0.00   
3     0006_152.6       0.00       0.00       0.00       0.00       0.00   
4     0006_152.9       0.00       0.00       0.00       0.00       0.00   
...          ...        ...        ...        ...        ...        ...   
3613   WFRC_8208       0.00       0.00       0.00       0.00       0.00   
3614   WFRC_8209       0.04       0.03       0.02       0.03       0.03   
3615   WFRC_8213       0.06       0.05       0.03       0.03       0.04   
3616   WFRC_8215       0.18       0.12       0.09       0.13       0.11   
3617   WFRC_8218       1.12       0.70       0.56       0.82       0.71   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   
...         ...        ...        ...        ...        ...        ...   
3613       0.00       0.00       0.00       0.00       0.00       0.00   
3614       0.04       0.04       0.03       0.02       0.03       0.03   
3615       0.05       0.07       0.05       0.03       0.03       0.04   
3616       0.17       0.18       0.12       0.09       0.13       0.11   
3617       1.03       1.13       0.71       0.58       0.84       0.72   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   
...         ...        ...        ...        ...        ...        ...   
3613       0.00       0.00       0.00       0.00       0.00       0.00   
3614       0.04       0.04       0.03       0.02       0.03       0.03   
3615       0.06       0.06       0.05       0.03       0.03       0.04   
3616       0.17       0.18       0.12       0.09       0.13       0.11   
3617       1.05       1.13       0.68       0.55       0.83       0.71   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   
...         ...        ...        ...        ...        ...        ...   
3613       0.00       0.00       0.00       0.00       0.00       0.00   
3614       0.04       0.04       0.03       0.02       0.03       0.03   
3615       0.06       0.06       0.05       0.03       0.03       0.04   
3616       0.18       0.17       0.12       0.09       0.12       0.10   
3617       1.04       1.08       0.71       0.57       0.81       0.70   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   

SEGID    FT  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9   2.0       0.00       0.00       0.00       0.00       0.00   
1     0006_149.9   2.0       0.00       0.00       0.00       0.00       0.00   
2     0006_150.6   2.0       0.00       0.00       0.00       0.00       0.00   
3     0006_152.6   3.0       0.00       0.00       0.00       0.00       0.00   
4     0006_152.9   2.0       0.00       0.00       0.00       0.00       0.00   
...          ...   ...        ...        ...        ...        ...        ...   
3613   WFRC_8208   5.0       0.00       0.00       0.00       0.00       0.00   
3614   WFRC_8209   4.0       0.04       0.03       0.02       0.03       0.03   
3615   WFRC_8213   5.0       0.06       0.05       0.03       0.03       0.04   
3616   WFRC_8215   4.0       0.18       0.12       0.09       0.13       0.11   
3617   WFRC_8218  31.0       1.12       0.70       0.56       0.82       0.71   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   
...         ...        ...        ...        ...        ...        ...   
3613       0.00       0.00       0.00       0.00       0.00       0.00   
3614       0.04       0.04       0.03       0.02       0.03       0.03   
3615       0.05       0.07       0.05       0.03       0.03       0.04   
3616       0.17       0.18       0.12       0.09       0.13       0.11   
3617       1.03       1.13       0.71       0.58       0.84       0.72   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   
...         ...        ...        ...        ...        ...        ...   
3613       0.00       0.00       0.00       0.00       0.00       0.00   
3614       0.04       0.04       0.03       0.02       0.03       0.03   
3615       0.06       0.06       0.05       0.03       0.03       0.04   
3616       0.17       0.18       0.12       0.09       0.13       0.11   
3617       1.05       1.13       0.68       0.55       0.83       0.71   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4          0.00       0.00       0.00       0.00       0.00       0.00   
...         ...        ...        ...        ...        ...        ...   
3613       0.00       0.00       0.00       0.00       0.00       0.00   
3614       0.04       0.04       0.03       0.02       0.03       0.03   
3615       0.06       0.06       0.05       0.03       0.03       0.04   
3616       0.18       0.17       0.12       0.09       0.12       0.10   
3617       1.04       1.08       0.71       0.57       0.81       0.70   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.00       0.00       0.00       0.00       0.00       0.00   
1          0.00       0.00       0.00       0.00       0.00       0.00   
2          0.00       0.00       0.00       0.00       0.00       0.00   
3          0.00       0.00       0.00       0.00       0.00       0.00   
4

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\temp\\3_VC_MaxDirFG_wVCGroups_Base19.csv'

...

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\temp\\3_VC_MaxDirFG_wVCGroups_UF40.csv'

UF50


SEGID  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9       0.14       0.14       0.13       0.09       0.07   
1     0006_149.9       0.31       0.29       0.27       0.21       0.15   
2     0006_150.6       0.31       0.29       0.27       0.20       0.15   
3     0006_152.6       0.34       0.32       0.30       0.20       0.17   
4     0006_152.9       0.47       0.31       0.24       0.39       0.29   
...          ...        ...        ...        ...        ...        ...   
3886   WFRC_8215       0.53       0.35       0.27       0.43       0.32   
3887   WFRC_8216       0.63       0.22       0.17       0.55       0.32   
3888   WFRC_8217       1.64       1.08       0.91       1.07       1.00   
3889   WFRC_8218       1.66       1.00       0.83       1.20       1.03   
3890   WFRC_8219       1.06       0.89       0.78       0.71       0.54   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.11       0.16       0.14       0.15       0.10       0.07   
1          0.27       0.30       0.28       0.27       0.21       0.15   
2          0.26       0.30       0.28       0.27       0.20       0.15   
3          0.24       0.32       0.30       0.29       0.20       0.16   
4          0.45       0.47       0.32       0.25       0.39       0.29   
...         ...        ...        ...        ...        ...        ...   
3886       0.54       0.53       0.35       0.28       0.44       0.32   
3887       0.73       0.63       0.22       0.18       0.55       0.32   
3888       1.34       1.65       1.10       0.92       1.09       1.01   
3889       1.32       1.67       1.00       0.85       1.23       1.05   
3890       1.03       1.07       0.90       0.80       0.73       0.54   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.12       0.15       0.15       0.14       0.10       0.08   
1          0.26       0.35       0.32       0.31       0.24       0.17   
2          0.26       0.35       0.32       0.31       0.23       0.17   
3          0.24       0.38       0.35       0.33       0.23       0.19   
4          0.45       0.48       0.30       0.24       0.39       0.29   
...         ...        ...        ...        ...        ...        ...   
3886       0.55       0.54       0.34       0.27       0.44       0.33   
3887       0.74       0.67       0.21       0.17       0.57       0.33   
3888       1.34       1.67       1.06       0.89       1.09       1.02   
3889       1.35       1.68       0.97       0.81       1.21       1.03   
3890       1.04       1.12       0.92       0.80       0.75       0.57   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.12       0.13       0.13       0.12       0.08       0.06   
1          0.31       0.28       0.27       0.25       0.19       0.13   
2          0.30       0.28       0.27       0.25       0.18       0.13   
3          0.28       0.31       0.29       0.27       0.18       0.15   
4          0.47       0.46       0.31       0.24       0.37       0.28   
...         ...        ...        ...        ...        ...        ...   
3886       0.57       0.51       0.35       0.27       0.41       0.31   
3887       0.76       0.59       0.22       0.16       0.51       0.31   
3888       1.40       1.59       1.07       0.90       1.03       1.00   
3889       1.34       1.60       0.99       0.84       1.18       1.02   
3890       1.09       1.02       0.86       0.75       0.66       0.50   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.10       0.15       0.14       0.14       0.10       0.07   
1          0.24       0.31       0.29       0.28       0.21       0.15   
2          0.23       0.31       0.29       0.28       0.20       0.15   
3          0.21       0.34       0.32       0.30       0.20       0.17   
4          0.43       0.48       0.32       0.25       0.40       0.30   

SEGID    FT  AnnFrPM15  AnnSaDY15  AnnSuDY15  AnnWkAM15  AnnWkMD15  \
0     0006_146.9   2.0       0.14       0.14       0.13       0.09       0.07   
1     0006_149.9   2.0       0.31       0.29       0.27       0.21       0.15   
2     0006_150.6   2.0       0.31       0.29       0.27       0.20       0.15   
3     0006_152.6   3.0       0.34       0.32       0.30       0.20       0.17   
4     0006_152.9   2.0       0.47       0.31       0.24       0.39       0.29   
...          ...   ...        ...        ...        ...        ...        ...   
3886   WFRC_8215   4.0       0.53       0.35       0.27       0.43       0.32   
3887   WFRC_8216  33.0       0.63       0.22       0.17       0.55       0.32   
3888   WFRC_8217   4.0       1.64       1.08       0.91       1.07       1.00   
3889   WFRC_8218  31.0       1.66       1.00       0.83       1.20       1.03   
3890   WFRC_8219   3.0       1.06       0.89       0.78       0.71       0.54   

      AnnWkPM15  AprFrPM15  AprSaDY15  AprSuDY15  AprWkAM15  AprWkMD15  \
0          0.11       0.16       0.14       0.15       0.10       0.07   
1          0.27       0.30       0.28       0.27       0.21       0.15   
2          0.26       0.30       0.28       0.27       0.20       0.15   
3          0.24       0.32       0.30       0.29       0.20       0.16   
4          0.45       0.47       0.32       0.25       0.39       0.29   
...         ...        ...        ...        ...        ...        ...   
3886       0.54       0.53       0.35       0.28       0.44       0.32   
3887       0.73       0.63       0.22       0.18       0.55       0.32   
3888       1.34       1.65       1.10       0.92       1.09       1.01   
3889       1.32       1.67       1.00       0.85       1.23       1.05   
3890       1.03       1.07       0.90       0.80       0.73       0.54   

      AprWkPM15  AugFrPM15  AugSaDY15  AugSuDY15  AugWkAM15  AugWkMD15  \
0          0.12       0.15       0.15       0.14       0.10       0.08   
1          0.26       0.35       0.32       0.31       0.24       0.17   
2          0.26       0.35       0.32       0.31       0.23       0.17   
3          0.24       0.38       0.35       0.33       0.23       0.19   
4          0.45       0.48       0.30       0.24       0.39       0.29   
...         ...        ...        ...        ...        ...        ...   
3886       0.55       0.54       0.34       0.27       0.44       0.33   
3887       0.74       0.67       0.21       0.17       0.57       0.33   
3888       1.34       1.67       1.06       0.89       1.09       1.02   
3889       1.35       1.68       0.97       0.81       1.21       1.03   
3890       1.04       1.12       0.92       0.80       0.75       0.57   

      AugWkPM15  DecFrPM15  DecSaDY15  DecSuDY15  DecWkAM15  DecWkMD15  \
0          0.12       0.13       0.13       0.12       0.08       0.06   
1          0.31       0.28       0.27       0.25       0.19       0.13   
2          0.30       0.28       0.27       0.25       0.18       0.13   
3          0.28       0.31       0.29       0.27       0.18       0.15   
4          0.47       0.46       0.31       0.24       0.37       0.28   
...         ...        ...        ...        ...        ...        ...   
3886       0.57       0.51       0.35       0.27       0.41       0.31   
3887       0.76       0.59       0.22       0.16       0.51       0.31   
3888       1.40       1.59       1.07       0.90       1.03       1.00   
3889       1.34       1.60       0.99       0.84       1.18       1.02   
3890       1.09       1.02       0.86       0.75       0.66       0.50   

      DecWkPM15  FalFrPM15  FalSaDY15  FalSuDY15  FalWkAM15  FalWkMD15  \
0          0.10       0.15       0.14       0.14       0.10       0.07   
1          0.24       0.31       0.29       0.28       0.21       0.15   
2          0.23       0.31       0.29       0.28       0.20       0.15   
3          0.21       0.34       0.32       0.30       0.20       0.17   
4

'Exporting E:\\GitHub\\V-over-C-Calculations\\results\\temp\\3_VC_MaxDirFG_wVCGroups_UF50.csv'

In [89]:
df_TDMsfmax = df_TDMsf.groupby('SEGID', as_index=False).agg({'FT':[np.max]})
df_TDMsfmax.columns = ['SEGID','FT']
df_TDMsfmax

SEGID    FT
0     0006_146.9   2.0
1     0006_149.9   2.0
2     0006_150.6   2.0
3     0006_152.6   3.0
4     0006_152.9   2.0
...          ...   ...
3925   WFRC_8215   4.0
3926   WFRC_8216  33.0
3927   WFRC_8217   4.0
3928   WFRC_8218  31.0
3929   WFRC_8219   3.0

[3930 rows x 2 columns]

In [90]:
df_VCGroup_Seasons

SeasonCode SeasonGroup SeasonName SeasonType
0         Ann     S00-Ann     Annual     Season
1         Win     S01-Win     Winter     Season
2         Spr     S02-Spr     Spring     Season
3         Sum     S03-Sum     Summer     Season
4         Fal     S04-Fal       Fall     Season
5         Jan     M01-Jan    January      Month
6         Feb     M02-Feb   February      Month
7         Mar     M03-Mar      March      Month
8         Apr     M04-Apr      April      Month
9         May     M05-May        May      Month
10        Jun     M06-Jun       June      Month
11        Jul     M07-Jul       July      Month
12        Aug     M08-Aug     August      Month
13        Sep     M09-Sep  September      Month
14        Oct     M10-Oct    October      Month
15        Nov     M11-Nov   November      Month
16        Dec     M12-Dec   December      Month

In [91]:
df_TDMsfmax

SEGID    FT
0     0006_146.9   2.0
1     0006_149.9   2.0
2     0006_150.6   2.0
3     0006_152.6   3.0
4     0006_152.9   2.0
...          ...   ...
3925   WFRC_8215   4.0
3926   WFRC_8216  33.0
3927   WFRC_8217   4.0
3928   WFRC_8218  31.0
3929   WFRC_8219   3.0

[3930 rows x 2 columns]